In [1]:
#codice che mi serve per accedere ai file di drive
#from google.colab import drive
#drive.mount('/content/drive')

In [2]:
#Il modulo re in Python serve per lavorare con le espressioni regolari (regular expressions).
# Le espressioni regolari sono una potente tecnica per cercare,
#estrarre e manipolare pattern (schemi) all'interno di stringhe di testo.
#Ecco alcune delle principali funzionalità del modulo re:
#Ricerca di pattern: Puoi usare re per cercare pattern specifici in una stringa.
#Ad esempio, puoi cercare tutte le occorrenze di un numero o di una certa parola in un testo.
import re

In [3]:
import pandas as pd
import numpy as np

In [4]:
import os

In [5]:
def sum_dicts(dict_list):
    # Initialize an empty dictionary to store the summed values
    summed_dict = {}

    # Iterate through each dictionary in the list
    for d in dict_list:
        for key, value in d.items():
            # If the key is already in the summed_dict, add the value, otherwise initialize it
            if key in summed_dict:
                summed_dict[key] += value
            else:
                summed_dict[key] = value

    return summed_dict

In [6]:
os.listdir("C:/Users/lcolo/Desktop/TESI/CODICI DEFINITIVI DIZ UNICO-2/PEDALION/output_pedalion_con_relation" )

['aeneas.xml',
 'aesop1.xml',
 'charb1.xml',
 'chion.xml',
 'crit.xml',
 'epictetus.xml',
 'epicurus1.xml',
 'genesis1.xml',
 'genesis2.xml',
 'genesis3.xml',
 'heron.xml',
 'iso.xml',
 'julian.xml',
 'longus.xml',
 'lucian_lis.xml',
 'lucian_prometheus.xml',
 'lucian_symposion.xml',
 'lysias_or24.xml',
 'paean.xml',
 'papyri.xml',
 'phlegon.xml',
 'procopius.xml',
 'pseudo-lucian_themule.xml',
 'pseudoplato_cleitophon.xml',
 'sextus.xml',
 'theophr.xml',
 'xenmem.xml']

In [7]:
# Lista per salvare tutti i percorsi dei file CSV
csv_file_paths = []

# Directory principale che contiene le sottodirectory
main_directory = "C:/Users/lcolo/Desktop/TESI/CODICI DEFINITIVI DIZ UNICO-2/PEDALION/output_pedalion_con_relation"

#per ogni cartella in output gorman devo ottenere la directory completa della singola cartella dell'autore. per farlo itero col ciclo for su tutte le cartelle presenti in gorman e concateno,
#per ottenere la directory della cartella della singola opera, la main directory col nome della cratella.
#per farlo uso la funzione di os che si chiama os.path join che fa una concatenazione di stringhe.
for folder in os.listdir(main_directory):
  folder_path = os.path.join(main_directory, folder)
  #ora voglio per ogni cartella una lista vuota poi da andare a riempire con i csv di ogni singola cartella.
  singola_cartella = []
  for file in os.listdir(folder_path): #per ogni file che sta nella mia cartella
    if file.endswith('.csv'): #controllo per vedere se sono davvero tutti csv i file.
      file_path = os.path.join(folder_path, file) #se il file è un csv la sua directory completa me la metti nella lista.
      singola_cartella.append(file_path)

  csv_file_paths.append(singola_cartella)

In [8]:
len(csv_file_paths)

27

In [9]:
# Lista per conservare i DataFrame filtrati
#per ogni lista creo una lista di di dataframe. questi sono i csv filtrati con le info che mi servono.
#ora lo trasformo in una funzione che prenda in input una lista di csv.
def filter_dataframe(csv_file_paths):
  dataframes_tot = [] #è una lista vuota in cui mettere i dataframe filtrati.
# Leggi, filtra e aggiungi ogni DataFrame alla lista
  for file_path in csv_file_paths:
    # Leggi il CSV in un DataFrame
      df = pd.read_csv(file_path)

    # Filtra il DataFrame mantenendo solo le righe dove '@lemma' è una stringa
      df_filtered = df[df['@lemma'].apply(lambda x: isinstance(x, str))]

    # Aggiungi il DataFrame filtrato alla lista
      dataframes_tot.append(df_filtered)

# Visualizza le prime righe di ciascun DataFrame per controllare la struttura
      data_info = {f"File {i+1}": df.head() for i, df in enumerate(dataframes_tot)}

# Mostra la struttura dei dati
      #for file_name, df_head in data_info.items():
       # print(f"\n{file_name}:")
        #print(df_head)
  return dataframes_tot

In [10]:
# Function to check and display anomalies in the postag
def check_postag_anomalies(df):
    valid_characters = {
        0: "nvadlgpcrmiu-",  # Part of speech
        1: "123-",         # Person
        2: "spd-",         # Number
        3: "pirltfa-",     # Tense
        4: "isomnp-",      # Mood
        5: "apme-",        # Voice
        6: "mfn-",         # Gender
        7: "ngdav-",       # Case
        8: "cs-"           # Grade
    }

    anomalies = []
    
    for index, row in df.iterrows():
        postag = row['@postag']
        if type(postag) != str: #perchè ci sono alcuni che hanno float e non stringa
            anomalies.append((row['@form'], postag, "attenzione no stringa"))
        else:
            if len(postag) != 9:  # Check if postag length is not 9
                anomalies.append((row['@form'], postag, "Incorrect length"))
            else:
            
                for i, char in enumerate(postag):
                    if char not in valid_characters[i]:
                        anomalies.append((row['@form'], postag, f"Unexpected character '{char}' at position {i+1}"))

    return anomalies


In [11]:
# Function to extract the numeric part from the filename, mi serve per oprdinare i file csv da 1 etc in ordine numerico, questa 
#è la funzione che va per tutti
def extract_number(file_path):
    # Use regex to find the numeric part of the filename
    return int(re.search(r'(\d+)\.csv$', file_path).group(1))



In [12]:
#sorted(csv_file_paths[0], key=extract_number) #questo è l'es. per vedere sul singolo file che la funzione vada

In [13]:
all_sorted_csv_filepaths = [] #ho creato una lista di cartelle ordinate in base al numero 
for folder in csv_file_paths:
  sorted_files = sorted(folder, key=extract_number)
  all_sorted_csv_filepaths.append(sorted_files)

In [14]:
#apply filter dataframe, questa funzione serviva per prendere solo di ogni tabella lemma e postag, applicato a tutti i file, 
#filter_dataframe prende in input una lista di csv
dataframes = [filter_dataframe(lis) for lis in all_sorted_csv_filepaths]

In [15]:
#NUMERO TOKENS

import pandas as pd
import string

def count_tokens(csv_file_paths):
    punct = set(string.punctuation + '·')  # Use a set for faster lookup
    total_tokens = 0
   
    # Iterate through each list of CSV file paths
    for file_list in csv_file_paths:
        for file_path in file_list:
            # Read the CSV file
            df = pd.read_csv(file_path)
           
            # Filter rows where '@lemma' is a string and '@form' is not in punctuation
            valid_tokens = df[df['@lemma'].apply(lambda x: isinstance(x, str)) & (~df['@form'].isin(punct))]
           
            # Accumulate the count of valid tokens
            total_tokens += valid_tokens.shape[0]

    return total_tokens


In [16]:



# Example usage:
total_tokens = count_tokens(all_sorted_csv_filepaths)
print(f"Total number of tokens: {total_tokens}")


Total number of tokens: 177262


In [17]:
#NUMERO TOKENS tolta punteggiatura

import pandas as pd
import string

def count_tokens_senza_punctuation(csv_file_paths):
    punct = set(string.punctuation + '·')  # Use a set for faster lookup
    punct.add('...')
    dataframes = []
   
    # Iterate through each list of CSV file paths
    for file_list in csv_file_paths:
        final_list = []
        for df in file_list:
            # Read the CSV file
            
           
            # Filter rows where '@lemma' is a string and '@form' is not in punctuation
            valid_tokens = df[df['@lemma'].apply(lambda x: isinstance(x, str)) & (~df['@form'].isin(punct))]
           
            # Accumulate the count of valid tokens
            final_list.append(valid_tokens) 
        dataframes.append(final_list)
    return dataframes

In [18]:


# Example usage -> creo nuovi dataframes senza punteggiatura:
dataframes = count_tokens_senza_punctuation(dataframes)



In [19]:


# Loop through the dataframes and check for anomalies
for j, lis in enumerate(dataframes):
    anomalies_info = {}
    output_lines = []  
    for i, df in enumerate(lis):
        anomalies_out = check_postag_anomalies(df)
        if len(anomalies_out) > 0:
            anomalies_info[f"File {i}"] = anomalies_out #c'è un dizionario che prende come chiave il file e come valore le anomalie
            # Print and collect the output only if anomalies exist
            print(f"File {i}")
            print(list(df['@form']))
            print(anomalies_out)
            
            # Save the output to the list
            output_lines.append(f"File {i}\n")
            output_lines.append(f"{list(df['@form'])}\n")
            output_lines.append(f"{anomalies_out}\n")

    # Save the collected output lines to a file serve per mettere le anomalie su un file vuoto. w significa che sto aprendo il file in scrittura.
    output_file_path = "C:/Users/lcolo/Desktop/TESI/CODICI DEFINITIVI DIZ UNICO-2/PEDALION/anomalie_pedalion/anomalies_output_pedalion_" + str(j) + ".txt"  
    with open(output_file_path, 'w', encoding = 'utf-8') as file:
        file.writelines(output_lines) #mi scrive sul file vuoto le righe che ho printato
    
    print(f"Output saved to {output_file_path}")


File 1
['τοῖς', 'δὲ', 'ὑπὲρ', 'τῶν', 'μεγίστων', 'μέλλουσι', 'κινδυνεύειν', 'ἱερῶν', 'καὶ', 'πατρίδος', 'καὶ', 'γονέων', 'καὶ', 'τέκνων', 'καὶ', 'τῶν', 'ἄλλων', 'οὐκ', 'ἴσος', 'οὐδὲ', 'ὅμοιος', 'ἀγών', 'ἐστιν', 'ἀλλὰ', 'σωθεῖσι', 'μὲν', 'καὶ', 'καλῶς', 'ἀμυναμένοις', 'τοὺς', 'πολεμίους', 'φοβεροὺς', 'τοῖς', 'ἐναντίοις', 'καὶ', 'δυσεπιθέτους', 'εἰς', 'τὸν', 'λοιπὸν', 'χρόνον', 'εἶναι', 'κακῶς', 'δὲ', 'προσενεχθεῖσι', 'πρὸς', 'τοὺς', 'κινδύνους', 'οὐδεμία', 'ἐλπὶς', 'σωτηρίας', 'ὑπάρξει']
[('ἄλλων', 'a-p---ng_', "Unexpected character '_' at position 9")]
File 3
['ἂν', 'δὲ', 'ἄρα', 'τι', 'σύμπτωμα', 'γένηται', 'ἀλλ’', 'οἵ', 'γε', 'λοιποὶ', 'τὰ', 'ὑπάρχοντα', 'εἰς', 'τ-', 'αὐτό', 'ποτε', 'καταστήσαιεν', 'ἄν', 'καθάπερ', 'τινὲς', 'τῶν', 'Ἑλλήνων', 'εἰς', 'τὸ', 'ἔσχατον', 'ἀφικόμενοι', 'πάλιν', 'ἀνέλαβον', 'ἑαυτούς']
[('τινὲς', 'p-p---cn-', "Unexpected character 'c' at position 7")]
File 8
['ἔπειτα', 'λοιπὸν', 'ἀπολέγειν', 'σώματα', 'τὰ', 'δυνησόμενα', 'μάλιστα', 'πονεῖν', 'καὶ', 'μερίσαντα'

In [20]:
#COSA SONO ESATTAMENTE I NAN ED ERRORE FLOAT.
#nan sono valori dove esistono righe in corrispondenza delle quali il postag non c'era.
#meglio stampare la form dei nan per essere sicuri che sia effettivamente un nan e non una forma vera e propria. 
#float al postag invece della stringa ho trovato dei valori float.
#in realtà nan e float qui coincidono, il nan è rappresentato come tipo float.
# QUANTI ERANO IN ORIGINE I NAN E QUANTI NE ABBIAMO RIMOSSI

def count_nan_anomalies(df_list):
    count = 0

    for i, df in enumerate(df_list):
        count += df['@postag'].isna().sum()
        if df[df['@postag'].isna()].empty != True:
            print(df[df['@postag'].isna()])

    return count

In [21]:
countN = [count_nan_anomalies(lis) for lis in dataframes]

                    @ref  @id @form @lemma @postag @relation
0  Leuven|0557-001|279|1    1     —      —     NaN      AuxG
                    @ref  @id @form @lemma @postag @relation
0  Leuven|0557-001|404|1    1     —      —     NaN      AuxG


In [22]:
sum(countN)

2

In [23]:
count_nananomalies = sum([count_nan_anomalies(lis) for lis in dataframes])
print(f'count_nan:{count_nananomalies}')

                    @ref  @id @form @lemma @postag @relation
0  Leuven|0557-001|279|1    1     —      —     NaN      AuxG
                    @ref  @id @form @lemma @postag @relation
0  Leuven|0557-001|404|1    1     —      —     NaN      AuxG
count_nan:2


In [24]:

def remove_nan_anomalies(df_list):
    for i, df in enumerate(df_list):

        df_list[i] = df[pd.notna(df['@postag'])]

    return df_list

In [25]:
nan_dataframes = [remove_nan_anomalies(lis) for lis in dataframes]

In [26]:
# QUANTI ERANO IN ORIGINE I G E QUANTI NE ABBIAMO RIMOSSI
def count_G_anomalies(df_list):
    count = 0
    count_z = 0
    for i, df in enumerate(df_list):
        n0 = df.shape[0]
        n1 = df[df['@form']!='G?'].shape[0]
        count += (n0-n1)
        df_z = df[df['@form'] =='G?']
        count_z += df_z[df_z['@postag']=='z--------'].shape[0]
        df_G = df[df['@form'] =='G?']
        for index, row in df_G.iterrows():
            if row['@form'] == 'G?':
                print('frase', i)
                print([index, row['@form'], row['@lemma'], row['@postag'], row['@relation']])

    return count, count_z

In [27]:
count_Ganomalies = [sum(x) for x in zip(*[count_G_anomalies(lis) for lis in dataframes])]
print(f'count_G:{count_Ganomalies[0]}')
print(f'count_G_z:{count_Ganomalies[1]}')

frase 55
[24, 'G?', '_', 'z--------', 'AuxG']
frase 68
[9, 'G?', '_', 'z--------', 'AuxG']
frase 109
[12, 'G?', '_', 'z--------', 'GAP']
frase 112
[13, 'G?', '_', 'z--------', 'AuxG']
frase 116
[2, 'G?', '_', 'z--------', 'GAP']
frase 121
[11, 'G?', '_', 'z--------', 'AuxG']
frase 158
[7, 'G?', '_', 'z--------', 'ADV']
frase 161
[5, 'G?', '_', 'z--------', 'AuxG']
frase 250
[5, 'G?', '_', 'z--------', 'GAP']
frase 272
[7, 'G?', '_', 'z--------', 'AuxG']
frase 273
[8, 'G?', '_', 'z--------', 'AuxG']
frase 280
[0, 'G?', '_', 'z--------', 'AuxG']
frase 7
[12, 'G?', '_', 'z--------', 'GAP']
frase 202
[5, 'G?', '_', 'z--------', 'GAP']
frase 300
[8, 'G?', '_', 'z--------', 'AuxG']
frase 305
[5, 'G?', '_', 'z--------', 'GAP']
frase 328
[16, 'G?', '_', 'z--------', 'AuxG']
frase 343
[13, 'G?', '_', 'z--------', nan]
frase 352
[6, 'G?', '_', 'z--------', 'AuxG']
frase 352
[10, 'G?', '_', 'z--------', 'GAP']
frase 353
[2, 'G?', '_', 'z--------', 'AuxG']
frase 397
[13, 'G?', '_', 'z--------', 'A

In [28]:
#ho fatto un sottinsieme in cui ho detto: raggruppa e tieni solo quello che 
#è diverso da G?
#df['@form']=='G?' così mi viene restituita una lista di True e False, True per quelle righe che hanno G? nella form
#se voglio prendere solo le righe che abbiano nel dataframe G? nella colonna form scrivo:
#df[df['@form']=='G?'] -> le quadre indicano che sto prendendo alcune righe df[] sta dicendo prendi
#alcuni elementi del dataframe. Qui le righe che prendo sono solo quelle che hanno il True. 

def remove_G_anomalies(df_list):
    for i, df in enumerate(df_list):

        df_list[i] = df[df['@form'] != 'G?'] 

    return df_list

In [29]:
G_dataframes = [remove_G_anomalies(lis) for lis in dataframes]

In [30]:
#df_list è la lista di tutti i dataframes di un'opera es. Eschine 1-50.
#se do come argomento a enumerate una lista, enumerate mi fa iterare sia l'indice, sia l'elemento della lista.
#se ho una lista con dentro 5 dataframes con enumerate io itero contemporaneamente sia sull'indice della lista che sull'elemnto.
#for i,df itero sia su 0 che df0, cioè il primo df che si chiama df0 sta in posizione 0 della lista. 
#questo mi permette di stampare qual è la frase che mi interessa.  
#iterrows() è un metodo di Pandas che permette di iterare (scorrere) attraverso le righe di un DataFrame. Ogni volta che viene chiamato, 
# iterrows() restituisce una tupla con due elementi:
# L'indice della riga (può essere numerico o un altro tipo di indice).
#La riga stessa sotto forma di un oggetto Pandas Series, con le colonne del DataFrame come etichette degli indici.

def print_9_anomalies(df_list):
    
    for i,df in enumerate(df_list):
        for index, row in df.iterrows():
            
            postag = row['@postag']
            if len(postag) == 9 and postag[-1] == '_':
               print('frase', i)
               print([index, row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])

In [31]:
#salvare la lista di directory
lis_dir = os.listdir("C:/Users/lcolo/Desktop/TESI/CODICI DEFINITIVI DIZ UNICO-2/PEDALION/output_pedalion_con_relation")
for j,lis in enumerate(dataframes):
    print('Opera',lis_dir[j])
    print_9_anomalies(lis)

Opera aeneas.xml
frase 1
[17, 'ἄλλων', 'ἄλλος', 'a-p---ng_', 'a-p---ng_', 'APOS_CO']
frase 15
[39, 'μεγάλων', 'μέγας', 'a-p---mg_', 'a-p---mg_', 'PNOM_CO']
frase 22
[5, 'τούτοις', 'οὗτος', 'a-p---nd_', 'a-p---nd_', 'OBJ']
frase 27
[6, 'ἄλλων', 'ἄλλος', 'a-p---ng_', 'a-p---ng_', 'ATR']
frase 180
[1, 'ἄλλο', 'ἄλλος', 'a-s---na_', 'a-s---na_', 'ATR_CO']
Opera aesop1.xml
frase 142
[1, 'ἀποστᾶσαν', 'ἀφίστημι', 'v-sapmfa_', 'v-sapmfa_', 'ATR']
frase 149
[7, 'Αἰσωπείου', 'Αἰσώπειος', 'a-s---fg_', 'a-s---fg_', 'ATR']
frase 168
[8, 'ἐμπίπτων', 'ἐμπίπτω', 'v-sppamn_', 'v-sppamn_', 'ADV']
frase 204
[4, 'ἄμφω', 'ἄμφω', 'a-d---mg_', 'a-d---mg_', 'SBJ']
frase 212
[1, 'πένης', 'πένης', 'a-s---mn_', 'a-s---mn_', 'ATR']
Opera charb1.xml
Opera chion.xml
frase 41
[31, 'ἐπιλήσμονί', 'ἐπιλήσμων', 'a-s---fd_', 'a-s---fd_', 'ATR']
Opera crit.xml
Opera epictetus.xml
frase 298
[15, 'τἆλλʼ', 'ἄλλος', 'a-p---nn_', 'a-p---nn_', 'SBJ_CO']
Opera epicurus1.xml
frase 32
[14, 'ὅπως', 'ὅπως', 'd-------_', 'd-------_', 

In [32]:
# QUANTI TOTALI TOLTI E CAMBIATI CON - = PEDALION

# Function to check and display anomalies in the postag
def count_9_anomalies(df_list):
  final_list = []
  count = 0
  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if len(postag) == 9 and postag[-1] == '_':
           count+=1

  return count

In [33]:
count_9anomalies = sum([count_9_anomalies(lis) for lis in dataframes])
print(f'count_9:{count_9anomalies}')

count_9:154


In [34]:
# QUANTI TOTALI TOLTI E CAMBIATI CON - = PEDALION

# Function to check and display anomalies in the postag
def replace_9_anomalies(df_list):
  final_list = []
  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if len(postag) == 9 and postag[-1] == '_':
          #modify the postag
          row['@postag'] = postag[:8] + '-'
          print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
          #update the dataframe .at è come dire append ma per i dataframe
          df.at[index, '@postag'] = row['@postag']
          modified = True

    #append the dataframe whether modified or not
    final_list.append(df)

  return final_list

In [35]:
anomalies9_dataframes = [replace_9_anomalies(lis) for lis in dataframes] # applico ad ogni dataframe che è una lista di liste la correzione

['ἄλλων', 'ἄλλος', 'a-p---ng_', 'a-p---ng-', 'APOS_CO']
['μεγάλων', 'μέγας', 'a-p---mg_', 'a-p---mg-', 'PNOM_CO']
['τούτοις', 'οὗτος', 'a-p---nd_', 'a-p---nd-', 'OBJ']
['ἄλλων', 'ἄλλος', 'a-p---ng_', 'a-p---ng-', 'ATR']
['ἄλλο', 'ἄλλος', 'a-s---na_', 'a-s---na-', 'ATR_CO']
['ἀποστᾶσαν', 'ἀφίστημι', 'v-sapmfa_', 'v-sapmfa-', 'ATR']
['Αἰσωπείου', 'Αἰσώπειος', 'a-s---fg_', 'a-s---fg-', 'ATR']
['ἐμπίπτων', 'ἐμπίπτω', 'v-sppamn_', 'v-sppamn-', 'ADV']
['ἄμφω', 'ἄμφω', 'a-d---mg_', 'a-d---mg-', 'SBJ']
['πένης', 'πένης', 'a-s---mn_', 'a-s---mn-', 'ATR']
['ἐπιλήσμονί', 'ἐπιλήσμων', 'a-s---fd_', 'a-s---fd-', 'ATR']
['τἆλλʼ', 'ἄλλος', 'a-p---nn_', 'a-p---nn-', 'SBJ_CO']
['ὅπως', 'ὅπως', 'd-------_', 'd--------', 'ADV']
['ὡς', 'ὡς', 'd-------_', 'd--------', 'ADV']
['μολιβῆς', 'μολιβοῦς', 'a-s---fg_', 'a-s---fg-', 'ADV_CO']
['ὡς', 'ὡς', 'd-------_', 'd--------', 'ADV']
['ὡς', 'ὡς', 'd-------_', 'd--------', 'ADV']
['ὡς', 'ὡς', 'd-------_', 'd--------', 'ADV']
['διαμεμηρυμένα', 'διαμηρύω', 'v-prpen

In [34]:
'''def print_g_particles(df_list):
    
    for i,df in enumerate(df_list):
        for index, row in df.iterrows():
            
            postag = row['@postag']
            if len(postag) == 9 and postag[0] == 'g':
               print('frase', i)
               print([index,row['@form'],postag])'''

"def print_g_particles(df_list):\n    \n    for i,df in enumerate(df_list):\n        for index, row in df.iterrows():\n            \n            postag = row['@postag']\n            if len(postag) == 9 and postag[0] == 'g':\n               print('frase', i)\n               print([index,row['@form'],postag])"

In [35]:
'''#salvare la lista di directory
lis_dir = os.listdir('output_pedalion_con_relation')
for j,lis in enumerate(dataframes):
    print('Opera',lis_dir[j])
    print_g_particles(lis)'''

"#salvare la lista di directory\nlis_dir = os.listdir('output_pedalion_con_relation')\nfor j,lis in enumerate(dataframes):\n    print('Opera',lis_dir[j])\n    print_g_particles(lis)"

In [36]:
'''def print_l8(df_list):
    
    for i,df in enumerate(df_list):
        for index, row in df.iterrows():
            
            postag = row['@postag']
            if len(postag) == 9 and postag[7] == 'l':
               print('frase', i)
               print([index,row['@form'],postag])'''

"def print_l8(df_list):\n    \n    for i,df in enumerate(df_list):\n        for index, row in df.iterrows():\n            \n            postag = row['@postag']\n            if len(postag) == 9 and postag[7] == 'l':\n               print('frase', i)\n               print([index,row['@form'],postag])"

In [37]:
'''#salvare la lista di directory
lis_dir = os.listdir('output_pedalion_con_relation')
for j,lis in enumerate(dataframes):
    print('Opera',lis_dir[j])
    print_l8(lis)'''

"#salvare la lista di directory\nlis_dir = os.listdir('output_pedalion_con_relation')\nfor j,lis in enumerate(dataframes):\n    print('Opera',lis_dir[j])\n    print_l8(lis)"

In [36]:
#QUANTE P FINALI RIMOSSE E QUANTE PER OGNI CATEGORIA??? ES. AVVERBI, AGGETTIVI, VERBI ETC. 
#GORMAN SOLO AGG E AVV 

def print_9P(df_list):
    
    for i,df in enumerate(df_list):
        for index, row in df.iterrows():
            
            postag = row['@postag']
            if len(postag) == 9 and postag[-1] == 'p':
               print('frase', i)
               print([index, row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])

In [37]:
#salvare la lista di directory
lis_dir = os.listdir("C:/Users/lcolo/Desktop/TESI/CODICI DEFINITIVI DIZ UNICO-2/PEDALION/output_pedalion_con_relation")
for j,lis in enumerate(dataframes):
    print('Opera',lis_dir[j])
    print_9P(lis)

Opera aeneas.xml
Opera aesop1.xml
frase 432
[7, 'τετράπουν', 'τετράπους', 'a-s---nnp', 'a-s---nnp', 'SBJ']
Opera charb1.xml
frase 213
[2, 'πρῶτον', 'πρῶτον', 'd-------p', 'd-------p', 'ADV']
Opera chion.xml
Opera crit.xml
frase 50
[7, 'ἄλλων', 'ἄλλος', 'p-p---mgp', 'p-p---mgp', 'ATR']
frase 50
[40, 'ἄλλο', 'ἄλλος', 'p-s---nap', 'p-s---nap', 'ATR']
frase 109
[2, 'τἆλλα', 'ἄλλος', 'p-p---nnp', 'p-p---nnp', 'SBJ']
frase 185
[0, 'ἄλλο', 'ἄλλος', 'p-s---nap', 'p-s---nap', 'ATR']
frase 207
[14, 'ἄλλων', 'ἄλλος', 'p-p---mgp', 'p-p---mgp', 'ATR']
frase 218
[7, 'μεγάλα', 'μέγας', 'a-p---nnp', 'a-p---nnp', 'ATR']
frase 219
[5, 'ἄλλων', 'ἄλλος', 'p-p---mgp', 'p-p---mgp', 'ATR']
frase 226
[0, 'ἄλλο', 'ἄλλος', 'p-s---nap', 'p-s---nap', 'ATR']
frase 228
[0, 'ἄλλο', 'ἄλλος', 'p-s---nap', 'p-s---nap', 'ATR']
Opera epictetus.xml
Opera epicurus1.xml
frase 25
[6, 'τόθʼ', 'τότε', 'd-------p', 'd-------p', 'ADV']
frase 27
[21, 'κακῶv', 'κακός', 'a-p---ngp', 'a-p---ngp', 'ATR']
frase 63
[41, 'μεγάλων', 'μέγ

In [38]:
# QUANTI TOTALI TOLTI E CAMBIATI CON - = PEDALION

# Function to check and display anomalies in the postag
def count_9p_anomalies(df_list):
  final_list = []
  count = 0
  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if len(postag) == 9 and postag[-1] == 'p':
           count+=1

  return count

In [39]:

count_9panomalies = sum([count_9p_anomalies(lis) for lis in dataframes])
print(f'count_9p:{count_9panomalies}')

count_9p:152


In [40]:
# Function to check and display anomalies in the postag
def replace_9p_anomalies(df_list):
  final_list = []
  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if len(postag) == 9 and postag[-1] == 'p':
          #modify the postag
          row['@postag'] = postag[:8] + '-'
          print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
          #update the dataframe .at è come dire append ma per i dataframe
          df.at[index, '@postag'] = row['@postag']
          modified = True

    #append the dataframe whether modified or not
    final_list.append(df)

  return final_list

In [41]:
anomalies9p_dataframes = [replace_9p_anomalies(lis) for lis in dataframes] # applico ad ogni dataframe che è una lista di liste la correzione

['τετράπουν', 'τετράπους', 'a-s---nnp', 'a-s---nn-', 'SBJ']
['πρῶτον', 'πρῶτον', 'd-------p', 'd--------', 'ADV']
['ἄλλων', 'ἄλλος', 'p-p---mgp', 'p-p---mg-', 'ATR']
['ἄλλο', 'ἄλλος', 'p-s---nap', 'p-s---na-', 'ATR']
['τἆλλα', 'ἄλλος', 'p-p---nnp', 'p-p---nn-', 'SBJ']
['ἄλλο', 'ἄλλος', 'p-s---nap', 'p-s---na-', 'ATR']
['ἄλλων', 'ἄλλος', 'p-p---mgp', 'p-p---mg-', 'ATR']
['μεγάλα', 'μέγας', 'a-p---nnp', 'a-p---nn-', 'ATR']
['ἄλλων', 'ἄλλος', 'p-p---mgp', 'p-p---mg-', 'ATR']
['ἄλλο', 'ἄλλος', 'p-s---nap', 'p-s---na-', 'ATR']
['ἄλλο', 'ἄλλος', 'p-s---nap', 'p-s---na-', 'ATR']
['τόθʼ', 'τότε', 'd-------p', 'd--------', 'ADV']
['κακῶv', 'κακός', 'a-p---ngp', 'a-p---ng-', 'ATR']
['μεγάλων', 'μέγας', 'a-p---ngp', 'a-p---ng-', 'ATR']
['ἀπολιποῦσα', 'ἀπολείπω', 'v-sapafnp', 'v-sapafn-', 'ADV']
['εἰκός', 'εἴκως', 'a-s---nnp', 'a-s---nn-', 'PNOM']
['κακοήθων', 'κακοήθης', 'a-p---mgp', 'a-p---mg-', 'ATR']
['φιλοτησίαι', 'φιλοτήσιος', 'a-p---fnp', 'a-p---fn-', 'SBJ_CO']
['ἄλλοις', 'ἄλλος', 'a-p---md

In [44]:
'''def print_x1(df_list):
    
    for i,df in enumerate(df_list):
        for index, row in df.iterrows():
            
            postag = row['@postag']
            if len(postag) == 9 and postag[0] == 'x':
               print('frase', i)
               print([index,row['@form'],postag])'''

"def print_x1(df_list):\n    \n    for i,df in enumerate(df_list):\n        for index, row in df.iterrows():\n            \n            postag = row['@postag']\n            if len(postag) == 9 and postag[0] == 'x':\n               print('frase', i)\n               print([index,row['@form'],postag])"

In [45]:
'''#salvare la lista di directory
lis_dir = os.listdir('output_pedalion_con_relation')
for j,lis in enumerate(dataframes):
    print('Opera',lis_dir[j])
    print_x1(lis)'''

"#salvare la lista di directory\nlis_dir = os.listdir('output_pedalion_con_relation')\nfor j,lis in enumerate(dataframes):\n    print('Opera',lis_dir[j])\n    print_x1(lis)"

In [42]:
def print_b(df_list):
    count = {}
    for i, df in enumerate(df_list):
        for index, row in df.iterrows():
            
            postag = row['@postag']
            if len(postag) == 9 and postag[0] == 'b':
                # Initialize the key if it does not exist
                if row['@lemma'] not in count:
                    count[row['@lemma']] = 0
                
                # Increment the count for this form
                count[row['@lemma']] += 1

                # Print relevant details
                # print('frase', i)
                # print([index, row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
    
    return count

In [43]:
#salvare la lista di directory
lis_dir = os.listdir("C:/Users/lcolo/Desktop/TESI/CODICI DEFINITIVI DIZ UNICO-2/PEDALION/output_pedalion_con_relation")
count_final = []
for j,lis in enumerate(dataframes):
    #print('Opera',lis_dir[j])
    count_final.append(print_b(lis))


In [44]:
# QUANTI TOTALI TOLTI E CAMBIATI CON - = PEDALION

# Function to check and display anomalies in the postag
def count_b_anomalies(df_list):
  final_list = []
  count = 0
  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if len(postag) == 9 and postag[0] == 'b':
           count+=1

  return count



In [45]:
count_banomalies = sum([count_b_anomalies(lis) for lis in dataframes])
print(f'count_b:{count_banomalies}')

count_b:5801


In [46]:
countB = [count_b_anomalies(lis) for lis in dataframes]

In [47]:
sum(countB)

5801

In [48]:
'καὶ' == 'καὶ'

True

In [48]:
def print_kai(df_list):
    kailist = ['καί', 'καὶ', 'κα-', 'κ-']
    for i,df in enumerate(df_list):
        for index, row in df.iterrows():
            
            postag = row['@postag']
            if len(postag) == 9 and row['@form'] in kailist:
               print('frase', i)
               print([index, row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])

In [49]:
#salvare la lista di directory
lis_dir = os.listdir("C:/Users/lcolo/Desktop/TESI/CODICI DEFINITIVI DIZ UNICO-2/PEDALION/output_pedalion_con_relation")
for j,lis in enumerate(dataframes):
    print('Opera',lis_dir[j])
    print_kai(lis)

Opera aeneas.xml
frase 0
[11, 'καὶ', 'καί', 'c--------', 'c--------', 'COORD']
frase 0
[32, 'καὶ', 'καί', 'c--------', 'c--------', 'AuxY']
frase 0
[34, 'καὶ', 'καί', 'c--------', 'c--------', 'COORD']
frase 1
[9, 'καὶ', 'καί', 'c--------', 'c--------', 'AuxY']
frase 1
[11, 'καὶ', 'καί', 'c--------', 'c--------', 'AuxY']
frase 1
[13, 'καὶ', 'καί', 'c--------', 'c--------', 'AuxY']
frase 1
[15, 'καὶ', 'καί', 'c--------', 'c--------', 'COORD']
frase 1
[29, 'καὶ', 'καί', 'c--------', 'c--------', 'COORD']
frase 1
[37, 'καὶ', 'καί', 'c--------', 'c--------', 'COORD']
frase 2
[4, 'καὶ', 'καί', 'c--------', 'c--------', 'COORD']
frase 2
[10, 'καὶ', 'καί', 'c--------', 'c--------', 'COORD']
frase 2
[18, 'καὶ', 'καί', 'c--------', 'c--------', 'COORD']
frase 4
[11, 'καὶ', 'καί', 'c--------', 'c--------', 'AuxY']
frase 4
[16, 'καὶ', 'καί', 'c--------', 'c--------', 'COORD']
frase 4
[21, 'καὶ', 'καί', 'c--------', 'c--------', 'COORD']
frase 4
[24, 'καὶ', 'καί', 'c--------', 'c--------', 'AuxY']

In [76]:
def count_kai_anomalies(df_list): 
    final_list = []
    kailist = ['καί', 'καὶ', 'κα-', 'κ-']
    
    # Initialize counts for the requested conditions
    count_kai_forms = 0
    count_AuxY_c = 0
    count_AuxY_d = 0
    count_AuxY_b = 0
    count_AuxY_not = 0
    count_AuxX_c = 0
    count_AuxX_d = 0
    count_AuxX_b = 0
    count_AuxX_not = 0
    count_AuxZ_c = 0
    count_AuxZ_d = 0
    count_AuxZ_b = 0
    count_AuxZ_not = 0
    count_AuxC_c = 0
    count_AuxC_d = 0
    count_AuxC_b = 0
    count_AuxC_not = 0
    count_COORD_c = 0
    count_COORD_d = 0
    count_COORD_b = 0
    count_COORD_not = 0
    count_not_relation = 0

    for df in df_list:
        modified = False  # track if the dataframe has been modified

        for index, row in df.iterrows():
            postag = row['@postag']
            
            # If the form is in the kai list, count it
            if row['@form'] in kailist:
                count_kai_forms += 1

                # Check the '@relation' and '@postag' for the specified conditions
                relation = row['@relation']
                if relation == 'AuxY':
                    if postag[0] == 'c':
                        count_AuxY_c += 1
                    elif postag[0] == 'd':
                        count_AuxY_d += 1
                    elif postag[0] == 'b':
                        count_AuxY_b += 1
                    else:
                        count_AuxY_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxX':
                    if postag[0] == 'c':
                        count_AuxX_c += 1
                    elif postag[0] == 'd':
                        count_AuxX_d += 1
                    elif postag[0] == 'b':
                        count_AuxX_b += 1
                    else:
                        count_AuxX_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxZ':
                    if postag[0] == 'c':
                        count_AuxZ_c += 1
                    elif postag[0] == 'd':
                        count_AuxZ_d += 1
                    elif postag[0] == 'b':
                        count_AuxZ_b += 1
                    else:
                        count_AuxZ_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxC':
                    if postag[0] == 'c':
                        count_AuxC_c += 1
                    elif postag[0] == 'd':
                        count_AuxC_d += 1
                    elif postag[0] == 'b':
                        count_AuxC_b += 1
                    else:
                        count_AuxC_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'COORD':
                    if postag[0] == 'c':
                        count_COORD_c += 1
                    elif postag[0] == 'd':
                        count_COORD_d += 1
                    elif postag[0] == 'b':
                        count_COORD_b += 1
                    else:
                        count_COORD_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                else:
                    count_not_relation += 1
                    print('+++++++++++++++++++++++++NOT RELATION START+++++++++++++++++++++++++++++')

                    print('->', f'conteggio: {count_not_relation}',[row['@form'], row['@lemma'], postag, row['@relation']])

                    print('+++++++++++++++++++++++++NOT RELATION END+++++++++++++++++++++++++++++')

    # Return the counts
    return {
        'total_kai_forms': count_kai_forms,
        'AuxY_c': count_AuxY_c,
        'AuxY_d': count_AuxY_d,
        'AuxY_b': count_AuxY_b,
        'AuxY_not' : count_AuxY_not,
        'AuxX_c': count_AuxX_c,
        'AuxX_d': count_AuxX_d,
        'AuxX_b': count_AuxX_b,
        'AuxX_not' : count_AuxX_not,
        'AuxZ_c': count_AuxZ_c,
        'AuxZ_d': count_AuxZ_d,
        'AuxZ_b': count_AuxZ_b,
        'AuxZ_not' : count_AuxZ_not,
        'AuxC_c': count_AuxC_c,
        'AuxC_d': count_AuxC_d,
        'AuxC_b': count_AuxC_b,
        'AuxC_not' : count_AuxC_not,
        'COORD_c': count_COORD_c,
        'COORD_d': count_COORD_d,
        'COORD_b': count_COORD_b,
        'COORD_not' : count_COORD_not,
        'relation_not' : count_not_relation 
    }


In [77]:
countkai_dataframes = [count_kai_anomalies(lis) for lis in dataframes]

+++++++++++++++++++++++++NOT RELATION START+++++++++++++++++++++++++++++
-> conteggio: 1 ['καὶ', 'καί', 'c--------', 'AuxK']
+++++++++++++++++++++++++NOT RELATION END+++++++++++++++++++++++++++++
+++++++++++++++++++++++++NOT RELATION START+++++++++++++++++++++++++++++
-> conteggio: 1 ['καὶ', 'καί', 'b--------', 'COORD_CO']
+++++++++++++++++++++++++NOT RELATION END+++++++++++++++++++++++++++++
+++++++++++++++++++++++++NOT RELATION START+++++++++++++++++++++++++++++
-> conteggio: 1 ['καὶ', 'καί', 'c--------', 'ATR']
+++++++++++++++++++++++++NOT RELATION END+++++++++++++++++++++++++++++
+++++++++++++++++++++++++NOT RELATION START+++++++++++++++++++++++++++++
-> conteggio: 1 ['καί', 'καί', 'b--------', 'OBJ']
+++++++++++++++++++++++++NOT RELATION END+++++++++++++++++++++++++++++
+++++++++++++++++++++++++NOT RELATION START+++++++++++++++++++++++++++++
-> conteggio: 2 ['καί', 'καί', 'b--------', 'OBJ']
+++++++++++++++++++++++++NOT RELATION END+++++++++++++++++++++++++++++
+++++++++++++++++++

In [52]:
def sum_dicts(dict_list):
    # Initialize an empty dictionary to store the summed values
    summed_dict = {}

    # Iterate through each dictionary in the list
    for d in dict_list:
        for key, value in d.items():
            # If the key is already in the summed_dict, add the value, otherwise initialize it
            if key in summed_dict:
                summed_dict[key] += value
            else:
                summed_dict[key] = value

    return summed_dict

In [53]:
summed_result = sum_dicts(countkai_dataframes)

countkai_dataframes = pd.DataFrame(list(summed_result.items()), columns=['Key', 'Value'])

In [54]:
countkai_dataframes

Key  Value
0   total_kai_forms  10252
1            AuxY_c   1572
2            AuxY_d    685
3            AuxY_b   1031
4          AuxY_not      0
5            AuxX_c      2
6            AuxX_d      0
7            AuxX_b      0
8          AuxX_not      0
9            AuxZ_c    465
10           AuxZ_d    762
11           AuxZ_b    128
12         AuxZ_not      0
13           AuxC_c      7
14           AuxC_d      0
15           AuxC_b      3
16         AuxC_not      0
17          COORD_c   2874
18          COORD_d      3
19          COORD_b   2691
20        COORD_not      0
21     relation_not     29

In [55]:

sum(countkai_dataframes['Value'])-10252

10252

In [56]:
def replace_kai_anomalies(df_list):
  final_list = []
  kailist = ['καί', 'καὶ', 'κα-', 'κ-']
  postag_list = ['d','c','b']
  relations = ['AuxC', 'COORD','AuxX','AuxY']

  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if len(postag) == 9 and row['@form'] in kailist:
          if postag[0] in postag_list:
            if row['@relation']== 'AuxZ':
              row['@postag'] = 'd' + postag[1:9]
              print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            elif row['@relation'] in relations:
              row['@postag'] = 'c' + postag[1:9]
              print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
          
          #update the dataframe .at è come dire append ma per i dataframe
          df.at[index, '@postag'] = row['@postag']
          modified = True

    #append the dataframe whether modified or not
    final_list.append(df)

  return final_list

In [57]:
anomalieskai_dataframes = [replace_kai_anomalies(lis) for lis in dataframes]

['καὶ', 'καί', 'c--------', 'c--------', 'COORD']
['καὶ', 'καί', 'c--------', 'c--------', 'AuxY']
['καὶ', 'καί', 'c--------', 'c--------', 'COORD']
['καὶ', 'καί', 'c--------', 'c--------', 'AuxY']
['καὶ', 'καί', 'c--------', 'c--------', 'AuxY']
['καὶ', 'καί', 'c--------', 'c--------', 'AuxY']
['καὶ', 'καί', 'c--------', 'c--------', 'COORD']
['καὶ', 'καί', 'c--------', 'c--------', 'COORD']
['καὶ', 'καί', 'c--------', 'c--------', 'COORD']
['καὶ', 'καί', 'c--------', 'c--------', 'COORD']
['καὶ', 'καί', 'c--------', 'c--------', 'COORD']
['καὶ', 'καί', 'c--------', 'c--------', 'COORD']
['καὶ', 'καί', 'c--------', 'c--------', 'AuxY']
['καὶ', 'καί', 'c--------', 'c--------', 'COORD']
['καὶ', 'καί', 'c--------', 'c--------', 'COORD']
['καὶ', 'καί', 'c--------', 'c--------', 'AuxY']
['καὶ', 'καί', 'c--------', 'c--------', 'AuxY']
['καὶ', 'καί', 'c--------', 'c--------', 'AuxY']
['καὶ', 'καί', 'c--------', 'c--------', 'AuxY']
['καὶ', 'καί', 'c--------', 'c--------', 'AuxY']
['καὶ', 'κ

In [58]:
#PROBLEMA PARTICELLE, QUI SEGNATE PER LO PIU' CON B. 

In [59]:
def print_h(df_list):
    
    for i,df in enumerate(df_list):
        for index, row in df.iterrows():
            
            postag = row['@postag']
            if row['@form'] == 'ἢ' or row['@form'] == 'ἤ' or row['@form'] == 'ἤπερ':
               print('frase', i)
               print([index, row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])

In [60]:
#salvare la lista di directory
lis_dir = os.listdir("C:/Users/lcolo/Desktop/TESI/CODICI DEFINITIVI DIZ UNICO-2/PEDALION/output_pedalion_con_relation")
for j,lis in enumerate(dataframes):
    print('Opera',lis_dir[j])
    print_h(lis)

Opera aeneas.xml
frase 0
[21, 'ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
frase 8
[28, 'ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
frase 20
[29, 'ἢ', 'ἤ1', 'c--------', 'c--------', 'AuxC']
frase 24
[2, 'ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
frase 25
[3, 'ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
frase 47
[18, 'ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
frase 47
[44, 'ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
frase 58
[42, 'ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
frase 58
[45, 'ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
frase 58
[53, 'ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
frase 59
[12, 'ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
frase 61
[26, 'ἢ', 'ἤ1', 'c--------', 'c--------', 'AuxY']
frase 67
[8, 'ἢ', 'ἤ', 'b--------', 'b--------', 'COORD']
frase 73
[16, 'ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
frase 79
[39, 'ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
frase 79
[64, 'ἢ', 'ἤ1', 'c--------', 'c--------', 'AuxY']
frase 79
[66, 'ἢ', 'ἤ1', 'c-----

In [61]:
def count_eper_anomalies(df_list):
    final_list = []
    eperlist = ['ἤπερ']
    
    
    # Initialize counts for the requested conditions
    count_eper_forms = 0
    count_AuxY_c = 0
    count_AuxY_d = 0
    count_AuxY_b = 0
    count_AuxY_not = 0
    count_AuxX_c = 0
    count_AuxX_d = 0
    count_AuxX_b = 0
    count_AuxX_not = 0
    count_AuxZ_c = 0
    count_AuxZ_d = 0
    count_AuxZ_b = 0
    count_AuxZ_not = 0
    count_AuxC_c = 0
    count_AuxC_d = 0
    count_AuxC_b = 0
    count_AuxC_not = 0
    count_COORD_c = 0
    count_COORD_d = 0
    count_COORD_b = 0
    count_COORD_not = 0
    count_not_relation = 0

    for df in df_list:
        modified = False  # track if the dataframe has been modified

        for index, row in df.iterrows():
            postag = row['@postag']
            
            # If the form is in the kai list, count it
            if row['@form'] in eperlist:
                count_eper_forms += 1

                # Check the '@relation' and '@postag' for the specified conditions
                relation = row['@relation']
                if relation == 'AuxY':
                    if postag[0] == 'c':
                        count_AuxY_c += 1
                    elif postag[0] == 'd':
                        count_AuxY_d += 1
                    elif postag[0] == 'b':
                        count_AuxY_b += 1
                    else:
                        count_AuxY_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxX':
                    if postag[0] == 'c':
                        count_AuxX_c += 1
                    elif postag[0] == 'd':
                        count_AuxX_d += 1
                    elif postag[0] == 'b':
                        count_AuxX_b += 1
                    else:
                        count_AuxX_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxZ':
                    if postag[0] == 'c':
                        count_AuxZ_c += 1
                    elif postag[0] == 'd':
                        count_AuxZ_d += 1
                    elif postag[0] == 'b':
                        count_AuxZ_b += 1
                    else:
                        count_AuxZ_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxC':
                    if postag[0] == 'c':
                        count_AuxC_c += 1
                    elif postag[0] == 'd':
                        count_AuxC_d += 1
                    elif postag[0] == 'b':
                        count_AuxC_b += 1
                    else:
                        count_AuxC_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'COORD':
                    if postag[0] == 'c':
                        count_COORD_c += 1
                    elif postag[0] == 'd':
                        count_COORD_d += 1
                    elif postag[0] == 'b':
                        count_COORD_b += 1
                    else:
                        count_COORD_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                else:
                    count_not_relation += 1
                    print([row['@form'], row['@lemma'], postag, row['@relation']])

    # Return the counts
    return {
        'total_eper_forms': count_eper_forms,
        'AuxY_c': count_AuxY_c,
        'AuxY_d': count_AuxY_d,
        'AuxY_b': count_AuxY_b,
        'AuxY_not' : count_AuxY_not,
        'AuxX_c': count_AuxX_c,
        'AuxX_d': count_AuxX_d,
        'AuxX_b': count_AuxX_b,
        'AuxX_not' : count_AuxX_not,
        'AuxZ_c': count_AuxZ_c,
        'AuxZ_d': count_AuxZ_d,
        'AuxZ_b': count_AuxZ_b,
        'AuxZ_not' : count_AuxZ_not,
        'AuxC_c': count_AuxC_c,
        'AuxC_d': count_AuxC_d,
        'AuxC_b': count_AuxC_b,
        'AuxC_not' : count_AuxC_not,
        'COORD_c': count_COORD_c,
        'COORD_d': count_COORD_d,
        'COORD_b': count_COORD_b,
        'COORD_not' : count_COORD_not,
        'relation_not' : count_not_relation 
    }

In [ ]:
counteper_dataframes = [count_eper_anomalies(lis) for lis in dataframes]

#qui sto stampando solo gli else, quindi sto stampando solo quando o ho una not relation, o non ho bcd ma con una relation usuale

['ἤπερ', 'ἤ', 'd--------', 'ADV']


In [63]:
summed_result = sum_dicts(counteper_dataframes)

counteper_dataframes = pd.DataFrame(list(summed_result.items()), columns=['Key', 'Value'])

In [64]:
sum(counteper_dataframes['Value'])-3

3

In [65]:
counteper_dataframes


Key  Value
0   total_eper_forms      3
1             AuxY_c      0
2             AuxY_d      0
3             AuxY_b      0
4           AuxY_not      0
5             AuxX_c      0
6             AuxX_d      0
7             AuxX_b      0
8           AuxX_not      0
9             AuxZ_c      0
10            AuxZ_d      0
11            AuxZ_b      0
12          AuxZ_not      0
13            AuxC_c      1
14            AuxC_d      0
15            AuxC_b      1
16          AuxC_not      0
17           COORD_c      0
18           COORD_d      0
19           COORD_b      0
20         COORD_not      0
21      relation_not      1

In [67]:
'''frase 37
[20, 'ἢ', 'u--------'] memoralia xen'''

'''ci sono due eta i = interiezioni, vanno tenute!'''

'''ETA LE METTO TUTTE COME DIGGLE O INTERIEZIONI O C = CONGIUNZIONE


hper da aggiungere'''

'ETA LE METTO TUTTE COME DIGGLE O INTERIEZIONI O C = CONGIUNZIONE\n\n\nhper da aggiungere'

In [67]:
# Function to check and display anomalies in the postag
def replace_eper_anomalies(df_list):
  final_list = []
  eperlist = ['ἤπερ']

  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if len(postag) == 9 and row['@form'] in eperlist:
          if postag[0] == 'c' or postag[0] == 'd' or postag[0] == 'b':
          #modify the postag
            if row['@relation']== 'AuxY' or row['@relation']== 'AuxZ'or row['@relation']== 'AuxC' or row['@relation']== 'AuxX' or row['@relation']== 'COORD':
              row['@postag'] = 'c' + postag[1:9]
              df.at[index, '@postag'] = row['@postag']
              print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
              modified = True

    #append the dataframe whether modified or not
    final_list.append(df)

  return final_list

In [68]:
anomalieseper_dataframes = [replace_eper_anomalies(lis) for lis in dataframes]

['ἤπερ', 'ἤ', 'c--------', 'c--------', 'AuxC']
['ἤπερ', 'ἤ', 'b--------', 'c--------', 'AuxC']


In [ ]:
def count_eta_anomalies(df_list):
    final_list = []
    etalist = ['ἤ', 'ἢ']
    
    
    # Initialize counts for the requested conditions
    count_eta_forms = 0
    count_AuxY_c = 0
    count_AuxY_d = 0
    count_AuxY_b = 0
    count_AuxY_not = 0
    count_AuxX_c = 0
    count_AuxX_d = 0
    count_AuxX_b = 0
    count_AuxX_not = 0
    count_AuxZ_c = 0
    count_AuxZ_d = 0
    count_AuxZ_b = 0
    count_AuxZ_not = 0
    count_AuxC_c = 0
    count_AuxC_d = 0
    count_AuxC_b = 0
    count_AuxC_not = 0
    count_COORD_c = 0
    count_COORD_d = 0
    count_COORD_b = 0
    count_COORD_not = 0
    count_not_relation = 0

    for df in df_list:
        modified = False  # track if the dataframe has been modified

        for index, row in df.iterrows():
            postag = row['@postag']
            
            # If the form is in the kai list, count it
            if row['@form'] in etalist:
                count_eta_forms += 1

                # Check the '@relation' and '@postag' for the specified conditions
                relation = row['@relation']
                if relation == 'AuxY':
                    if postag[0] == 'c':
                        count_AuxY_c += 1
                    elif postag[0] == 'd':
                        count_AuxY_d += 1
                    elif postag[0] == 'b':
                        count_AuxY_b += 1
                    else:
                        count_AuxY_not += 1
                        print('->' , [row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxX':
                    if postag[0] == 'c':
                        count_AuxX_c += 1
                    elif postag[0] == 'd':
                        count_AuxX_d += 1
                    elif postag[0] == 'b':
                        count_AuxX_b += 1
                    else:
                        count_AuxX_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxZ':
                    if postag[0] == 'c':
                        count_AuxZ_c += 1
                    elif postag[0] == 'd':
                        count_AuxZ_d += 1
                    elif postag[0] == 'b':
                        count_AuxZ_b += 1
                    else:
                        count_AuxZ_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxC':
                    if postag[0] == 'c':
                        count_AuxC_c += 1
                    elif postag[0] == 'd':
                        count_AuxC_d += 1
                    elif postag[0] == 'b':
                        count_AuxC_b += 1
                    else:
                        count_AuxC_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'COORD':
                    if postag[0] == 'c':
                        count_COORD_c += 1
                    elif postag[0] == 'd':
                        count_COORD_d += 1
                    elif postag[0] == 'b':
                        count_COORD_b += 1
                    else:
                        count_COORD_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                else:
                    count_not_relation += 1
                    print([row['@form'], row['@lemma'], postag, row['@relation']])

    # Return the counts
    return {
        'total_eta_forms': count_eta_forms,
        'AuxY_c': count_AuxY_c,
        'AuxY_d': count_AuxY_d,
        'AuxY_b': count_AuxY_b,
        'AuxY_not' : count_AuxY_not,
        'AuxX_c': count_AuxX_c,
        'AuxX_d': count_AuxX_d,
        'AuxX_b': count_AuxX_b,
        'AuxX_not' : count_AuxX_not,
        'AuxZ_c': count_AuxZ_c,
        'AuxZ_d': count_AuxZ_d,
        'AuxZ_b': count_AuxZ_b,
        'AuxZ_not' : count_AuxZ_not,
        'AuxC_c': count_AuxC_c,
        'AuxC_d': count_AuxC_d,
        'AuxC_b': count_AuxC_b,
        'AuxC_not' : count_AuxC_not,
        'COORD_c': count_COORD_c,
        'COORD_d': count_COORD_d,
        'COORD_b': count_COORD_b,
        'COORD_not' : count_COORD_not,
        'relation_not' : count_not_relation 
    }

In [70]:
counteta_dataframes = [count_eta_anomalies(lis) for lis in dataframes]

['ἤ', 'ἤ2', 'i--------', 'AuxY']
['ἤ', 'ἤ2', 'i--------', 'AuxY']
['ἤ', 'ἤ2', 'i--------', 'AuxY']
['ἤ', 'ἤ2', 'i--------', 'AuxY']
['ἢ', 'ἤ', 'i--------', 'AuxY']
['ἢ', 'ἤ', 'i--------', 'AuxY']
['ἢ', ',', 'u--------', 'COORD']


In [71]:
summed_result = sum_dicts(counteta_dataframes)

counteta_dataframes = pd.DataFrame(list(summed_result.items()), columns=['Key', 'Value'])

In [72]:
sum(counteta_dataframes['Value'])-963

963

In [73]:
counteta_dataframes

Key  Value
0   total_eta_forms    963
1            AuxY_c    204
2            AuxY_d      2
3            AuxY_b     50
4          AuxY_not      6
5            AuxX_c      0
6            AuxX_d      0
7            AuxX_b      0
8          AuxX_not      0
9            AuxZ_c      0
10           AuxZ_d      0
11           AuxZ_b      0
12         AuxZ_not      0
13           AuxC_c    243
14           AuxC_d      0
15           AuxC_b      9
16         AuxC_not      0
17          COORD_c    360
18          COORD_d      1
19          COORD_b     87
20        COORD_not      1
21     relation_not      0

In [75]:
# Function to check and display anomalies in the postag
def replace_eta_anomalies(df_list):
  final_list = []
  etalist = ['ἤ', 'ἢ']

  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if len(postag) == 9 and row['@form'] in etalist:
          #modify the postag
          if postag[0] == 'c' or postag[0] == 'd' or postag[0] == 'b':
          #modify the postag
            if row['@relation']== 'AuxY' or row['@relation']== 'AuxZ'or row['@relation']== 'AuxC' or row['@relation']== 'AuxX' or row['@relation']== 'COORD':
              row['@postag'] = 'c' + postag[1:9]
              
          df.at[index, '@postag'] = row['@postag']
          print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
          modified = True

    #append the dataframe whether modified or not
    final_list.append(df)

  return final_list

In [76]:
anomalieseta_dataframes = [replace_eta_anomalies(lis) for lis in dataframes]

['ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
['ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
['ἢ', 'ἤ1', 'c--------', 'c--------', 'AuxC']
['ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
['ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
['ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
['ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
['ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
['ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
['ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
['ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
['ἢ', 'ἤ1', 'c--------', 'c--------', 'AuxY']
['ἢ', 'ἤ', 'b--------', 'c--------', 'COORD']
['ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
['ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
['ἢ', 'ἤ1', 'c--------', 'c--------', 'AuxY']
['ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
['ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
['ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
['ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
['ἢ', 'ἤ1', 'c--------', 'c--------', 'COORD']
['ἢ', 'ἤ1', 'c---

In [77]:
# Function to check and display anomalies in the postag
def replace_etaU_anomalies(df_list):
  final_list = []
  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if len(postag) == 9 and postag[0] == 'u' and row['@form'] == 'ἢ':
          #modify the postag
          row['@postag'] = 'c' + postag[1:9]
          print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
          #update the dataframe .at è come dire append ma per i dataframe
          df.at[index, '@postag'] = row['@postag']
          modified = True

    #append the dataframe whether modified or not
    final_list.append(df)

  return final_list

#'output_pedalion_con_relation'

In [78]:
anomaliesetaU_dataframes = [replace_etaU_anomalies(lis) for lis in dataframes]

['ἢ', ',', 'u--------', 'c--------', 'COORD']


In [79]:
#CRASI PROBLEMA

In [80]:

def print_crasi(df_list):
    vocali_spirito_accento = ['ἄ', 'ἔ', 'ἤ', 'ἴ', 'ὄ', 'ὔ', 'ἆ', 'ἦ', 'ἶ', 'ὖ','ἀ', 'ἐ', 'ἠ', 'ἰ', 'ὀ', 'ὐ', 'ἁ', 'ἡ', 'ἱ', 'ὁ', 'ὑ']
    vocali_greche_complete = [
    # Vocali greche di base
    'α', 'ε', 'η', 'ι', 'ο', 'υ', 'ω',
    'Α', 'Ε', 'Η', 'Ι', 'Ο', 'Υ', 'Ω',

    # Con spirito aspro
    'ἁ', 'ἑ', 'ἡ', 'ἱ', 'ὁ', 'ὑ', 'ὡ',
    'Ἁ', 'Ἑ', 'Ἡ', 'Ἱ', 'Ὁ', 'Ὑ', 'Ὡ',

    # Con spirito dolce
    'ἀ', 'ἐ', 'ἠ', 'ἰ', 'ὀ', 'ὐ', 'ὠ',
    'Ἀ', 'Ἐ', 'Ἠ', 'Ἰ', 'Ὀ', 'Ὠ',

    # Con accento acuto
    'ά', 'έ', 'ή', 'ί', 'ό', 'ύ', 'ώ',
    'Ά', 'Έ', 'Ή', 'Ί', 'Ό', 'Ύ', 'Ώ',

    # Con accento circonflesso
    'ᾶ', 'ῆ', 'ῖ', 'ῦ', 'ῶ',
    'ᾶ', 'ῆ', 'ῖ', 'ῦ', 'ῶ',

    # Con accento acuto e spirito aspro
    'ἄ', 'ἔ', 'ἤ', 'ἴ', 'ὄ', 'ὔ', 'ὤ',
    'Ἄ', 'Ἔ', 'Ἤ', 'Ἴ', 'Ὄ', 'Ὕ', 'Ὤ',

    # Con accento acuto e spirito dolce
    'ἂ', 'ἒ', 'ἢ', 'ἲ', 'ὂ', 'ὒ', 'ὢ',
    'Ἂ', 'Ἒ', 'Ἢ', 'Ἲ', 'Ὂ', 'Ὓ', 'Ὢ',

    # Con accento circonflesso e spirito dolce
    'ἆ', 'ἦ', 'ἶ', 'ὖ', 'ὦ',
    'Ἆ', 'Ἦ', 'Ἶ', 'Ὦ',

    # Con accento circonflesso e spirito aspro
    'ἇ', 'ἧ', 'ἷ', 'ὗ', 'ὧ',
    'Ἇ', 'Ἧ', 'Ἷ', 'Ὧ'
]

    for i,df in enumerate(df_list):
        for index, row in df.iterrows():
            
            postag = row['@postag']
            if len(row['@form'])>=3:
                if not (row['@form'][0] in vocali_greche_complete and row['@form'][1] in vocali_greche_complete):
                    if row['@form'][1] in vocali_spirito_accento or row['@form'][2] in vocali_spirito_accento:
                        print('frase', i)
                        print([index, row['@form'], row['@lemma'], postag, row['@relation']])

In [81]:

lis_dir = os.listdir("C:/Users/lcolo/Desktop/TESI/CODICI DEFINITIVI DIZ UNICO-2/PEDALION/output_pedalion_con_relation")
for j,lis in enumerate(dataframes):
    print('Opera',lis_dir[j])
    print_crasi(lis)

Opera aeneas.xml
Opera aesop1.xml
frase 51
[13, 'κἄν', 'κἄν', 'b--------', 'AuxC']
frase 144
[10, 'κἄν', 'κἄν', 'c--------', 'AuxC']
frase 323
[5, 'κἄν', 'κἄν', 'c--------', 'AuxC']
frase 401
[8, 'κἄν', 'κἄν', 'c--------', 'AuxC']
frase 462
[10, 'κἄν', 'κἄν', 'c--------', 'AuxC']
frase 472
[12, 'κἄν', 'κἄν', 'c--------', 'AuxC']
frase 476
[11, 'κἄν', 'κἄν', 'c--------', 'AuxC']
frase 538
[10, 'κἄν', 'κἄν', 'c--------', 'AuxC']
Opera charb1.xml
Opera chion.xml
Opera crit.xml
frase 55
[9, 'τἀργύριόν', 'ἀργύριον', 'n-s---nn-', 'SBJ']
frase 58
[10, 'τἀμά', 'ἐμός', 'a-p---na-', 'OBJ']
frase 86
[6, 'τἀνθρώπεια', 'ἀνθρώπειος', 'a-p---nn-', 'SBJ']
frase 109
[2, 'τἆλλα', 'ἄλλος', 'p-p---nn-', 'SBJ']
frase 133
[8, 'ταὐτόν', 'αὐτός', 'p-s---nn-', 'PNOM']
frase 215
[15, 'τἆλλα', 'ἄλλος', 'p-p---na-', 'ADV']
Opera epictetus.xml
frase 12
[5, 'τἆλλα', 'ἄλλος', 'p-p---na-', 'OBJ_CO']
frase 23
[8, 'κἀκεῖνα', 'κἀκεῖνος', 'a-p---na-', 'OBJ']
frase 95
[0, 'κἄν', 'κἄν', 'c--------', 'AuxC']
frase 142
[0, '

In [82]:
'''dic = {
    'κἄν': ['καί', 'ἄν'],
    'τἀργύριόν': ['τὸ', 'ἀργύριον'],
    'τἀμά': ['τὰ', 'ἐμά'],
    'τἀνθρώπεια': ['τὰ', 'ἀνθρώπεια'],
    'τἆλλα': ['τὰ', 'ἄλλα'],
    'ταὐτόν': ['τὸ', 'αὐτόν'],
    'τἆνατία': ['τὰ', 'ἐναντία'],
    'τἆμπαλιν': ['τὰ', 'ἔμπαλιν'],
    'κἀκεῖνα': ['καί', 'ἐκεῖνα'],
    'κἀμέ': ['καί', 'ἐμέ'],
    'κἀγώ': ['καί', 'ἐγώ'],
    'κἀμοῦ': ['καί', 'ἐμοῦ'],
    'κἀνταῦθα': ['καί', 'ἐνταῦθα'],
    'κἀκεῖθεν': ['καί', 'ἐκεῖθεν'],
    'τἆγαθά': ['τὰ', 'ἀγαθά'],
    'τοὐναντίον': ['τὸ', 'ἐναντίον'],
    'τοὔνομα': ['τὸ', 'ὄνομα'],
    'κἀκείνῃ': ['καί', 'ἐκείνῃ'],
    'κἀκεῖνο': ['καί', 'ἐκεῖνο']
}'''

"dic = {\n    'κἄν': ['καί', 'ἄν'],\n    'τἀργύριόν': ['τὸ', 'ἀργύριον'],\n    'τἀμά': ['τὰ', 'ἐμά'],\n    'τἀνθρώπεια': ['τὰ', 'ἀνθρώπεια'],\n    'τἆλλα': ['τὰ', 'ἄλλα'],\n    'ταὐτόν': ['τὸ', 'αὐτόν'],\n    'τἆνατία': ['τὰ', 'ἐναντία'],\n    'τἆμπαλιν': ['τὰ', 'ἔμπαλιν'],\n    'κἀκεῖνα': ['καί', 'ἐκεῖνα'],\n    'κἀμέ': ['καί', 'ἐμέ'],\n    'κἀγώ': ['καί', 'ἐγώ'],\n    'κἀμοῦ': ['καί', 'ἐμοῦ'],\n    'κἀνταῦθα': ['καί', 'ἐνταῦθα'],\n    'κἀκεῖθεν': ['καί', 'ἐκεῖθεν'],\n    'τἆγαθά': ['τὰ', 'ἀγαθά'],\n    'τοὐναντίον': ['τὸ', 'ἐναντίον'],\n    'τοὔνομα': ['τὸ', 'ὄνομα'],\n    'κἀκείνῃ': ['καί', 'ἐκείνῃ'],\n    'κἀκεῖνο': ['καί', 'ἐκεῖνο']\n}"

In [83]:
def print_kan(df_list):
    
    for i,df in enumerate(df_list):
        for index, row in df.iterrows():
            
            postag = row['@postag']
            if row['@form'] == 'κἄν':
               print('frase', i)
               print([index, row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])

In [84]:

lis_dir = os.listdir("C:/Users/lcolo/Desktop/TESI/CODICI DEFINITIVI DIZ UNICO-2/PEDALION/output_pedalion_con_relation")
for j,lis in enumerate(dataframes):
    print('Opera',lis_dir[j])
    print_kan(lis)

Opera aeneas.xml
Opera aesop1.xml
frase 51
[13, 'κἄν', 'κἄν', 'b--------', 'b--------', 'AuxC']
frase 144
[10, 'κἄν', 'κἄν', 'c--------', 'c--------', 'AuxC']
frase 323
[5, 'κἄν', 'κἄν', 'c--------', 'c--------', 'AuxC']
frase 401
[8, 'κἄν', 'κἄν', 'c--------', 'c--------', 'AuxC']
frase 462
[10, 'κἄν', 'κἄν', 'c--------', 'c--------', 'AuxC']
frase 472
[12, 'κἄν', 'κἄν', 'c--------', 'c--------', 'AuxC']
frase 476
[11, 'κἄν', 'κἄν', 'c--------', 'c--------', 'AuxC']
frase 538
[10, 'κἄν', 'κἄν', 'c--------', 'c--------', 'AuxC']
Opera charb1.xml
Opera chion.xml
Opera crit.xml
Opera epictetus.xml
frase 95
[0, 'κἄν', 'κἄν', 'c--------', 'c--------', 'AuxC']
frase 158
[2, 'κἄν', 'κἄν', 'c--------', 'c--------', 'AuxZ']
Opera epicurus1.xml
Opera genesis1.xml
Opera genesis2.xml
Opera genesis3.xml
Opera heron.xml
Opera iso.xml
Opera julian.xml
frase 36
[4, 'κἄν', 'κἄν', 'c--------', 'c--------', 'AuxC']
Opera longus.xml
Opera lucian_lis.xml
Opera lucian_prometheus.xml
Opera lucian_symposion.

In [85]:
def count_kan_anomalies(df_list):
    final_list = []
    kanlist = ['κἄν']
    
    
    # Initialize counts for the requested conditions
    count_kan_forms = 0
    count_AuxY_c = 0
    count_AuxY_d = 0
    count_AuxY_b = 0
    count_AuxY_not = 0
    count_AuxX_c = 0
    count_AuxX_d = 0
    count_AuxX_b = 0
    count_AuxX_not = 0
    count_AuxZ_c = 0
    count_AuxZ_d = 0
    count_AuxZ_b = 0
    count_AuxZ_not = 0
    count_AuxC_c = 0
    count_AuxC_d = 0
    count_AuxC_b = 0
    count_AuxC_not = 0
    count_COORD_c = 0
    count_COORD_d = 0
    count_COORD_b = 0
    count_COORD_not = 0
    count_not_relation = 0

    for df in df_list:
        modified = False  # track if the dataframe has been modified

        for index, row in df.iterrows():
            postag = row['@postag']
            
            # If the form is in the kai list, count it
            if row['@form'] in kanlist:
                count_kan_forms += 1

                # Check the '@relation' and '@postag' for the specified conditions
                relation = row['@relation']
                if relation == 'AuxY':
                    if postag[0] == 'c':
                        count_AuxY_c += 1
                    elif postag[0] == 'd':
                        count_AuxY_d += 1
                    elif postag[0] == 'b':
                        count_AuxY_b += 1
                    else:
                        count_AuxY_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxX':
                    if postag[0] == 'c':
                        count_AuxX_c += 1
                    elif postag[0] == 'd':
                        count_AuxX_d += 1
                    elif postag[0] == 'b':
                        count_AuxX_b += 1
                    else:
                        count_AuxX_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxZ':
                    if postag[0] == 'c':
                        count_AuxZ_c += 1
                    elif postag[0] == 'd':
                        count_AuxZ_d += 1
                    elif postag[0] == 'b':
                        count_AuxZ_b += 1
                    else:
                        count_AuxZ_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxC':
                    if postag[0] == 'c':
                        count_AuxC_c += 1
                    elif postag[0] == 'd':
                        count_AuxC_d += 1
                    elif postag[0] == 'b':
                        count_AuxC_b += 1
                    else:
                        count_AuxC_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'COORD':
                    if postag[0] == 'c':
                        count_COORD_c += 1
                    elif postag[0] == 'd':
                        count_COORD_d += 1
                    elif postag[0] == 'b':
                        count_COORD_b += 1
                    else:
                        count_COORD_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                else:
                    count_not_relation += 1
                    print([row['@form'], row['@lemma'], postag, row['@relation']])

    # Return the counts
    return {
        'total_kan_forms': count_kan_forms,
        'AuxY_c': count_AuxY_c,
        'AuxY_d': count_AuxY_d,
        'AuxY_b': count_AuxY_b,
        'AuxY_not' : count_AuxY_not,
        'AuxX_c': count_AuxX_c,
        'AuxX_d': count_AuxX_d,
        'AuxX_b': count_AuxX_b,
        'AuxX_not' : count_AuxX_not,
        'AuxZ_c': count_AuxZ_c,
        'AuxZ_d': count_AuxZ_d,
        'AuxZ_b': count_AuxZ_b,
        'AuxZ_not' : count_AuxZ_not,
        'AuxC_c': count_AuxC_c,
        'AuxC_d': count_AuxC_d,
        'AuxC_b': count_AuxC_b,
        'AuxC_not' : count_AuxC_not,
        'COORD_c': count_COORD_c,
        'COORD_d': count_COORD_d,
        'COORD_b': count_COORD_b,
        'COORD_not' : count_COORD_not,
        'relation_not' : count_not_relation 
    }

In [86]:
countkan_dataframes = [count_kan_anomalies(lis) for lis in dataframes]

In [87]:
summed_result = sum_dicts(countkan_dataframes)

countkan_dataframes = pd.DataFrame(list(summed_result.items()), columns=['Key', 'Value'])

In [88]:
sum(countkan_dataframes['Value'])-17

13

In [89]:
countkan_dataframes

Key  Value
0   total_kan_forms     15
1            AuxY_c      1
2            AuxY_d      0
3            AuxY_b      0
4          AuxY_not      0
5            AuxX_c      0
6            AuxX_d      0
7            AuxX_b      0
8          AuxX_not      0
9            AuxZ_c      1
10           AuxZ_d      0
11           AuxZ_b      0
12         AuxZ_not      0
13           AuxC_c     12
14           AuxC_d      0
15           AuxC_b      1
16         AuxC_not      0
17          COORD_c      0
18          COORD_d      0
19          COORD_b      0
20        COORD_not      0
21     relation_not      0

In [90]:
# Function to check and display anomalies in the postag
def replace_kan_anomalies(df_list):
  final_list = []
  kanlist = ['κἄν']

  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if len(postag) == 9 and row['@form'] in kanlist:
          if postag[0] == 'c' or postag[0] == 'd' or postag[0] == 'b':
          #modify the postag
           if row['@relation']== 'AuxY' or row['@relation']== 'AuxZ' or row['@relation']== 'AuxC' or row['@relation']== 'AuxX' or row['@relation']== 'COORD':
              row['@postag'] = 'c' + postag[1:9]
          df.at[index, '@postag'] = row['@postag']
          print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
          modified = True

    #append the dataframe whether modified or not
    final_list.append(df)

  return final_list

In [91]:
anomalieskan_dataframes = [replace_kan_anomalies(lis) for lis in dataframes]

['κἄν', 'κἄν', 'b--------', 'c--------', 'AuxC']
['κἄν', 'κἄν', 'c--------', 'c--------', 'AuxC']
['κἄν', 'κἄν', 'c--------', 'c--------', 'AuxC']
['κἄν', 'κἄν', 'c--------', 'c--------', 'AuxC']
['κἄν', 'κἄν', 'c--------', 'c--------', 'AuxC']
['κἄν', 'κἄν', 'c--------', 'c--------', 'AuxC']
['κἄν', 'κἄν', 'c--------', 'c--------', 'AuxC']
['κἄν', 'κἄν', 'c--------', 'c--------', 'AuxC']
['κἄν', 'κἄν', 'c--------', 'c--------', 'AuxC']
['κἄν', 'κἄν', 'c--------', 'c--------', 'AuxZ']
['κἄν', 'κἄν', 'c--------', 'c--------', 'AuxC']
['κἄν', 'κἄν', 'c--------', 'c--------', 'AuxY']
['κἄν', 'κἄν', 'c--------', 'c--------', 'AuxC']
['κἄν', 'κἄν', 'c--------', 'c--------', 'AuxC']
['κἄν', 'κἄν', 'c--------', 'c--------', 'AuxC']


In [92]:
def print_alla(df_list):
    alla = ['ἀλλʼ', 'ἀλλά', 'ἀλλὰ', 'ἀλλ’']
    for i,df in enumerate(df_list):
        for index, row in df.iterrows():
            
            postag = row['@postag']
            if row['@form'] in alla:
               print('frase', i)
               print([index, row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])

In [93]:
#salvare la lista di directory
lis_dir = os.listdir("C:/Users/lcolo/Desktop/TESI/CODICI DEFINITIVI DIZ UNICO-2/PEDALION/output_pedalion_con_relation")
for j,lis in enumerate(dataframes):
    print('Opera',lis_dir[j])
    print_alla(lis)

Opera aeneas.xml
frase 1
[26, 'ἀλλὰ', 'ἀλλά', 'd--------', 'd--------', 'COORD']
frase 2
[16, 'ἀλλὰ', 'ἀλλά', 'd--------', 'd--------', 'COORD']
frase 3
[7, 'ἀλλ’', 'ἀλλά', 'c--------', 'c--------', 'AuxY']
frase 58
[6, 'ἀλλὰ', 'ἀλλά', 'd--------', 'd--------', 'COORD']
frase 58
[37, 'ἀλλὰ', 'ἀλλά', 'd--------', 'd--------', 'AuxY']
frase 61
[13, 'ἀλλ’', 'ἀλλά', 'c--------', 'c--------', 'COORD']
frase 65
[17, 'ἀλλ’', 'ἀλλά', 'c--------', 'c--------', 'COORD']
frase 84
[11, 'ἀλλ’', 'ἀλλά', 'b--------', 'b--------', 'COORD']
frase 91
[4, 'ἀλλ’', 'ἀλλά', 'c--------', 'c--------', 'COORD']
frase 102
[19, 'ἀλλ’', 'ἀλλά', 'c--------', 'c--------', 'COORD']
frase 116
[0, 'ἀλλ’', 'ἀλλά', 'c--------', 'c--------', 'AuxY']
frase 149
[21, 'ἀλλ’', 'ἀλλά', 'c--------', 'c--------', 'COORD']
frase 158
[14, 'ἀλλὰ', 'ἀλλά', 'd--------', 'd--------', 'COORD']
frase 179
[0, 'ἀλλὰ', 'ἀλλά', 'd--------', 'd--------', 'AuxY']
frase 190
[14, 'ἀλλ’', 'ἀλλά', 'c--------', 'c--------', 'COORD']
frase 196
[8, 

In [94]:
def count_alla_anomalies(df_list):
    final_list = []
    alla_list = ['ἀλλʼ', 'ἀλλά', 'ἀλλὰ', 'ἀλλ’']
    
    
    # Initialize counts for the requested conditions
    count_alla_forms = 0
    count_AuxY_c = 0
    count_AuxY_d = 0
    count_AuxY_b = 0
    count_AuxY_not = 0
    count_AuxX_c = 0
    count_AuxX_d = 0
    count_AuxX_b = 0
    count_AuxX_not = 0
    count_AuxZ_c = 0
    count_AuxZ_d = 0
    count_AuxZ_b = 0
    count_AuxZ_not = 0
    count_AuxC_c = 0
    count_AuxC_d = 0
    count_AuxC_b = 0
    count_AuxC_not = 0
    count_COORD_c = 0
    count_COORD_d = 0
    count_COORD_b = 0
    count_COORD_not = 0
    count_not_relation = 0

    for df in df_list:
        modified = False  # track if the dataframe has been modified

        for index, row in df.iterrows():
            postag = row['@postag']
            
            # If the form is in the kai list, count it
            if row['@form'] in alla_list:
                count_alla_forms += 1

                # Check the '@relation' and '@postag' for the specified conditions
                relation = row['@relation']
                if relation == 'AuxY':
                    if postag[0] == 'c':
                        count_AuxY_c += 1
                    elif postag[0] == 'd':
                        count_AuxY_d += 1
                    elif postag[0] == 'b':
                        count_AuxY_b += 1
                    else:
                        count_AuxY_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxX':
                    if postag[0] == 'c':
                        count_AuxX_c += 1
                    elif postag[0] == 'd':
                        count_AuxX_d += 1
                    elif postag[0] == 'b':
                        count_AuxX_b += 1
                    else:
                        count_AuxX_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxZ':
                    if postag[0] == 'c':
                        count_AuxZ_c += 1
                    elif postag[0] == 'd':
                        count_AuxZ_d += 1
                    elif postag[0] == 'b':
                        count_AuxZ_b += 1
                    else:
                        count_AuxZ_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxC':
                    if postag[0] == 'c':
                        count_AuxC_c += 1
                    elif postag[0] == 'd':
                        count_AuxC_d += 1
                    elif postag[0] == 'b':
                        count_AuxC_b += 1
                    else:
                        count_AuxC_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'COORD':
                    if postag[0] == 'c':
                        count_COORD_c += 1
                    elif postag[0] == 'd':
                        count_COORD_d += 1
                    elif postag[0] == 'b':
                        count_COORD_b += 1
                    else:
                        count_COORD_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                else:
                    count_not_relation += 1
                    print([row['@form'], row['@lemma'], postag, row['@relation']])

    # Return the counts
    return {
        'total_alla_forms': count_alla_forms,
        'AuxY_c': count_AuxY_c,
        'AuxY_d': count_AuxY_d,
        'AuxY_b': count_AuxY_b,
        'AuxY_not' : count_AuxY_not,
        'AuxX_c': count_AuxX_c,
        'AuxX_d': count_AuxX_d,
        'AuxX_b': count_AuxX_b,
        'AuxX_not' : count_AuxX_not,
        'AuxZ_c': count_AuxZ_c,
        'AuxZ_d': count_AuxZ_d,
        'AuxZ_b': count_AuxZ_b,
        'AuxZ_not' : count_AuxZ_not,
        'AuxC_c': count_AuxC_c,
        'AuxC_d': count_AuxC_d,
        'AuxC_b': count_AuxC_b,
        'AuxC_not' : count_AuxC_not,
        'COORD_c': count_COORD_c,
        'COORD_d': count_COORD_d,
        'COORD_b': count_COORD_b,
        'COORD_not' : count_COORD_not,
        'relation_not' : count_not_relation 
    }

In [95]:
countalla_dataframes = [count_alla_anomalies(lis) for lis in dataframes]

In [96]:
summed_result = sum_dicts(countalla_dataframes)

countalla_dataframes = pd.DataFrame(list(summed_result.items()), columns=['Key', 'Value'])

In [97]:
sum(countalla_dataframes['Value'])-1037

905

In [98]:
countalla_dataframes

Key  Value
0   total_alla_forms    971
1             AuxY_c    246
2             AuxY_d     94
3             AuxY_b     75
4           AuxY_not      0
5             AuxX_c      0
6             AuxX_d      0
7             AuxX_b      0
8           AuxX_not      0
9             AuxZ_c      0
10            AuxZ_d      0
11            AuxZ_b      1
12          AuxZ_not      0
13            AuxC_c      2
14            AuxC_d      0
15            AuxC_b      0
16          AuxC_not      0
17           COORD_c    379
18           COORD_d      4
19           COORD_b    170
20         COORD_not      0
21      relation_not      0

In [99]:
# Function to check and display anomalies in the postag
def replace_alla_anomalies(df_list):
  final_list = []
  allalist = ['ἀλλʼ', 'ἀλλά', 'ἀλλὰ', 'ἀλλ’']

  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if len(postag) == 9 and row['@form'] in allalist:
          if postag[0] == 'c' or postag[0] == 'd' or postag[0] == 'b':
          #modify the postag
            if row['@relation']== 'AuxY' or row['@relation']== 'AuxZ'or row['@relation']== 'AuxC' or row['@relation']== 'AuxX' or row['@relation']== 'COORD':
              row['@postag'] = 'c' + postag[1:9]
          df.at[index, '@postag'] = row['@postag']
          print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
          modified = True

    #append the dataframe whether modified or not
    final_list.append(df)

  return final_list

In [100]:
anomaliesalla_dataframes = [replace_alla_anomalies(lis) for lis in dataframes]

['ἀλλὰ', 'ἀλλά', 'd--------', 'c--------', 'COORD']
['ἀλλὰ', 'ἀλλά', 'd--------', 'c--------', 'COORD']
['ἀλλ’', 'ἀλλά', 'c--------', 'c--------', 'AuxY']
['ἀλλὰ', 'ἀλλά', 'd--------', 'c--------', 'COORD']
['ἀλλὰ', 'ἀλλά', 'd--------', 'c--------', 'AuxY']
['ἀλλ’', 'ἀλλά', 'c--------', 'c--------', 'COORD']
['ἀλλ’', 'ἀλλά', 'c--------', 'c--------', 'COORD']
['ἀλλ’', 'ἀλλά', 'b--------', 'c--------', 'COORD']
['ἀλλ’', 'ἀλλά', 'c--------', 'c--------', 'COORD']
['ἀλλ’', 'ἀλλά', 'c--------', 'c--------', 'COORD']
['ἀλλ’', 'ἀλλά', 'c--------', 'c--------', 'AuxY']
['ἀλλ’', 'ἀλλά', 'c--------', 'c--------', 'COORD']
['ἀλλὰ', 'ἀλλά', 'd--------', 'c--------', 'COORD']
['ἀλλὰ', 'ἀλλά', 'd--------', 'c--------', 'AuxY']
['ἀλλ’', 'ἀλλά', 'c--------', 'c--------', 'COORD']
['ἀλλ’', 'ἀλλά', 'c--------', 'c--------', 'COORD']
['ἀλλὰ', 'ἀλλά', 'd--------', 'c--------', 'AuxY']
['ἀλλ’', 'ἀλλά', 'c--------', 'c--------', 'COORD']
['ἀλλὰ', 'ἀλλά', 'c--------', 'c--------', 'COORD']
['ἀλλὰ', 'ἀλλά', 

In [101]:
'''File 898
['ἦ', 'καί', 'ἀρσενικόν', 'ἡμῖν', 'ἀφίκατε', ';']
[('ἦ', 'b--------', "Unexpected character 'b' at position 1"),
 
 [('Ασξδ', 'm-------', 'Incorrect length')]'''

'File 898\n[\'ἦ\', \'καί\', \'ἀρσενικόν\', \'ἡμῖν\', \'ἀφίκατε\', \';\']\n[(\'ἦ\', \'b--------\', "Unexpected character \'b\' at position 1"),\n \n [(\'Ασξδ\', \'m-------\', \'Incorrect length\')]'

In [102]:
"οὔθʼ" == 'οὔθ’'

False

In [103]:
def count_oute_anomalies(df_list):
    final_list = []
    oute_list = ["οὔτε", "μήτε","οὐτ'", "μὴτ'","οὔθʼ", "μὴθʼ",'μήθ’','μήτ’','οὔτ’','οὔτʼ','οὔθ’']
    
    
    # Initialize counts for the requested conditions
    count_oute_forms = 0
    count_AuxY_c = 0
    count_AuxY_d = 0
    count_AuxY_b = 0
    count_AuxY_not = 0
    count_AuxX_c = 0
    count_AuxX_d = 0
    count_AuxX_b = 0
    count_AuxX_not = 0
    count_AuxZ_c = 0
    count_AuxZ_d = 0
    count_AuxZ_b = 0
    count_AuxZ_not = 0
    count_AuxC_c = 0
    count_AuxC_d = 0
    count_AuxC_b = 0
    count_AuxC_not = 0
    count_COORD_c = 0
    count_COORD_d = 0
    count_COORD_b = 0
    count_COORD_not = 0
    count_not_relation = 0

    for df in df_list:
        modified = False  # track if the dataframe has been modified

        for index, row in df.iterrows():
            postag = row['@postag']
            
            # If the form is in the kai list, count it
            if row['@form'] in oute_list:
                count_oute_forms += 1

                # Check the '@relation' and '@postag' for the specified conditions
                relation = row['@relation']
                if relation == 'AuxY':
                    if postag[0] == 'c':
                        count_AuxY_c += 1
                    elif postag[0] == 'd':
                        count_AuxY_d += 1
                    elif postag[0] == 'b':
                        count_AuxY_b += 1
                    else:
                        count_AuxY_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxX':
                    if postag[0] == 'c':
                        count_AuxX_c += 1
                    elif postag[0] == 'd':
                        count_AuxX_d += 1
                    elif postag[0] == 'b':
                        count_AuxX_b += 1
                    else:
                        count_AuxX_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxZ':
                    if postag[0] == 'c':
                        count_AuxZ_c += 1
                    elif postag[0] == 'd':
                        count_AuxZ_d += 1
                    elif postag[0] == 'b':
                        count_AuxZ_b += 1
                    else:
                        count_AuxZ_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxC':
                    if postag[0] == 'c':
                        count_AuxC_c += 1
                    elif postag[0] == 'd':
                        count_AuxC_d += 1
                    elif postag[0] == 'b':
                        count_AuxC_b += 1
                    else:
                        count_AuxC_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'COORD':
                    if postag[0] == 'c':
                        count_COORD_c += 1
                    elif postag[0] == 'd':
                        count_COORD_d += 1
                    elif postag[0] == 'b':
                        count_COORD_b += 1
                    else:
                        count_COORD_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                else:
                    count_not_relation += 1
                    print([row['@form'], row['@lemma'], postag, row['@relation']])

    # Return the counts
    return {
        'total_oute_forms': count_oute_forms,
        'AuxY_c': count_AuxY_c,
        'AuxY_d': count_AuxY_d,
        'AuxY_b': count_AuxY_b,
        'AuxY_not' : count_AuxY_not,
        'AuxX_c': count_AuxX_c,
        'AuxX_d': count_AuxX_d,
        'AuxX_b': count_AuxX_b,
        'AuxX_not' : count_AuxX_not,
        'AuxZ_c': count_AuxZ_c,
        'AuxZ_d': count_AuxZ_d,
        'AuxZ_b': count_AuxZ_b,
        'AuxZ_not' : count_AuxZ_not,
        'AuxC_c': count_AuxC_c,
        'AuxC_d': count_AuxC_d,
        'AuxC_b': count_AuxC_b,
        'AuxC_not' : count_AuxC_not,
        'COORD_c': count_COORD_c,
        'COORD_d': count_COORD_d,
        'COORD_b': count_COORD_b,
        'COORD_not' : count_COORD_not,
        'relation_not' : count_not_relation 
    }

In [104]:
countoute_dataframes = [count_oute_anomalies(lis) for lis in dataframes]

['οὔτε', 'οὔτε', 'c--------', 'fAuxY']
['οὔτε', 'οὔτε', 'c--------', 'COORD_CO']
['οὔτ’', 'φιλέω', 'v2spia---', 'COORD']


In [105]:
summed_result = sum_dicts(countoute_dataframes)

countoute_dataframes = pd.DataFrame(list(summed_result.items()), columns=['Key', 'Value'])

In [106]:
sum(countoute_dataframes['Value'])-523

501

In [107]:
countoute_dataframes

Key  Value
0   total_oute_forms    512
1             AuxY_c    200
2             AuxY_d     24
3             AuxY_b     36
4           AuxY_not      0
5             AuxX_c      0
6             AuxX_d      0
7             AuxX_b      0
8           AuxX_not      0
9             AuxZ_c     17
10            AuxZ_d     13
11            AuxZ_b      0
12          AuxZ_not      0
13            AuxC_c      0
14            AuxC_d      0
15            AuxC_b      0
16          AuxC_not      0
17           COORD_c    165
18           COORD_d     17
19           COORD_b     37
20         COORD_not      1
21      relation_not      2

In [108]:
# Function to check and display anomalies in the postag
def replace_oute_anomalies(df_list):
  final_list = []
  outelist = ["οὔτε", "μήτε","οὐτ'", "μὴτ'","οὔθʼ", "μὴθʼ",'μήθ’','μήτ’','οὔτ’','οὔτʼ','οὔθ’']

  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if len(postag) == 9 and row['@form'] in outelist:
          if postag[0] == 'c' or postag[0] == 'd' or postag[0] == 'b':
            if row['@relation']== 'AuxY' or row['@relation']== 'AuxZ'or row['@relation']== 'AuxC' or row['@relation']== 'AuxX'or row['@relation']== 'COORD':
              row['@postag'] = 'c' + postag[1:9]
            #print([row['@lemma'], row['@form'], postag, row['@postag'],row['@relation']])
          
          #update the dataframe .at è come dire append ma per i dataframe
          df.at[index, '@postag'] = row['@postag']
          print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
          modified = True

    #append the dataframe whether modified or not
    final_list.append(df)

  return final_list

In [109]:
anomaliesoute_dataframes = [replace_oute_anomalies(lis) for lis in dataframes]

['μήτε', 'μήτε', 'd--------', 'c--------', 'AuxY']
['μήτε', 'μήτε', 'd--------', 'c--------', 'COORD']
['μήτε', 'μήτε', 'd--------', 'c--------', 'AuxY']
['μήτε', 'μήτε', 'd--------', 'c--------', 'COORD']
['μήτε', 'μήτε', 'd--------', 'c--------', 'AuxY']
['μήτε', 'μήτε', 'd--------', 'c--------', 'COORD']
['οὔθʼ', 'οὔτε', 'd--------', 'c--------', 'AuxY']
['οὔθʼ', 'οὔτε', 'c--------', 'c--------', 'AuxY']
['οὔθʼ', 'οὔτε', 'c--------', 'c--------', 'AuxY']
['οὔθʼ', 'οὔτε', 'b--------', 'c--------', 'COORD']
['οὔτε', 'οὔτε', 'c--------', 'c--------', 'fAuxY']
['οὔτʼ', 'οὔτε', 'b--------', 'c--------', 'COORD']
['οὔτε', 'οὔτε', 'd--------', 'c--------', 'AuxY']
['οὔτε', 'οὔτε', 'b--------', 'c--------', 'COORD']
['οὔτε', 'οὔτε', 'b--------', 'c--------', 'AuxY']
['οὔτε', 'οὔτε', 'b--------', 'c--------', 'COORD']
['μήτε', 'μήτε', 'b--------', 'c--------', 'AuxY']
['μήτε', 'μήτε', 'b--------', 'c--------', 'COORD']
['οὔτε', 'οὔτε', 'b--------', 'c--------', 'AuxY']
['οὔτε', 'οὔτε', 'b---

In [110]:
def count_eite_anomalies(df_list):
    final_list = []
    eite_list = ["εἴτε"]
    
    
    # Initialize counts for the requested conditions
    count_eite_forms = 0
    count_AuxY_c = 0
    count_AuxY_d = 0
    count_AuxY_b = 0
    count_AuxY_not = 0
    count_AuxX_c = 0
    count_AuxX_d = 0
    count_AuxX_b = 0
    count_AuxX_not = 0
    count_AuxZ_c = 0
    count_AuxZ_d = 0
    count_AuxZ_b = 0
    count_AuxZ_not = 0
    count_AuxC_c = 0
    count_AuxC_d = 0
    count_AuxC_b = 0
    count_AuxC_not = 0
    count_COORD_c = 0
    count_COORD_d = 0
    count_COORD_b = 0
    count_COORD_not = 0
    count_not_relation = 0

    for df in df_list:
        modified = False  # track if the dataframe has been modified

        for index, row in df.iterrows():
            postag = row['@postag']
            
            # If the form is in the kai list, count it
            if row['@form'] in eite_list:
                count_eite_forms += 1

                # Check the '@relation' and '@postag' for the specified conditions
                relation = row['@relation']
                if relation == 'AuxY':
                    if postag[0] == 'c':
                        count_AuxY_c += 1
                    elif postag[0] == 'd':
                        count_AuxY_d += 1
                    elif postag[0] == 'b':
                        count_AuxY_b += 1
                    else:
                        count_AuxY_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxX':
                    if postag[0] == 'c':
                        count_AuxX_c += 1
                    elif postag[0] == 'd':
                        count_AuxX_d += 1
                    elif postag[0] == 'b':
                        count_AuxX_b += 1
                    else:
                        count_AuxX_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxZ':
                    if postag[0] == 'c':
                        count_AuxZ_c += 1
                    elif postag[0] == 'd':
                        count_AuxZ_d += 1
                    elif postag[0] == 'b':
                        count_AuxZ_b += 1
                    else:
                        count_AuxZ_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxC':
                    if postag[0] == 'c':
                        count_AuxC_c += 1
                    elif postag[0] == 'd':
                        count_AuxC_d += 1
                    elif postag[0] == 'b':
                        count_AuxC_b += 1
                    else:
                        count_AuxC_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'COORD':
                    if postag[0] == 'c':
                        count_COORD_c += 1
                    elif postag[0] == 'd':
                        count_COORD_d += 1
                    elif postag[0] == 'b':
                        count_COORD_b += 1
                    else:
                        count_COORD_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                else:
                    count_not_relation += 1
                    print([row['@form'], row['@lemma'], postag, row['@relation']])

    # Return the counts
    return {
        'total_eite_forms': count_eite_forms,
        'AuxY_c': count_AuxY_c,
        'AuxY_d': count_AuxY_d,
        'AuxY_b': count_AuxY_b,
        'AuxY_not' : count_AuxY_not,
        'AuxX_c': count_AuxX_c,
        'AuxX_d': count_AuxX_d,
        'AuxX_b': count_AuxX_b,
        'AuxX_not' : count_AuxX_not,
        'AuxZ_c': count_AuxZ_c,
        'AuxZ_d': count_AuxZ_d,
        'AuxZ_b': count_AuxZ_b,
        'AuxZ_not' : count_AuxZ_not,
        'AuxC_c': count_AuxC_c,
        'AuxC_d': count_AuxC_d,
        'AuxC_b': count_AuxC_b,
        'AuxC_not' : count_AuxC_not,
        'COORD_c': count_COORD_c,
        'COORD_d': count_COORD_d,
        'COORD_b': count_COORD_b,
        'COORD_not' : count_COORD_not,
        'relation_not' : count_not_relation 
    }

In [111]:
counteite_dataframes = [count_eite_anomalies(lis) for lis in dataframes]

In [112]:
summed_result = sum_dicts(counteite_dataframes)

counteite_dataframes = pd.DataFrame(list(summed_result.items()), columns=['Key', 'Value'])

In [113]:
sum(counteite_dataframes['Value'])-53

53

In [114]:
counteite_dataframes

Key  Value
0   total_eite_forms     53
1             AuxY_c     12
2             AuxY_d      1
3             AuxY_b      3
4           AuxY_not      0
5             AuxX_c      0
6             AuxX_d      0
7             AuxX_b      0
8           AuxX_not      0
9             AuxZ_c      0
10            AuxZ_d      0
11            AuxZ_b      0
12          AuxZ_not      0
13            AuxC_c     17
14            AuxC_d      1
15            AuxC_b      0
16          AuxC_not      0
17           COORD_c     12
18           COORD_d      2
19           COORD_b      5
20         COORD_not      0
21      relation_not      0

In [115]:
# Function to check and display anomalies in the postag
def replace_eite_anomalies(df_list):
  final_list = []
  eitelist = ["εἴτε"]

  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if len(postag) == 9 and row['@form'] in eitelist:
          if postag[0] == 'c' or postag[0] == 'd' or postag[0] == 'b':
            if row['@relation']== 'AuxY' or row['@relation']== 'AuxZ'or row['@relation']== 'AuxC' or row['@relation']== 'AuxX'or row['@relation']== 'COORD':
              row['@postag'] = 'c' + postag[1:9]
          
          #update the dataframe .at è come dire append ma per i dataframe
          df.at[index, '@postag'] = row['@postag']
          print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
          modified = True

    #append the dataframe whether modified or not
    final_list.append(df)

  return final_list

In [116]:
anomalieseite_dataframes = [replace_eite_anomalies(lis) for lis in dataframes]

['εἴτε', 'εἴτε', 'd--------', 'c--------', 'AuxC']
['εἴτε', 'εἴτε', 'd--------', 'c--------', 'COORD']
['εἴτε', 'εἴτε', 'b--------', 'c--------', 'AuxY']
['εἴτε', 'εἴτε', 'b--------', 'c--------', 'COORD']
['εἴτε', 'εἴτε', 'c--------', 'c--------', 'AuxC']
['εἴτε', 'εἴτε', 'c--------', 'c--------', 'AuxC']
['εἴτε', 'εἴτε', 'c--------', 'c--------', 'AuxY']
['εἴτε', 'εἴτε', 'c--------', 'c--------', 'COORD']
['εἴτε', 'εἴτε', 'c--------', 'c--------', 'AuxC']
['εἴτε', 'εἴτε', 'c--------', 'c--------', 'COORD']
['εἴτε', 'εἴτε', 'c--------', 'c--------', 'AuxC']
['εἴτε', 'εἴτε', 'c--------', 'c--------', 'COORD']
['εἴτε', 'εἴτε', 'c--------', 'c--------', 'AuxY']
['εἴτε', 'εἴτε', 'c--------', 'c--------', 'AuxY']
['εἴτε', 'εἴτε', 'b--------', 'c--------', 'COORD']
['εἴτε', 'εἴτε', 'c--------', 'c--------', 'AuxC']
['εἴτε', 'εἴτε', 'b--------', 'c--------', 'COORD']
['εἴτε', 'εἴτε', 'b--------', 'c--------', 'AuxY']
['εἴτε', 'εἴτε', 'b--------', 'c--------', 'COORD']
['εἴτε', 'εἴτε', 'c----

In [117]:
def count_te_anomalies(df_list):
    final_list = []
    te_list = ["-τ'", "τ'", "τε", "-τ' ", "τ' ", "τε ", 'τέ','-θ’','θ’','-τ’','τ’','-τε','τʼ']
    
    
    # Initialize counts for the requested conditions
    count_te_forms = 0
    count_AuxY_c = 0
    count_AuxY_d = 0
    count_AuxY_b = 0
    count_AuxY_not = 0
    count_AuxX_c = 0
    count_AuxX_d = 0
    count_AuxX_b = 0
    count_AuxX_not = 0
    count_AuxZ_c = 0
    count_AuxZ_d = 0
    count_AuxZ_b = 0
    count_AuxZ_not = 0
    count_AuxC_c = 0
    count_AuxC_d = 0
    count_AuxC_b = 0
    count_AuxC_not = 0
    count_COORD_c = 0
    count_COORD_d = 0
    count_COORD_b = 0
    count_COORD_not = 0
    count_not_relation = 0

    for df in df_list:
        modified = False  # track if the dataframe has been modified

        for index, row in df.iterrows():
            postag = row['@postag']
            
            # If the form is in the kai list, count it
            if row['@form'] in te_list:
                count_te_forms += 1

                # Check the '@relation' and '@postag' for the specified conditions
                relation = row['@relation']
                if relation == 'AuxY':
                    if postag[0] == 'c':
                        count_AuxY_c += 1
                    elif postag[0] == 'd':
                        count_AuxY_d += 1
                    elif postag[0] == 'b':
                        count_AuxY_b += 1
                    else:
                        count_AuxY_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxX':
                    if postag[0] == 'c':
                        count_AuxX_c += 1
                    elif postag[0] == 'd':
                        count_AuxX_d += 1
                    elif postag[0] == 'b':
                        count_AuxX_b += 1
                    else:
                        count_AuxX_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxZ':
                    if postag[0] == 'c':
                        count_AuxZ_c += 1
                    elif postag[0] == 'd':
                        count_AuxZ_d += 1
                    elif postag[0] == 'b':
                        count_AuxZ_b += 1
                    else:
                        count_AuxZ_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxC':
                    if postag[0] == 'c':
                        count_AuxC_c += 1
                    elif postag[0] == 'd':
                        count_AuxC_d += 1
                    elif postag[0] == 'b':
                        count_AuxC_b += 1
                    else:
                        count_AuxC_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'COORD':
                    if postag[0] == 'c':
                        count_COORD_c += 1
                    elif postag[0] == 'd':
                        count_COORD_d += 1
                    elif postag[0] == 'b':
                        count_COORD_b += 1
                    else:
                        count_COORD_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                else:
                    count_not_relation += 1
                    print([row['@form'], row['@lemma'], postag, row['@relation']])

    # Return the counts
    return {
        'total_te_forms': count_te_forms,
        'AuxY_c': count_AuxY_c,
        'AuxY_d': count_AuxY_d,
        'AuxY_b': count_AuxY_b,
        'AuxY_not' : count_AuxY_not,
        'AuxX_c': count_AuxX_c,
        'AuxX_d': count_AuxX_d,
        'AuxX_b': count_AuxX_b,
        'AuxX_not' : count_AuxX_not,
        'AuxZ_c': count_AuxZ_c,
        'AuxZ_d': count_AuxZ_d,
        'AuxZ_b': count_AuxZ_b,
        'AuxZ_not' : count_AuxZ_not,
        'AuxC_c': count_AuxC_c,
        'AuxC_d': count_AuxC_d,
        'AuxC_b': count_AuxC_b,
        'AuxC_not' : count_AuxC_not,
        'COORD_c': count_COORD_c,
        'COORD_d': count_COORD_d,
        'COORD_b': count_COORD_b,
        'COORD_not' : count_COORD_not,
        'relation_not' : count_not_relation 
    }

In [118]:
countte_dataframes = [count_te_anomalies(lis) for lis in dataframes]

['τε', 'τε', 'c--------', 'MWE2']
['τε', 'τε', 'b--------', 'MWE']
['τ’', 'τε', 'c--------', 'MWE']
['τ’', 'τε', 'c--------', 'MWE']
['τ’', 'τε', 'c--------', 'MWE']
['τε', 'τε', 'c--------', 'MWE']
['τε', 'τε', 'c--------', 'MWE']
['τέ', 'τε', 'd--------', 'MWE']
['τ’', 'τε', 'c--------', 'MWE']
['τε', 'τε', 'd--------', 'MWE']
['τ’', 'τε', 'c--------', 'MWE']
['τε', 'τε', 'd--------', 'MWE']
['τε', 'τε', 'c--------', 'AUX']
['τε', 'τε', 'b--------', '!!!relation not recognized!!!MWE2']
['τε', 'τε', 'c--------', 'AUX']
['τε', 'τε', 'c--------', 'MWE']
['τε', 'τέ', 'c--------', 'ADV_CO']
['τε', 'τε', 'c--------', 'ATR']
['τε', 'τε', 'c--------', 'MWE']
['τε', 'τε', 'c--------', 'MWE']
['τέ', 'τε', 'c--------', 'MWE']


In [119]:
summed_result = sum_dicts(countte_dataframes)

countte_dataframes = pd.DataFrame(list(summed_result.items()), columns=['Key', 'Value'])

In [120]:
sum(countte_dataframes['Value'])-1611

1567

In [121]:
countte_dataframes

Key  Value
0   total_te_forms   1589
1           AuxY_c   1115
2           AuxY_d     36
3           AuxY_b    177
4         AuxY_not      0
5           AuxX_c      0
6           AuxX_d      0
7           AuxX_b      0
8         AuxX_not      0
9           AuxZ_c      2
10          AuxZ_d      4
11          AuxZ_b      1
12        AuxZ_not      0
13          AuxC_c      0
14          AuxC_d      0
15          AuxC_b      0
16        AuxC_not      0
17         COORD_c    197
18         COORD_d      3
19         COORD_b     33
20       COORD_not      0
21    relation_not     21

In [122]:
# Function to check and display anomalies in the postag
def replace_te_anomalies(df_list):
  final_list = []
  telist = ["-τ'", "τ'", "τε", "-τ' ", "τ' ", "τε ", 'τέ','-θ’','θ’','-τ’','τ’','-τε','τʼ']

  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if len(postag) == 9 and row['@form'] in telist:
          if postag[0] == 'c' or postag[0] == 'd' or postag[0] == 'b':
            if row['@relation']== 'AuxZ':
              row['@postag'] = 'd' + postag[1:9]
            elif row['@relation']== 'AuxC' or row['@relation']== 'COORD' or row['@relation']== 'AuxY'or row['@relation']== 'AuxX' :
               row['@postag'] = 'c' + postag[1:9]
            
          df.at[index, '@postag'] = row['@postag']
          print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
          modified = True

    #append the dataframe whether modified or not
    final_list.append(df)

  return final_list

In [123]:
anomalieste_dataframes = [replace_te_anomalies(lis) for lis in dataframes]

['τε', 'τε', 'c--------', 'c--------', 'AuxY']
['τε', 'τε', 'c--------', 'c--------', 'AuxY']
['τε', 'τε', 'c--------', 'c--------', 'AuxY']
['τε', 'τε', 'c--------', 'c--------', 'AuxY']
['τε', 'τε', 'c--------', 'c--------', 'AuxY']
['τε', 'τε', 'c--------', 'c--------', 'AuxY']
['τε', 'τε', 'c--------', 'c--------', 'AuxY']
['τε', 'τε', 'c--------', 'c--------', 'AuxY']
['τε', 'τε', 'c--------', 'c--------', 'AuxY']
['τε', 'τε', 'c--------', 'c--------', 'AuxY']
['τε', 'τε', 'c--------', 'c--------', 'AuxY']
['τε', 'τε', 'c--------', 'c--------', 'AuxY']
['τε', 'τε', 'c--------', 'c--------', 'COORD']
['τε', 'τε', 'c--------', 'c--------', 'AuxY']
['τε', 'τε', 'c--------', 'c--------', 'COORD']
['τε', 'τε', 'c--------', 'c--------', 'AuxY']
['τε', 'τε', 'c--------', 'c--------', 'AuxY']
['τε', 'τε', 'c--------', 'c--------', 'AuxY']
['τε', 'τε', 'c--------', 'c--------', 'MWE2']
['τε', 'τε', 'c--------', 'c--------', 'AuxY']
['τε', 'τε', 'c--------', 'c--------', 'COORD']
['τε', 'τε

In [124]:
def count_mende_anomalies(df_list):
    final_list = []
    mende_list = ['μέν', '-δέ', 'δέ','μὲν', 'δὲ', '-δʼ','-δ’','δʼ,','δ’','-δὲ','δʼ']
    
    
    # Initialize counts for the requested conditions
    count_mende_forms = 0
    count_AuxY_c = 0
    count_AuxY_d = 0
    count_AuxY_b = 0
    count_AuxY_not = 0
    count_AuxX_c = 0
    count_AuxX_d = 0
    count_AuxX_b = 0
    count_AuxX_not = 0
    count_AuxZ_c = 0
    count_AuxZ_d = 0
    count_AuxZ_b = 0
    count_AuxZ_not = 0
    count_AuxC_c = 0
    count_AuxC_d = 0
    count_AuxC_b = 0
    count_AuxC_not = 0
    count_COORD_c = 0
    count_COORD_d = 0
    count_COORD_b = 0
    count_COORD_not = 0
    count_not_relation = 0

    for df in df_list:
        modified = False  # track if the dataframe has been modified

        for index, row in df.iterrows():
            postag = row['@postag']
            
            # If the form is in the kai list, count it
            if row['@form'] in mende_list:
                count_mende_forms += 1

                # Check the '@relation' and '@postag' for the specified conditions
                relation = row['@relation']
                if relation == 'AuxY':
                    if postag[0] == 'c':
                        count_AuxY_c += 1
                    elif postag[0] == 'd':
                        count_AuxY_d += 1
                    elif postag[0] == 'b':
                        count_AuxY_b += 1
                    else:
                        count_AuxY_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxX':
                    if postag[0] == 'c':
                        count_AuxX_c += 1
                    elif postag[0] == 'd':
                        count_AuxX_d += 1
                    elif postag[0] == 'b':
                        count_AuxX_b += 1
                    else:
                        count_AuxX_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxZ':
                    if postag[0] == 'c':
                        count_AuxZ_c += 1
                    elif postag[0] == 'd':
                        count_AuxZ_d += 1
                    elif postag[0] == 'b':
                        count_AuxZ_b += 1
                    else:
                        count_AuxZ_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxC':
                    if postag[0] == 'c':
                        count_AuxC_c += 1
                    elif postag[0] == 'd':
                        count_AuxC_d += 1
                    elif postag[0] == 'b':
                        count_AuxC_b += 1
                    else:
                        count_AuxC_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'COORD':
                    if postag[0] == 'c':
                        count_COORD_c += 1
                    elif postag[0] == 'd':
                        count_COORD_d += 1
                    elif postag[0] == 'b':
                        count_COORD_b += 1
                    else:
                        count_COORD_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                else:
                    count_not_relation += 1
                    print([row['@form'], row['@lemma'], postag, row['@relation']])

    # Return the counts
    return {
        'total_mende_forms': count_mende_forms,
        'AuxY_c': count_AuxY_c,
        'AuxY_d': count_AuxY_d,
        'AuxY_b': count_AuxY_b,
        'AuxY_not' : count_AuxY_not,
        'AuxX_c': count_AuxX_c,
        'AuxX_d': count_AuxX_d,
        'AuxX_b': count_AuxX_b,
        'AuxX_not' : count_AuxX_not,
        'AuxZ_c': count_AuxZ_c,
        'AuxZ_d': count_AuxZ_d,
        'AuxZ_b': count_AuxZ_b,
        'AuxZ_not' : count_AuxZ_not,
        'AuxC_c': count_AuxC_c,
        'AuxC_d': count_AuxC_d,
        'AuxC_b': count_AuxC_b,
        'AuxC_not' : count_AuxC_not,
        'COORD_c': count_COORD_c,
        'COORD_d': count_COORD_d,
        'COORD_b': count_COORD_b,
        'COORD_not' : count_COORD_not,
        'relation_not' : count_not_relation 
    }

In [125]:
countmende_dataframes = [count_mende_anomalies(lis) for lis in dataframes]

['μὲν', 'μέν', 'd--------', 'ATR']
['δέ', 'δέ', 'd--------', 'AUX']
['δέ', 'δέ', 'd--------', 'AUX']
['δέ', 'δέ', 'd--------', 'AUX']
['δὲ', 'δέ', 'd--------', 'SBJ']
['δὲ', 'δέ', 'd--------', 'ADV']
['δὲ', 'δέ', 'd--------', 'COORD_CO']
['δ’', 'δέ', 'd--------', 'COORD_CO']


In [126]:
summed_result = sum_dicts(countmende_dataframes)

countmende_dataframes = pd.DataFrame(list(summed_result.items()), columns=['Key', 'Value'])

In [127]:
sum(countmende_dataframes['Value'])-6922

6566

In [128]:
countmende_dataframes

Key  Value
0   total_mende_forms   6744
1              AuxY_c      0
2              AuxY_d   4683
3              AuxY_b    611
4            AuxY_not      0
5              AuxX_c      0
6              AuxX_d      0
7              AuxX_b      0
8            AuxX_not      0
9              AuxZ_c      0
10             AuxZ_d     10
11             AuxZ_b      0
12           AuxZ_not      0
13             AuxC_c      0
14             AuxC_d      0
15             AuxC_b      0
16           AuxC_not      0
17            COORD_c      1
18            COORD_d   1017
19            COORD_b    414
20          COORD_not      0
21       relation_not      8

In [129]:
# Function to check and display anomalies in the postag

#ATTENZIONE CHE CAMBIA AUX C QUI!!!!

def replace_mende_anomalies(df_list):
  final_list = []
  mendelist = ['μέν', '-δέ', 'δέ','μὲν', 'δὲ', '-δʼ','-δ’','δʼ,','δ’','-δὲ','δʼ']

  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if len(postag) == 9 and row['@form'] in mendelist:
          if postag[0] == 'c' or postag[0] == 'd' or postag[0] == 'b':
            if row['@relation']== 'AuxY' or row['@relation']== 'AuxZ' or row['@relation']== 'AuxC'or   row['@relation']== 'COORD' or row['@relation']== 'AuxX':
              row['@postag'] = 'd' + postag[1:9]
       
          
          #update the dataframe .at è come dire append ma per i dataframe
          df.at[index, '@postag'] = row['@postag']
          print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
          modified = True

    #append the dataframe whether modified or not
    final_list.append(df)

  return final_list

In [130]:
anomaliesmende_dataframes = [replace_mende_anomalies(lis) for lis in dataframes]

['δὲ', 'δέ', 'd--------', 'd--------', 'AuxY']
['μὲν', 'μέν', 'd--------', 'd--------', 'AuxY']
['δὲ', 'δέ', 'd--------', 'd--------', 'COORD']
['δὲ', 'δέ', 'd--------', 'd--------', 'AuxY']
['μὲν', 'μέν', 'd--------', 'd--------', 'AuxY']
['δὲ', 'δέ', 'd--------', 'd--------', 'AuxY']
['μὲν', 'μέν', 'd--------', 'd--------', 'AuxY']
['δὲ', 'δέ', 'd--------', 'd--------', 'COORD']
['μὲν', 'μέν', 'd--------', 'd--------', 'AuxY']
['δὲ', 'δέ', 'd--------', 'd--------', 'AuxY']
['δὲ', 'δέ', 'd--------', 'd--------', 'AuxY']
['δὲ', 'δέ', 'd--------', 'd--------', 'AuxY']
['δὲ', 'δέ', 'd--------', 'd--------', 'AuxY']
['δὲ', 'δέ', 'd--------', 'd--------', 'AuxY']
['μὲν', 'μέν', 'd--------', 'd--------', 'AuxY']
['δὲ', 'δέ', 'd--------', 'd--------', 'AuxY']
['δὲ', 'δέ', 'd--------', 'd--------', 'COORD']
['δὲ', 'δέ', 'd--------', 'd--------', 'AuxY']
['δὲ', 'δέ', 'd--------', 'd--------', 'AuxY']
['δὲ', 'δέ', 'd--------', 'd--------', 'AuxY']
['μὲν', 'μέν', 'd--------', 'd--------', 'AuxY'

In [131]:

def count_dh_anomalies(df_list):
    final_list = []
    dh_list = ['δή','δὴ']
    
    
    # Initialize counts for the requested conditions
    count_dh_forms = 0
    count_AuxY_c = 0
    count_AuxY_d = 0
    count_AuxY_b = 0
    count_AuxY_not = 0
    count_AuxX_c = 0
    count_AuxX_d = 0
    count_AuxX_b = 0
    count_AuxX_not = 0
    count_AuxZ_c = 0
    count_AuxZ_d = 0
    count_AuxZ_b = 0
    count_AuxZ_not = 0
    count_AuxC_c = 0
    count_AuxC_d = 0
    count_AuxC_b = 0
    count_AuxC_not = 0
    count_COORD_c = 0
    count_COORD_d = 0
    count_COORD_b = 0
    count_COORD_not = 0
    count_not_relation = 0

    for df in df_list:
        modified = False  # track if the dataframe has been modified

        for index, row in df.iterrows():
            postag = row['@postag']
            
            # If the form is in the kai list, count it
            if row['@form'] in dh_list:
                count_dh_forms += 1

                # Check the '@relation' and '@postag' for the specified conditions
                relation = row['@relation']
                if relation == 'AuxY':
                    if postag[0] == 'c':
                        count_AuxY_c += 1
                    elif postag[0] == 'd':
                        count_AuxY_d += 1
                    elif postag[0] == 'b':
                        count_AuxY_b += 1
                    else:
                        count_AuxY_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxX':
                    if postag[0] == 'c':
                        count_AuxX_c += 1
                    elif postag[0] == 'd':
                        count_AuxX_d += 1
                    elif postag[0] == 'b':
                        count_AuxX_b += 1
                    else:
                        count_AuxX_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxZ':
                    if postag[0] == 'c':
                        count_AuxZ_c += 1
                    elif postag[0] == 'd':
                        count_AuxZ_d += 1
                    elif postag[0] == 'b':
                        count_AuxZ_b += 1
                    else:
                        count_AuxZ_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxC':
                    if postag[0] == 'c':
                        count_AuxC_c += 1
                    elif postag[0] == 'd':
                        count_AuxC_d += 1
                    elif postag[0] == 'b':
                        count_AuxC_b += 1
                    else:
                        count_AuxC_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'COORD':
                    if postag[0] == 'c':
                        count_COORD_c += 1
                    elif postag[0] == 'd':
                        count_COORD_d += 1
                    elif postag[0] == 'b':
                        count_COORD_b += 1
                    else:
                        count_COORD_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                else:
                    count_not_relation += 1
                    print([row['@form'], row['@lemma'], postag, row['@relation']])

    # Return the counts
    return {
        'total_dh_forms': count_dh_forms,
        'AuxY_c': count_AuxY_c,
        'AuxY_d': count_AuxY_d,
        'AuxY_b': count_AuxY_b,
        'AuxY_not' : count_AuxY_not,
        'AuxX_c': count_AuxX_c,
        'AuxX_d': count_AuxX_d,
        'AuxX_b': count_AuxX_b,
        'AuxX_not' : count_AuxX_not,
        'AuxZ_c': count_AuxZ_c,
        'AuxZ_d': count_AuxZ_d,
        'AuxZ_b': count_AuxZ_b,
        'AuxZ_not' : count_AuxZ_not,
        'AuxC_c': count_AuxC_c,
        'AuxC_d': count_AuxC_d,
        'AuxC_b': count_AuxC_b,
        'AuxC_not' : count_AuxC_not,
        'COORD_c': count_COORD_c,
        'COORD_d': count_COORD_d,
        'COORD_b': count_COORD_b,
        'COORD_not' : count_COORD_not,
        'relation_not' : count_not_relation 
    }

In [132]:
countdh_dataframes = [count_dh_anomalies(lis) for lis in dataframes]

In [133]:
summed_result = sum_dicts(countdh_dataframes)

countdh_dataframes = pd.DataFrame(list(summed_result.items()), columns=['Key', 'Value'])

In [134]:
sum(countdh_dataframes['Value'])-486

482

In [135]:
countdh_dataframes

Key  Value
0   total_dh_forms    484
1           AuxY_c      0
2           AuxY_d    480
3           AuxY_b      0
4         AuxY_not      0
5           AuxX_c      0
6           AuxX_d      0
7           AuxX_b      0
8         AuxX_not      0
9           AuxZ_c      0
10          AuxZ_d      4
11          AuxZ_b      0
12        AuxZ_not      0
13          AuxC_c      0
14          AuxC_d      0
15          AuxC_b      0
16        AuxC_not      0
17         COORD_c      0
18         COORD_d      0
19         COORD_b      0
20       COORD_not      0
21    relation_not      0

In [136]:
# Function to check and display anomalies in the postag
def replace_dh_anomalies(df_list):
  final_list = []
  dhlist = ['δή','δὴ']

  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if len(postag) == 9 and row['@form'] in dhlist:
          if postag[0] == 'c' or postag[0] == 'd' or postag[0] == 'b':
            if row['@relation']== 'AuxY' or row['@relation']== 'AuxZ' or row['@relation']== 'AuxC'or   row['@relation']== 'COORD' or row['@relation']== 'AuxX':
              row['@postag'] = 'd' + postag[1:9]
          
          
          #update the dataframe .at è come dire append ma per i dataframe
          df.at[index, '@postag'] = row['@postag']
          print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
          modified = True

    #append the dataframe whether modified or not
    final_list.append(df)

  return final_list

In [137]:
anomaliesdh_dataframes = [replace_dh_anomalies(lis) for lis in dataframes]

['δὴ', 'δή', 'd--------', 'd--------', 'AuxY']
['δὴ', 'δή', 'd--------', 'd--------', 'AuxY']
['δὴ', 'δή', 'd--------', 'd--------', 'AuxY']
['δὴ', 'δή', 'd--------', 'd--------', 'AuxY']
['δὴ', 'δή', 'd--------', 'd--------', 'AuxY']
['δὴ', 'δή', 'd--------', 'd--------', 'AuxY']
['δὴ', 'δή', 'd--------', 'd--------', 'AuxY']
['δή', 'δή', 'd--------', 'd--------', 'AuxY']
['δή', 'δή', 'd--------', 'd--------', 'AuxY']
['δή', 'δή', 'd--------', 'd--------', 'AuxY']
['δή', 'δή', 'd--------', 'd--------', 'AuxY']
['δή', 'δή', 'd--------', 'd--------', 'AuxY']
['δή', 'δή', 'd--------', 'd--------', 'AuxY']
['δή', 'δή', 'd--------', 'd--------', 'AuxY']
['δή', 'δή', 'd--------', 'd--------', 'AuxY']
['δή', 'δή', 'd--------', 'd--------', 'AuxY']
['δή', 'δή', 'd--------', 'd--------', 'AuxY']
['δή', 'δή', 'd--------', 'd--------', 'AuxY']
['δή', 'δή', 'd--------', 'd--------', 'AuxY']
['δή', 'δή', 'd--------', 'd--------', 'AuxY']
['δή', 'δή', 'd--------', 'd--------', 'AuxY']
['δὴ', 'δή', 

In [138]:

def count_mede_anomalies(df_list):
    final_list = []
    mede_list = ['μηδὲ', 'μηδέ', 'μηδ’', "οὐδʼ", "οὐδέ", "οὐδὲ",'οὐδ’']
    
    
    # Initialize counts for the requested conditions
    count_mede_forms = 0
    count_AuxY_c = 0
    count_AuxY_d = 0
    count_AuxY_b = 0
    count_AuxY_not = 0
    count_AuxX_c = 0
    count_AuxX_d = 0
    count_AuxX_b = 0
    count_AuxX_not = 0
    count_AuxZ_c = 0
    count_AuxZ_d = 0
    count_AuxZ_b = 0
    count_AuxZ_not = 0
    count_AuxC_c = 0
    count_AuxC_d = 0
    count_AuxC_b = 0
    count_AuxC_not = 0
    count_COORD_c = 0
    count_COORD_d = 0
    count_COORD_b = 0
    count_COORD_not = 0
    count_not_relation = 0

    for df in df_list:
        modified = False  # track if the dataframe has been modified

        for index, row in df.iterrows():
            postag = row['@postag']
            
            # If the form is in the kai list, count it
            if row['@form'] in mede_list:
                count_mede_forms += 1

                # Check the '@relation' and '@postag' for the specified conditions
                relation = row['@relation']
                if relation == 'AuxY':
                    if postag[0] == 'c':
                        count_AuxY_c += 1
                    elif postag[0] == 'd':
                        count_AuxY_d += 1
                    elif postag[0] == 'b':
                        count_AuxY_b += 1
                    else:
                        count_AuxY_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxX':
                    if postag[0] == 'c':
                        count_AuxX_c += 1
                    elif postag[0] == 'd':
                        count_AuxX_d += 1
                    elif postag[0] == 'b':
                        count_AuxX_b += 1
                    else:
                        count_AuxX_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxZ':
                    if postag[0] == 'c':
                        count_AuxZ_c += 1
                    elif postag[0] == 'd':
                        count_AuxZ_d += 1
                    elif postag[0] == 'b':
                        count_AuxZ_b += 1
                    else:
                        count_AuxZ_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'AuxC':
                    if postag[0] == 'c':
                        count_AuxC_c += 1
                    elif postag[0] == 'd':
                        count_AuxC_d += 1
                    elif postag[0] == 'b':
                        count_AuxC_b += 1
                    else:
                        count_AuxC_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                elif relation == 'COORD':
                    if postag[0] == 'c':
                        count_COORD_c += 1
                    elif postag[0] == 'd':
                        count_COORD_d += 1
                    elif postag[0] == 'b':
                        count_COORD_b += 1
                    else:
                        count_COORD_not += 1
                        print([row['@form'], row['@lemma'], postag, row['@relation']])
                else:
                    count_not_relation += 1
                    print([row['@form'], row['@lemma'], postag, row['@relation']])

    # Return the counts
    return {
        'total_mede_forms': count_mede_forms,
        'AuxY_c': count_AuxY_c,
        'AuxY_d': count_AuxY_d,
        'AuxY_b': count_AuxY_b,
        'AuxY_not' : count_AuxY_not,
        'AuxX_c': count_AuxX_c,
        'AuxX_d': count_AuxX_d,
        'AuxX_b': count_AuxX_b,
        'AuxX_not' : count_AuxX_not,
        'AuxZ_c': count_AuxZ_c,
        'AuxZ_d': count_AuxZ_d,
        'AuxZ_b': count_AuxZ_b,
        'AuxZ_not' : count_AuxZ_not,
        'AuxC_c': count_AuxC_c,
        'AuxC_d': count_AuxC_d,
        'AuxC_b': count_AuxC_b,
        'AuxC_not' : count_AuxC_not,
        'COORD_c': count_COORD_c,
        'COORD_d': count_COORD_d,
        'COORD_b': count_COORD_b,
        'COORD_not' : count_COORD_not,
        'relation_not' : count_not_relation 
    }

In [139]:
countmede_dataframes = [count_mede_anomalies(lis) for lis in dataframes]

['οὐδ’', 'οὐδέ', 'c--------', 'COORD_CO']


In [140]:
summed_result = sum_dicts(countmede_dataframes)

countmede_dataframes = pd.DataFrame(list(summed_result.items()), columns=['Key', 'Value'])

In [141]:
sum(countmede_dataframes['Value'])-483

413

In [142]:
countmede_dataframes

Key  Value
0   total_mede_forms    448
1             AuxY_c     30
2             AuxY_d     22
3             AuxY_b     18
4           AuxY_not      0
5             AuxX_c      0
6             AuxX_d      0
7             AuxX_b      0
8           AuxX_not      0
9             AuxZ_c     70
10            AuxZ_d    153
11            AuxZ_b      2
12          AuxZ_not      0
13            AuxC_c      1
14            AuxC_d      0
15            AuxC_b      0
16          AuxC_not      0
17           COORD_c     81
18           COORD_d     29
19           COORD_b     41
20         COORD_not      0
21      relation_not      1

In [143]:
# Function to check and display anomalies in the postag CONTROLLAAAA AUX X!!! E IL NUMERO TOKENS PER CORREGGERE
def replace_mede_anomalies(df_list):
  final_list = []
  mede_list = ['μηδὲ', 'μηδέ', 'μηδ’', "οὐδʼ", "οὐδέ", "οὐδὲ",'οὐδ’']

  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if len(postag) == 9 and row['@form'] in mede_list:
          if postag[0] == 'c' or postag[0] == 'd' or postag[0] == 'b':
          #modify the postag
            if row['@relation']== 'AuxZ':
              row['@postag'] = 'd' + postag[1:9]
            #print([row['@lemma'], row['@form'], postag, row['@postag'],row['@relation']])
            elif row['@relation']== 'AuxY' or row['@relation']== 'AuxC' or row['@relation']== 'COORD':
              row['@postag'] = 'c' + postag[1:9]
            #print([row['@lemma'], row['@form'], postag, row['@postag'],row['@relation']])
          
          #update the dataframe .at è come dire append ma per i dataframe
          df.at[index, '@postag'] = row['@postag']
          print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
          modified = True

    #append the dataframe whether modified or not
    final_list.append(df)

  return final_list

In [144]:
anomaliesmede_dataframes = [replace_mede_anomalies(lis) for lis in dataframes]

['οὐδὲ', 'οὐδέ', 'd--------', 'c--------', 'COORD']
['οὐδὲ', 'οὐδέ', 'd--------', 'c--------', 'COORD']
['μηδὲ', 'μηδέ', 'd--------', 'd--------', 'AuxZ']
['μηδὲ', 'μηδέ', 'd--------', 'd--------', 'AuxZ']
['μηδὲ', 'μηδέ', 'd--------', 'c--------', 'COORD']
['μηδὲ', 'μηδέ', 'b--------', 'c--------', 'COORD']
['μηδὲ', 'μηδέ', 'd--------', 'c--------', 'COORD']
['μηδὲ', 'μηδέ', 'd--------', 'c--------', 'COORD']
['μηδὲ', 'μηδέ', 'd--------', 'c--------', 'AuxY']
['μηδὲ', 'μηδέ', 'd--------', 'c--------', 'COORD']
['μηδὲ', 'μηδέ', 'd--------', 'c--------', 'COORD']
['μηδὲ', 'μηδέ', 'd--------', 'd--------', 'AuxZ']
['οὐδὲ', 'οὐδέ', 'd--------', 'd--------', 'AuxZ']
['μηδὲ', 'μηδέ', 'd--------', 'd--------', 'AuxZ']
['μηδὲ', 'μηδέ', 'd--------', 'c--------', 'COORD']
['οὐδʼ', 'οὐδέ', 'b--------', 'c--------', 'COORD']
['οὐδʼ', 'οὐδέ', 'b--------', 'c--------', 'COORD']
['οὐδέ', 'οὐδέ', 'd--------', 'c--------', 'AuxY']
['οὐδέ', 'οὐδέ', 'c--------', 'c--------', 'AuxY']
['οὐδέ', 'οὐδέ', 'd-

In [145]:
def print_an(df_list):
    
    for i,df in enumerate(df_list):
        for index, row in df.iterrows():
            
            postag = row['@postag']
            if row['@form'] == 'ἄν':
               print('frase', i)
               print([index,row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])

In [146]:
#salvare la lista di directory
lis_dir = os.listdir("C:/Users/lcolo/Desktop/TESI/CODICI DEFINITIVI DIZ UNICO-2/PEDALION/output_pedalion_con_relation")
for j,lis in enumerate(dataframes):
    print('Opera',lis_dir[j])
    print_an(lis)

Opera aeneas.xml
frase 0
[15, 'ἄν', 'ἐάν', 'c--------', 'c--------', 'AuxC']
frase 3
[18, 'ἄν', 'ἄν', 'd--------', 'd--------', 'AuxY']
frase 28
[9, 'ἄν', 'ἄν', 'd--------', 'd--------', 'AuxY']
frase 32
[23, 'ἄν', 'ἐάν', 'c--------', 'c--------', 'AuxC']
frase 58
[56, 'ἄν', 'ἄν', 'd--------', 'd--------', 'AuxY']
frase 81
[0, 'ἄν', 'ἐάν', 'c--------', 'c--------', 'AuxC']
frase 123
[29, 'ἄν', 'ἄν', 'd--------', 'd--------', 'AuxY']
frase 177
[4, 'ἄν', 'ἐάν', 'c--------', 'c--------', 'AuxC']
frase 214
[52, 'ἄν', 'ἐάν', 'c--------', 'c--------', 'AuxC']
frase 286
[2, 'ἄν', 'ἄν', 'd--------', 'd--------', 'AuxY']
Opera aesop1.xml
frase 5
[7, 'ἄν', 'ἄν', 'd--------', 'd--------', 'AuxY']
frase 55
[18, 'ἄν', 'ἄν', 'd--------', 'd--------', 'AuxY']
frase 56
[5, 'ἄν', 'ἄν', 'd--------', 'd--------', 'AuxY']
frase 148
[17, 'ἄν', 'ἄν', 'd--------', 'd--------', 'AuxY']
frase 149
[5, 'ἄν', 'ἄν', 'd--------', 'd--------', 'AuxY']
frase 258
[8, 'ἄν', 'ἄν', 'd--------', 'd--------', 'AuxY']
frase

In [147]:
'''Opera sextus.xml
frase 80
[0, 'καὶ', 'b--------']
frase 268
[15, 'α', 'b--------']     lettere n--------
frase 268
[16, 'ε', 'b--------']      lettt
frase 268
[17, 'η', 'b--------']         lettere
frase 268
[18, 'ι', 'b--------']        lettere
frase 268
[19, 'ο', 'b--------']       lettere
frase 268
[20, 'υ', 'b--------']
frase 268
[21, 'ω', 'b--------']'''

"Opera sextus.xml\nfrase 80\n[0, 'καὶ', 'b--------']\nfrase 268\n[15, 'α', 'b--------']     lettere n--------\nfrase 268\n[16, 'ε', 'b--------']      lettt\nfrase 268\n[17, 'η', 'b--------']         lettere\nfrase 268\n[18, 'ι', 'b--------']        lettere\nfrase 268\n[19, 'ο', 'b--------']       lettere\nfrase 268\n[20, 'υ', 'b--------']\nfrase 268\n[21, 'ω', 'b--------']"

In [148]:
# QUANTI TOTALI TOLTI E CAMBIATI CON - = PEDALION

# Function to check and display anomalies in the postag
def count_lettgreche_anomalies(df_list):
  lettere_greche = [
    'α', 'ε', 'η', 'ι', 'ο', 'υ', 'ω', 'η', 'ω', 'ε', 'ο', 'α', 'ι', 'υ', 'α', 'υ',
    'ζ', 'θ', 'λ', 'μ', 'ν', 'ξ', 'ρ', 'σ', 'φ', 'χ', 'ψ', 'θ', 'φ', 'χ', 'β', 'γ',
    'δ', 'κ', 'π', 'τ', 'θ', 'φ', 'χ', 'θ', 'φ', 'χ', 'κ', 'π', 'τ', 'ρ', 'ζ', 'ξ',
    'ψ', 'ζ', 'σ', 'δ', 'ξ', 'κ', 'σ', 'ψ', 'π', 'σ', 'α', 'ι', 'υ', 'α', 'ι', 'υ',
    'α', 'ι', 'υ', 'η', 'ω', 'ε', 'ο', 'α', 'ι', 'υ', 'η', 'ω', 'α', 'ι', 'υ', 'ο',
    'ε', 'α', 'ι', 'υ', 'α', 'ι', 'υ', 'ε', 'η', 'η', 'ε', 'ε', 'η', 'ο', 'ω', 'ω',
    'ο', 'ο', 'ω', 'αι', 'ου', 'α', 'ε', 'ο', 'αι', 'ει', 'ρα', 'ρ', 'α', 'ρα', 'αι',
    'αι', 'ει', 'ου', 'α', 'ι', 'υ', 'η', 'ω', 'α', 'ερ', 'ρ', 'ε', 'ρε', 'ρ', 'ε',
    'α', 'ε', 'ι', 'ι', 'ει', 'ζ', 'σ', 'β', 'σ', 'ι', 'σ', 'ζ', 'σ', 'σ', 'ζ', 'σ',
    'σ', 'ζ', 'ι', 'τ', 'σ', 'σ', 'σ', 'ης', 'σ', 'σ', 'σ'
]
  final_list = []
  count = 0
  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if len(postag) == 9 and row['@form'] in lettere_greche:
           count+=1

  return count

In [149]:
count_lettgreche = sum([count_lettgreche_anomalies(lis) for lis in dataframes])
print(f'count_letteregreche:{count_lettgreche}')

count_letteregreche:205


In [150]:
#SPECIFICA SOLO NELL'OPERA DI SEXTUS XML



# Function to check and display anomalies in the postag
def replace_LETTERE_anomalies(df_list):
  final_list = []
  lettere_greche = [
    'α', 'ε', 'η', 'ι', 'ο', 'υ', 'ω', 'η', 'ω', 'ε', 'ο', 'α', 'ι', 'υ', 'α', 'υ',
    'ζ', 'θ', 'λ', 'μ', 'ν', 'ξ', 'ρ', 'σ', 'φ', 'χ', 'ψ', 'θ', 'φ', 'χ', 'β', 'γ',
    'δ', 'κ', 'π', 'τ', 'θ', 'φ', 'χ', 'θ', 'φ', 'χ', 'κ', 'π', 'τ', 'ρ', 'ζ', 'ξ',
    'ψ', 'ζ', 'σ', 'δ', 'ξ', 'κ', 'σ', 'ψ', 'π', 'σ', 'α', 'ι', 'υ', 'α', 'ι', 'υ',
    'α', 'ι', 'υ', 'η', 'ω', 'ε', 'ο', 'α', 'ι', 'υ', 'η', 'ω', 'α', 'ι', 'υ', 'ο',
    'ε', 'α', 'ι', 'υ', 'α', 'ι', 'υ', 'ε', 'η', 'η', 'ε', 'ε', 'η', 'ο', 'ω', 'ω',
    'ο', 'ο', 'ω', 'αι', 'ου', 'α', 'ε', 'ο', 'αι', 'ει', 'ρα', 'ρ', 'α', 'ρα', 'αι',
    'αι', 'ει', 'ου', 'α', 'ι', 'υ', 'η', 'ω', 'α', 'ερ', 'ρ', 'ε', 'ρε', 'ρ', 'ε',
    'α', 'ε', 'ι', 'ι', 'ει', 'ζ', 'σ', 'β', 'σ', 'ι', 'σ', 'ζ', 'σ', 'σ', 'ζ', 'σ',
    'σ', 'ζ', 'ι', 'τ', 'σ', 'σ', 'σ', 'ης', 'σ', 'σ', 'σ'
]
  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if len(postag) == 9 and row['@form'] in lettere_greche:
          #modify the postag
          row['@postag'] = 'n--------' 
          print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
          #update the dataframe .at è come dire append ma per i dataframe
          df.at[index, '@postag'] = row['@postag']
          modified = True

    #append the dataframe whether modified or not
    final_list.append(df)

  return final_list

#'output_pedalion_con_relation'

In [151]:
anomaliesLETT_dataframes = [replace_LETTERE_anomalies(lis) for lis in dataframes]

['ει', '.ω', 'v3siia---', 'n--------', 'AuxC']
['δ', 'δ', 'm--------', 'n--------', 'ATR']
['δ', 'δ', 'm--------', 'n--------', 'ATR']
['ζ', 'ζ', 'm--------', 'n--------', 'ATR']
['η', 'η', 'm--------', 'n--------', 'ATR']
['ι', 'ι', 'm--------', 'n--------', 'ATR']
['δ', 'δ', 'm--------', 'n--------', 'ATR']
['λ', 'λ', 'm--------', 'n--------', 'ATR']
['α', 'α', 'm--------', 'n--------', 'ATR']
['η', 'η', 'm--------', 'n--------', 'ATR']
['η', 'G', '---------', 'n--------', 'GAP']
['η', 'η', 'm--------', 'n--------', 'ATR']
['η', 'η', 'm--------', 'n--------', 'ATR']
['κ', 'κ', 'm--------', 'n--------', 'ATR']
['δ', 'δ', 'm--------', 'n--------', 'ADV']
['μ', 'μ', 'm--------', 'n--------', 'ATR']
['γ', 'γ', 'm--------', 'n--------', 'ATR']
['μ', 'μ', 'm--------', 'n--------', 'ATR']
['γ', 'γ', 'm--------', 'n--------', 'ATR']
['δ', 'δ', 'm--------', 'n--------', 'ATR']
['φ', 'φ', 'm--------', 'n--------', 'ATR']
['σ', 'σ', 'm--------', 'n--------', 'ATR']
['α', 'α', 'm--------', 'n---

In [152]:
#CELLA SOPRA ATTENTA ALLA LEMMATIZZAZIONE DELLE LETTERE GRECHE!

In [153]:
def print_num(df_list):
    
    for i,df in enumerate(df_list):
        for index, row in df.iterrows():
            
            postag = row['@postag']
            if len(postag) == 9 and postag == 'm--------':
               print('frase', i)
               print([index, row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])

In [154]:
#salvare la lista di directory
lis_dir = os.listdir("C:/Users/lcolo/Desktop/TESI/CODICI DEFINITIVI DIZ UNICO-2/PEDALION/output_pedalion_con_relation")
for j,lis in enumerate(dataframes):
    print('Opera',lis_dir[j])
    print_num(lis)

Opera aeneas.xml
frase 18
[31, 'δύο', 'δύο', 'm--------', 'm--------', 'ADV_CO']
frase 24
[0, 'δύο', 'δύο', 'm--------', 'm--------', 'ATR_CO']
frase 61
[5, 'τρεῖς', 'τρεῖς', 'm--------', 'm--------', 'SBJ']
frase 146
[32, 'δύο', 'δύο', 'm--------', 'm--------', 'ATR']
frase 151
[40, 'ἑξήκοντα', 'ἑξήκοντα', 'm--------', 'm--------', 'ATR']
frase 168
[16, 'τρεῖς', 'τρεῖς', 'm--------', 'm--------', 'OBJ_CO']
frase 168
[20, 'δύο', 'δύο', 'm--------', 'm--------', 'OBJ_CO']
frase 264
[8, 'πέντε', 'πέντε', 'm--------', 'm--------', 'ATR']
frase 277
[18, 'δύο', 'δύο', 'm--------', 'm--------', 'ATR']
Opera aesop1.xml
frase 121
[9, 'ἑκατόν', 'ἑκατόν', 'm--------', 'm--------', 'ATR']
frase 214
[9, 'ἑκατόν', 'ἑκατόν', 'm--------', 'm--------', 'ATR']
frase 343
[1, 'δύο', 'δύο', 'm--------', 'm--------', 'ATR']
frase 350
[0, 'δύο', 'δύο', 'm--------', 'm--------', 'ATR']
frase 454
[0, 'δύο', 'δύο', 'm--------', 'm--------', 'OBJ']
Opera charb1.xml
frase 217
[8, 'ἑκκαίδεκα', 'ἑκκαίδεκα', 'm----

In [155]:
#STO PRINTANDO QUELLO CHE IN gORMAN ERA NUMERALE, QUI NON LO è. POI PER I NUMERALI METTO M A TUTTO
'''def print_numER(df_list):
    
    for i,df in enumerate(df_list):
        for index, row in df.iterrows():
            
            postag = row['@postag']
            if len(postag) == 9 and postag == 'a-_---__-':
               print('frase', i)
               print([index,row['@form'],postag])'''

"def print_numER(df_list):\n    \n    for i,df in enumerate(df_list):\n        for index, row in df.iterrows():\n            \n            postag = row['@postag']\n            if len(postag) == 9 and postag == 'a-_---__-':\n               print('frase', i)\n               print([index,row['@form'],postag])"

In [156]:
#salvare la lista di directory
'''lis_dir = os.listdir('output_pedalion_con_relation')
for j,lis in enumerate(dataframes):
    print('Opera',lis_dir[j])
    print_numER(lis)'''

"lis_dir = os.listdir('output_pedalion_con_relation')\nfor j,lis in enumerate(dataframes):\n    print('Opera',lis_dir[j])\n    print_numER(lis)"

In [157]:
#CONFRONTO DA GORMAN QUELLI CHE ERANO SEGNATI COME NOMI PROPRI MA NON SOLO. POSTAG STRANO. QUI STRANE LETTERE
def print_nomipr(df_list):
    
    for i,df in enumerate(df_list):
        for index, row in df.iterrows():
            
            postag = row['@postag']
            if len(postag) == 9 and postag == 'n-_---__-':
               print('frase', i)
               print([index, row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])

In [158]:
#salvare la lista di directory
lis_dir = os.listdir("C:/Users/lcolo/Desktop/TESI/CODICI DEFINITIVI DIZ UNICO-2/PEDALION/output_pedalion_con_relation")
for j,lis in enumerate(dataframes):
    print('Opera',lis_dir[j])
    print_nomipr(lis)

Opera aeneas.xml
Opera aesop1.xml
Opera charb1.xml
Opera chion.xml
Opera crit.xml
Opera epictetus.xml
Opera epicurus1.xml
Opera genesis1.xml
Opera genesis2.xml
Opera genesis3.xml
Opera heron.xml
frase 101
[17, 'ψΩ', 'ψΩ', 'n-_---__-', 'n-_---__-', 'APOS']
frase 101
[22, ',ς', ',ς', 'n-_---__-', 'n-_---__-', 'SBJ']
frase 101
[27, 'Τ', 'Τ', 'n-_---__-', 'n-_---__-', 'APOS']
frase 101
[43, '∠', '∠', 'n-_---__-', 'n-_---__-', 'APOS']
frase 101
[51, 'Ε', 'Ε', 'n-_---__-', 'n-_---__-', 'APOS']
frase 105
[2, 'ΕΖ', 'ΕΖ', 'n-_---__-', 'n-_---__-', 'APOS']
frase 106
[5, 'Α', 'Α', 'n-_---__-', 'n-_---__-', 'PNOM']
frase 107
[3, '∠Ε', '∠Ε', 'n-_---__-', 'n-_---__-', 'APOS_CO']
frase 107
[5, '∠Ζ', '∠Ζ', 'n-_---__-', 'n-_---__-', 'APOS_CO']
frase 108
[17, 'ΗΘΚ', 'ΗΘΚ', 'n-_---__-', 'n-_---__-', 'SBJ']
frase 109
[5, 'ΜΛΝΞ', 'ΜΛΝΞ', 'n-_---__-', 'n-_---__-', 'APOS']
frase 109
[9, 'ΝΞ', 'ΝΞ', 'n-_---__-', 'n-_---__-', 'OBJ']
frase 109
[11, 'Α∠', 'Α∠', 'n-_---__-', 'n-_---__-', 'ADV']
frase 110
[5, '∠Ο'

In [159]:
# QUANTI TOTALI TOLTI E CAMBIATI CON - = PEDALION

# Function to check and display anomalies in the postag
def count_nomip_anomalies(df_list):
  final_list = []
  count = 0
  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if len(postag) == 9 and postag == 'n-_---__-':
           count+=1

  return count

In [160]:
count_nomipanomalies = sum([count_nomip_anomalies(lis) for lis in dataframes])
print(f'count_nomip:{count_nomipanomalies}')

count_nomip:205


In [161]:
# Function to check and display anomalies in the postag
def replace_nomip_anomalies(df_list):
  final_list = []
  
  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if len(postag) == 9 and postag == 'n-_---__-':
            row['@postag'] = 'n--------'
            print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            df.at[index, '@postag'] = row['@postag']
            modified = True

    #append the dataframe whether modified or not
    final_list.append(df)

  return final_list

In [162]:
anomaliesnomip_dataframes = [replace_nomip_anomalies(lis) for lis in dataframes]

['ψΩ', 'ψΩ', 'n-_---__-', 'n--------', 'APOS']
[',ς', ',ς', 'n-_---__-', 'n--------', 'SBJ']
['Τ', 'Τ', 'n-_---__-', 'n--------', 'APOS']
['∠', '∠', 'n-_---__-', 'n--------', 'APOS']
['Ε', 'Ε', 'n-_---__-', 'n--------', 'APOS']
['ΕΖ', 'ΕΖ', 'n-_---__-', 'n--------', 'APOS']
['Α', 'Α', 'n-_---__-', 'n--------', 'PNOM']
['∠Ε', '∠Ε', 'n-_---__-', 'n--------', 'APOS_CO']
['∠Ζ', '∠Ζ', 'n-_---__-', 'n--------', 'APOS_CO']
['ΗΘΚ', 'ΗΘΚ', 'n-_---__-', 'n--------', 'SBJ']
['ΜΛΝΞ', 'ΜΛΝΞ', 'n-_---__-', 'n--------', 'APOS']
['ΝΞ', 'ΝΞ', 'n-_---__-', 'n--------', 'OBJ']
['Α∠', 'Α∠', 'n-_---__-', 'n--------', 'ADV']
['∠Ο', '∠Ο', 'n-_---__-', 'n--------', 'APOS']
['ΠΡ', 'ΠΡ', 'n-_---__-', 'n--------', 'SBJ']
['Ο', 'Ο', 'n-_---__-', 'n--------', 'OBJ']
['ΕΖ', 'ΕΖ', 'n-_---__-', 'n--------', 'APOS_CO']
['ΘΚ', 'ΘΚ', 'n-_---__-', 'n--------', 'APOS']
['ΠΡ', 'ΠΡ', 'n-_---__-', 'n--------', 'APOS_CO']
['Τ', 'Τ', 'n-_---__-', 'n--------', 'APOS_CO']
['Υ', 'Υ', 'n-_---__-', 'n--------', 'APOS_CO']
['Ο', 'Ο'

In [163]:
def print_incorrectlenght(df_list):
    
    for i,df in enumerate(df_list):
        for index, row in df.iterrows():
            
            postag = row['@postag']
            if len(postag) != 9 and all(c=='-' for c in postag[1:9]):
               print('frase', i)
               print([index, row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])

In [164]:
#salvare la lista di directory
lis_dir = os.listdir("C:/Users/lcolo/Desktop/TESI/CODICI DEFINITIVI DIZ UNICO-2/PEDALION/output_pedalion_con_relation")
for j,lis in enumerate(dataframes):
    print('Opera',lis_dir[j])
    print_incorrectlenght(lis)

Opera aeneas.xml
Opera aesop1.xml
frase 348
[0, 'ἄν', 'ἐάν', 'c-------', 'c-------', 'AuxC']
Opera charb1.xml
Opera chion.xml
Opera crit.xml
Opera epictetus.xml
frase 157
[0, 'ὡς', 'ὡς', 'c-------', 'c-------', 'AuxC']
Opera epicurus1.xml
Opera genesis1.xml
Opera genesis2.xml
Opera genesis3.xml
Opera heron.xml
Opera iso.xml
frase 1
[46, '[0]', '_', '-', '-', 'PRED']
frase 7
[35, '[1]', '_', '-', '-', 'ExD']
frase 7
[36, '[2]', '_', '-', '-', 'ADV']
Opera julian.xml
Opera longus.xml
Opera lucian_lis.xml
Opera lucian_prometheus.xml
frase 72
[29, '[0]', '_', '_', '_', 'PRED']
Opera lucian_symposion.xml
Opera lysias_or24.xml
frase 17
[2, 'κ-', 'καί', 'd-------', 'd-------', 'AuxZ']
Opera paean.xml
frase 155
[15, 'ἄχρις', 'ἄχρι', 'c', 'c', 'AuxP']
Opera papyri.xml
frase 24
[27, '[1]', '_', '_', '_', 'ADV']
frase 33
[4, '[0]', '_', '_', '_', 'PRED']
frase 38
[5, '[0]', '_', '_', '_', 'PRED']
frase 51
[4, '[0]', '_', '_', '_', 'PRED']
frase 57
[9, '[0]', '_', '_', '_', 'OBJ']
frase 95
[7, '[0

In [165]:
#SOPRA RICONTROLLA INCORRECT LENGHT

In [166]:
# QUANTI TOTALI TOLTI E CAMBIATI CON - = PEDALION

# Function to check and display anomalies in the postag
def count_incorrectlenght_anomalies(df_list):
  final_list = []
  count = 0
  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if len(postag) != 9 and all(c=='-' for c in postag[1:9]):
           count+=1

  return count

In [167]:
count_incorrectlenght = sum([count_incorrectlenght_anomalies(lis) for lis in dataframes])
print(f'count_incorrectlunghezza:{count_incorrectlenght}')

count_incorrectlunghezza:279


In [168]:
#QUESTA VA CAMBIATA PRESTANDO ATTENZIONEEEE DEVO CONTROLLARE CHE NON MI CANCELLI IL POSTAG O NON ME LO MODIFICHI NEL CORREGGERNE LA LUNGHEZZA A 9 TRATTINI!!!

def replace_incorrectlenght_anomalies(df_list):
    final_list = []
    for df in df_list:
        modified = False
        for index, row in df.iterrows():
            postag = row['@postag']
            if len(postag) == 8 and all(postag[i] == '-' for i in range(1, 8)):
                row['@postag'] = postag + '-'
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            elif len(postag) == 10 and all(postag[i] == '-' for i in range(1, 10)):
                row['@postag'] = postag[:9]
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
     
          
          #update the dataframe .at è come dire append ma per i dataframe
            df.at[index, '@postag'] = row['@postag']
            modified = True
        final_list.append(df)

    return final_list

In [169]:
anomalieslenght_dataframes = [replace_incorrectlenght_anomalies(lis) for lis in dataframes]

['ἄν', 'ἐάν', 'c-------', 'c--------', 'AuxC']
['ὡς', 'ὡς', 'c-------', 'c--------', 'AuxC']
['κ-', 'καί', 'd-------', 'd--------', 'AuxZ']
['ζ', 'ζ', 'm-------', 'm--------', 'ATR']
['β', 'β', 'm-------', 'm--------', 'ATR']
['γ', 'γ', 'm-------', 'm--------', 'ATR']
['ιϛ', 'ιϛ', 'm-------', 'm--------', 'ATR']
['ιζ', 'ιζ', 'm-------', 'm--------', 'ATR']
['Ασξδ', 'Ἄσξδ', 'm-------', 'm--------', 'ATR']
['α', 'α', 'm-------', 'm--------', 'ATR']
['λ', 'λ', 'm-------', 'm--------', 'ATR']
['λ', 'λ', 'm-------', 'm--------', 'ADV']
['καὶ', 'καί', 'd---------', 'd--------', 'AuxZ']
['δ’', 'δέ', 'd---------', 'd--------', 'COORD']
['καὶ', 'καί', 'd---------', 'd--------', 'AuxZ']
['καὶ', 'καί', 'd---------', 'd--------', 'AuxZ']
['καὶ', 'καί', 'd---------', 'd--------', 'AuxZ']
['ὡς', 'ὡς', 'd---------', 'd--------', 'AuxZ']
['ὡς', 'ὡς', 'd---------', 'd--------', 'AuxZ']
['δὲ', 'δέ', 'd---------', 'd--------', 'AuxY']
['καὶ', 'καί', 'd---------', 'd--------', 'AuxZ']
['δὲ', 'δέ', 'd-----

In [170]:
# Function to check and display anomalies in the postag
def print_g_aggverbali(df_list):
  final_list = []
  anomalies_g_aggverbali = []

  for i,df in enumerate(df_list):
     #print(df['@form'])
     #print('frase numero',i)
     for index, row in df.iterrows():
       
        postag = row['@postag']
        if len(postag) == 9 and postag[4] == 'g':
            print('frase',i)
            print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            #anomalies_g_aggverbali.append([index, row['@form'], postag])
            #print(final_list)
            #print(anomalies_g_aggverbali)

In [171]:
#salvare la lista di directory
lis_dir = os.listdir("C:/Users/lcolo/Desktop/TESI/CODICI DEFINITIVI DIZ UNICO-2/PEDALION/output_pedalion_con_relation")
for j,lis in enumerate(dataframes):
    print('Opera',lis_dir[j])
    print_g_aggverbali(lis)

Opera aeneas.xml
frase 237
['ἐπιμελητέον', 'ἐπιμέλω', 'v-s-g-nn-', 'v-s-g-nn-', 'PRED']
Opera aesop1.xml
Opera charb1.xml
Opera chion.xml
Opera crit.xml
frase 75
['πρακτέον', 'πράσσω', 'v-s-g-na-', 'v-s-g-na-', 'PNOM']
frase 100
['πρακτέον', 'πράσσω', 'v-s-g-nn-', 'v-s-g-nn-', 'PNOM_CO']
frase 100
['γυμναστέον', 'γυμνάζω', 'v-s-g-nn-', 'v-s-g-nn-', 'PNOM_CO']
frase 100
['ἐδεστέον', 'ἐσθίω', 'v-s-g-nn-', 'v-s-g-nn-', 'PNOM_CO']
frase 100
['ποτέον', 'πίνω', 'v-s-g-nn-', 'v-s-g-nn-', 'PNOM_CO']
frase 124
['φροντιστέον', 'φροντίζω', 'v-s-g-nn-', 'v-s-g-nn-', 'PNOM']
frase 131
['ποιητέον', 'ποιέω', 'v-s-g-nn-', 'v-s-g-nn-', 'PNOM']
frase 135
['σκεπτέον', 'σκέπτομαι', 'v-s-g-nn-', 'v-s-g-nn-', 'PNOM']
frase 138
['σκεπτέον', 'σκέπτομαι', 'v-s-g-nn-', 'v-s-g-nn-', 'PNOM']
frase 146
['ἀδικητέον', 'ἀδικέω', 'v-s-g-na-', 'v-s-g-na-', 'PNOM']
frase 146
['ἀδικητέον', 'ἀδικέω', 'v-s-g-na-', 'v-s-g-na-', 'PNOM']
frase 175
['ποιητέον', 'ποιέω', 'v-s-g-nn-', 'v-s-g-nn-', 'PNOM_CO']
frase 175
['ἐξαπατητ

In [172]:
''' 'ποιητέον', 'a-s---nn- PROBLEMA DI LEMMATIZZAZIONE '''

" 'ποιητέον', 'a-s---nn- PROBLEMA DI LEMMATIZZAZIONE "

In [173]:
# QUANTI TOTALI TOLTI E CAMBIATI CON - = PEDALION

# Function to check and display anomalies in the postag
def count_aggverb_anomalies(df_list):
  final_list = []
  count = 0
  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if len(postag) == 9 and (postag == 'v-s-g-nn-' or postag == 'v-s-g-na-'):
           count+=1

  return count

In [174]:
count_aggverbanomalies = sum([count_aggverb_anomalies(lis) for lis in dataframes])
print(f'count_aggverb:{count_aggverbanomalies}')

count_aggverb:27


In [175]:
# Function to check and display anomalies in the postag
def replace_aggverb_anomalies(df_list):
  final_list = []
  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if len(postag) == 9 and (postag == 'v-s-g-nn-' or postag == 'v-s-g-na-'):
          
            row['@postag'] = 'a-s---nn-'
            print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            df.at[index, '@postag'] = row['@postag']
            modified = True

    #append the dataframe whether modified or not
    final_list.append(df)

  return final_list

In [176]:
aggvsugorman_dataframes = [replace_aggverb_anomalies(lis) for lis in dataframes]

['ἐπιμελητέον', 'ἐπιμέλω', 'v-s-g-nn-', 'a-s---nn-', 'PRED']
['πρακτέον', 'πράσσω', 'v-s-g-na-', 'a-s---nn-', 'PNOM']
['πρακτέον', 'πράσσω', 'v-s-g-nn-', 'a-s---nn-', 'PNOM_CO']
['γυμναστέον', 'γυμνάζω', 'v-s-g-nn-', 'a-s---nn-', 'PNOM_CO']
['ἐδεστέον', 'ἐσθίω', 'v-s-g-nn-', 'a-s---nn-', 'PNOM_CO']
['ποτέον', 'πίνω', 'v-s-g-nn-', 'a-s---nn-', 'PNOM_CO']
['φροντιστέον', 'φροντίζω', 'v-s-g-nn-', 'a-s---nn-', 'PNOM']
['ποιητέον', 'ποιέω', 'v-s-g-nn-', 'a-s---nn-', 'PNOM']
['σκεπτέον', 'σκέπτομαι', 'v-s-g-nn-', 'a-s---nn-', 'PNOM']
['σκεπτέον', 'σκέπτομαι', 'v-s-g-nn-', 'a-s---nn-', 'PNOM']
['ἀδικητέον', 'ἀδικέω', 'v-s-g-na-', 'a-s---nn-', 'PNOM']
['ἀδικητέον', 'ἀδικέω', 'v-s-g-na-', 'a-s---nn-', 'PNOM']
['ποιητέον', 'ποιέω', 'v-s-g-nn-', 'a-s---nn-', 'PNOM_CO']
['ἐξαπατητέον', 'ἐξαπατάω', 'v-s-g-nn-', 'a-s---nn-', 'PNOM_CO']
['ποιητέον', 'ποιέω', 'v-s-g-nn-', 'a-s---nn-', 'PNOM']
['ποιητέον', 'ποιέω', 'v-s-g-nn-', 'a-s---nn-', 'PNOM']
['ὑπεικτέον', 'ὑπείκω', 'v-s-g-nn-', 'a-s---nn-', 'PNO

In [177]:
#PRONOMI E NOMI CON MASCHILE E FEMMINILE UGUALE

In [178]:

def print_tis(df_list):
  final_list = []
  greek_words = [
    # Nominative
         # τί (originale), senza accento, con accento acuto, con accento grave
    "τίνε", "τινε", "τινέ", "τινὲ", # τίνε (originale), senza accento, con accento acuto, con accento grave
    "τίνε", "τινε", "τινέ", "τινὲ", # stesso per la seconda occorrenza di τίνε
    "τίνες", "τινες", "τινές", "τινὲς", # τίνες (originale), senza accento, con accento acuto, con accento grave
    "τίνα", "τινα", "τινά", "τινὰ", # τίνα (originale), senza accento, con accento acuto, con accento grave
     "τίς", "τις", "τις́", "τις̀",   # τίς (originale), senza accento, con accento acuto, con accento grave
    "τί", "τι", "τί", "τὶ", 
    # Genitive
    "τίνος", "τινος", "τινός", "τινὸς", # τίνος (originale), senza accento, con accento acuto, con accento grave
    "του", "τού", "τοὺ",       # τοῦ (originale), senza accento, con accento acuto, con accento grave
    "τίνος", "τινος", "τινός", "τινὸς", # stessa struttura per la seconda occorrenza di τίνος
     "του", "τού", "τοὺ",       # stessa struttura per la seconda occorrenza di τοῦ
    "τίνοιν", "τινοιν", "τινοίν", "τινοὶν", # τίνοιν (originale), senza accento, con accento acuto, con accento grave
    "τίνοιν", "τινοιν", "τινοίν", "τινοὶν", # stessa struttura per la seconda occorrenza di τίνοιν
    "τίνων", "τινων", "τινῶν", "τινῶν", # τίνων (originale), senza accento, con accento acuto, con accento grave
    "τίνων", "τινων", "τινῶν", "τινῶν", # stessa struttura per la seconda occorrenza di τίνων
    
    # Dative
    "τίνι", "τινι", "τινί", "τινὶ",     # τίνι (originale), senza accento, con accento acuto, con accento grave
    "τω", "τώ", "τὼ",           # τῷ (originale), senza accento, con accento acuto, con accento grave
    "τίνι", "τινι", "τινί", "τινὶ",     # stessa struttura per la seconda occorrenza di τίνι
    "τω", "τώ", "τὼ",           # stessa struttura per la seconda occorrenza di τῷ
    "τίνοιν", "τινοιν", "τινοίν", "τινοὶν", # τίνοιν (originale), senza accento, con accento acuto, con accento grave
    "τίνοιν", "τινοιν", "τινοίν", "τινοὶν", # stessa struttura per la seconda occorrenza di τίνοιν
    "τίσι", "τισι", "τίσί", "τίσι", # τίσι(ν) (originale), senza accento, con accento acuto, con accento grave
    "τίσι", "τισι", "τίσί", "τίσι", # stessa struttura per la seconda occorrenza di τίσι(ν)
    "τίσιν", "τισιν", "τίσίν", "τίσιν", # τίσι(ν) (originale), senza accento, con accento acuto, con accento grave
    "τίσιν", "τισιν", "τίσίν", "τίσιν",
    # Accusative
    "τίνα", "τινα", "τινά", "τινὰ",     # τίνα (originale), senza accento, con accento acuto, con accento grave
    "τί", "τι", "τί", "τὶ",           # τί (originale), senza accento, con accento acuto, con accento grave
    "τίνε", "τινε", "τινέ", "τινὲ",     # τίνε (originale), senza accento, con accento acuto, con accento grave
    "τίνε", "τινε", "τινέ", "τινὲ",     # stessa struttura per la seconda occorrenza di τίνε
    "τίνας", "τινας", "τινάς", "τινὰς", # τίνας (originale), senza accento, con accento acuto, con accento grave
    "τίνα", "τινα", "τινά", "τινὰ"      # τίνα (originale), senza accento, con accento acuto, con accento grave
]
  for i,df in enumerate(df_list):
    for index, row in df.iterrows():
        postag = row['@postag']
        if row['@form'] in greek_words:
            print('frase', i)
            print([index,row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])

In [179]:
#salvare la lista di directory
lis_dir = os.listdir('output_pedalion_con_relation')
for j,lis in enumerate(dataframes):
    print('Opera',lis_dir[j])
    print_tis(lis)

Opera aeneas.xml
frase 0
[16, 'τι', 'τις', 'a-s---nn-', 'a-s---nn-', 'ATR']
frase 3
[3, 'τι', 'τις', 'a-s---nn-', 'a-s---nn-', 'ATR']
frase 3
[21, 'τινὲς', 'τις', 'p-p---cn-', 'p-p---cn-', 'SBJ']
frase 8
[30, 'τινα', 'τις', 'p-s---ca-', 'p-s---ca-', 'ATR']
frase 27
[20, 'τι', 'τις', 'p-s---nn-', 'p-s---nn-', 'OBJ']
frase 28
[10, 'τις', 'τις', 'p-s---cn-', 'p-s---cn-', 'SBJ']
frase 28
[25, 'τι', 'τις', 'p-s---na-', 'p-s---na-', 'ATR']
frase 30
[21, 'τι', 'τις', 'p-s---nn-', 'p-s---nn-', 'OBJ']
frase 31
[8, 'τι', 'τις', 'p-s---na-', 'p-s---na-', 'ATR']
frase 32
[24, 'τις', 'τις', 'p-s---cn-', 'p-s---cn-', 'SBJ']
frase 34
[17, 'τι', 'τις', 'p-s---nn-', 'p-s---nn-', 'SBJ']
frase 41
[15, 'τινὸς', 'τις', 'p-s---cg-', 'p-s---cg-', 'SBJ']
frase 47
[22, 'τινα', 'τις', 'p-s---ca-', 'p-s---ca-', 'ATR']
frase 48
[6, 'τινὰς', 'τις', 'p-p---ca-', 'p-p---ca-', 'OBJ']
frase 50
[8, 'τινῶν', 'τις', 'p-p---cg-', 'p-p---cg-', 'SBJ']
frase 58
[16, 'τι', 'τις', 'p-s---na-', 'p-s---na-', 'OBJ']
frase 58
[48,

In [180]:
# QUANTI TOTALI TOLTI E CAMBIATI CON - = PEDALION

# Function to check and display anomalies in the postag
def count_tismascfemm_anomalies(df_list):
  greek_words = [
    # Nominative
         # τί (originale), senza accento, con accento acuto, con accento grave
    "τίνε", "τινε", "τινέ", "τινὲ", # τίνε (originale), senza accento, con accento acuto, con accento grave
    "τίνε", "τινε", "τινέ", "τινὲ", # stesso per la seconda occorrenza di τίνε
    "τίνες", "τινες", "τινές", "τινὲς", # τίνες (originale), senza accento, con accento acuto, con accento grave
    "τίνα", "τινα", "τινά", "τινὰ", # τίνα (originale), senza accento, con accento acuto, con accento grave
     "τίς", "τις", "τις́", "τις̀",   # τίς (originale), senza accento, con accento acuto, con accento grave
    "τί", "τι", "τί", "τὶ", 
    # Genitive
    "τίνος", "τινος", "τινός", "τινὸς", # τίνος (originale), senza accento, con accento acuto, con accento grave
    "του", "τού", "τοὺ",       # τοῦ (originale), senza accento, con accento acuto, con accento grave
    "τίνος", "τινος", "τινός", "τινὸς", # stessa struttura per la seconda occorrenza di τίνος
     "του", "τού", "τοὺ",       # stessa struttura per la seconda occorrenza di τοῦ
    "τίνοιν", "τινοιν", "τινοίν", "τινοὶν", # τίνοιν (originale), senza accento, con accento acuto, con accento grave
    "τίνοιν", "τινοιν", "τινοίν", "τινοὶν", # stessa struttura per la seconda occorrenza di τίνοιν
    "τίνων", "τινων", "τινῶν", "τινῶν", # τίνων (originale), senza accento, con accento acuto, con accento grave
    "τίνων", "τινων", "τινῶν", "τινῶν", # stessa struttura per la seconda occorrenza di τίνων
    
    # Dative
    "τίνι", "τινι", "τινί", "τινὶ",     # τίνι (originale), senza accento, con accento acuto, con accento grave
    "τω", "τώ", "τὼ",           # τῷ (originale), senza accento, con accento acuto, con accento grave
    "τίνι", "τινι", "τινί", "τινὶ",     # stessa struttura per la seconda occorrenza di τίνι
    "τω", "τώ", "τὼ",           # stessa struttura per la seconda occorrenza di τῷ
    "τίνοιν", "τινοιν", "τινοίν", "τινοὶν", # τίνοιν (originale), senza accento, con accento acuto, con accento grave
    "τίνοιν", "τινοιν", "τινοίν", "τινοὶν", # stessa struttura per la seconda occorrenza di τίνοιν
    "τίσι", "τισι", "τίσί", "τίσι", # τίσι(ν) (originale), senza accento, con accento acuto, con accento grave
    "τίσι", "τισι", "τίσί", "τίσι", # stessa struttura per la seconda occorrenza di τίσι(ν)
    "τίσιν", "τισιν", "τίσίν", "τίσιν", # τίσι(ν) (originale), senza accento, con accento acuto, con accento grave
    "τίσιν", "τισιν", "τίσίν", "τίσιν",
    # Accusative
    "τίνα", "τινα", "τινά", "τινὰ",     # τίνα (originale), senza accento, con accento acuto, con accento grave
    "τί", "τι", "τί", "τὶ",           # τί (originale), senza accento, con accento acuto, con accento grave
    "τίνε", "τινε", "τινέ", "τινὲ",     # τίνε (originale), senza accento, con accento acuto, con accento grave
    "τίνε", "τινε", "τινέ", "τινὲ",     # stessa struttura per la seconda occorrenza di τίνε
    "τίνας", "τινας", "τινάς", "τινὰς", # τίνας (originale), senza accento, con accento acuto, con accento grave
    "τίνα", "τινα", "τινά", "τινὰ"      # τίνα (originale), senza accento, con accento acuto, con accento grave
]
  pos_6c = ['f', 'm']
  final_list = []
  count = 0
  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if row['@form'] in greek_words:
            if postag[0] != 'l':
              if len(postag) == 9 and postag[6] in pos_6c and (postag[0] == 'a' or postag[0] =='p'):
                count+=1

  return count

In [181]:
count_tismascfemm = sum([count_tismascfemm_anomalies(lis) for lis in dataframes])
print(f'count_tismaschilefemm:{count_tismascfemm}')

count_tismaschilefemm:32


In [182]:
# Function to check and display anomalies in the postag
def replace_tis_anomalies(df_list):
  greek_words = [
    # Nominative
         # τί (originale), senza accento, con accento acuto, con accento grave
    "τίνε", "τινε", "τινέ", "τινὲ", # τίνε (originale), senza accento, con accento acuto, con accento grave
    "τίνε", "τινε", "τινέ", "τινὲ", # stesso per la seconda occorrenza di τίνε
    "τίνες", "τινες", "τινές", "τινὲς", # τίνες (originale), senza accento, con accento acuto, con accento grave
    "τίνα", "τινα", "τινά", "τινὰ", # τίνα (originale), senza accento, con accento acuto, con accento grave
     "τίς", "τις", "τις́", "τις̀",   # τίς (originale), senza accento, con accento acuto, con accento grave
    "τί", "τι", "τί", "τὶ", 
    # Genitive
    "τίνος", "τινος", "τινός", "τινὸς", # τίνος (originale), senza accento, con accento acuto, con accento grave
    "του", "τού", "τοὺ",       # τοῦ (originale), senza accento, con accento acuto, con accento grave
    "τίνος", "τινος", "τινός", "τινὸς", # stessa struttura per la seconda occorrenza di τίνος
     "του", "τού", "τοὺ",       # stessa struttura per la seconda occorrenza di τοῦ
    "τίνοιν", "τινοιν", "τινοίν", "τινοὶν", # τίνοιν (originale), senza accento, con accento acuto, con accento grave
    "τίνοιν", "τινοιν", "τινοίν", "τινοὶν", # stessa struttura per la seconda occorrenza di τίνοιν
    "τίνων", "τινων", "τινῶν", "τινῶν", # τίνων (originale), senza accento, con accento acuto, con accento grave
    "τίνων", "τινων", "τινῶν", "τινῶν", # stessa struttura per la seconda occorrenza di τίνων
    
    # Dative
    "τίνι", "τινι", "τινί", "τινὶ",     # τίνι (originale), senza accento, con accento acuto, con accento grave
    "τω", "τώ", "τὼ",           # τῷ (originale), senza accento, con accento acuto, con accento grave
    "τίνι", "τινι", "τινί", "τινὶ",     # stessa struttura per la seconda occorrenza di τίνι
    "τω", "τώ", "τὼ",           # stessa struttura per la seconda occorrenza di τῷ
    "τίνοιν", "τινοιν", "τινοίν", "τινοὶν", # τίνοιν (originale), senza accento, con accento acuto, con accento grave
    "τίνοιν", "τινοιν", "τινοίν", "τινοὶν", # stessa struttura per la seconda occorrenza di τίνοιν
    "τίσι", "τισι", "τίσί", "τίσι", # τίσι(ν) (originale), senza accento, con accento acuto, con accento grave
    "τίσι", "τισι", "τίσί", "τίσι", # stessa struttura per la seconda occorrenza di τίσι(ν)
    "τίσιν", "τισιν", "τίσίν", "τίσιν", # τίσι(ν) (originale), senza accento, con accento acuto, con accento grave
    "τίσιν", "τισιν", "τίσίν", "τίσιν",
    # Accusative
    "τίνα", "τινα", "τινά", "τινὰ",     # τίνα (originale), senza accento, con accento acuto, con accento grave
    "τί", "τι", "τί", "τὶ",           # τί (originale), senza accento, con accento acuto, con accento grave
    "τίνε", "τινε", "τινέ", "τινὲ",     # τίνε (originale), senza accento, con accento acuto, con accento grave
    "τίνε", "τινε", "τινέ", "τινὲ",     # stessa struttura per la seconda occorrenza di τίνε
    "τίνας", "τινας", "τινάς", "τινὰς", # τίνας (originale), senza accento, con accento acuto, con accento grave
    "τίνα", "τινα", "τινά", "τινὰ"      # τίνα (originale), senza accento, con accento acuto, con accento grave
]
  final_list = []
  pos_6c = ['f', 'm']
  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if row['@form'] in greek_words:
            if postag[0] != 'l':
              if len(postag) == 9 and postag[6] in pos_6c and (postag[0] == 'a' or postag[0] =='p'):
              #modify the postag
                row['@postag'] = postag[:6] + 'c' + postag[7:9] 
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']]) 
                #update the dataframe .at è come dire append ma per i dataframe
              df.at[index, '@postag'] = row['@postag']
              modified = True

    #append the dataframe whether modified or not
    final_list.append(df)

  return final_list

#cambia in c solo se prima posizione ha A o P e solo per femminile e maschile, non neutro

In [183]:
anomaliestis_dataframes = [replace_tis_anomalies(lis) for lis in dataframes]

['τις', 'τις', 'p-s---mn-', 'p-s---cn-', 'SBJ']
['τις', 'τις', 'p-s---mn-', 'p-s---cn-', 'SBJ']
['τινες', 'τις', 'p-p---mn-', 'p-p---cn-', 'SBJ']
['τινας', 'τις', 'p-p---ma-', 'p-p---ca-', 'ATR']
['τινα', 'τις', 'p-s---ma-', 'p-s---ca-', 'ATR']
['τις', 'τις', 'p-s---mn-', 'p-s---cn-', 'SBJ']
['τινας', 'τις', 'p-p---ma-', 'p-p---ca-', 'ATR']
['τινα', 'τις', 'p-s---fa-', 'p-s---ca-', 'SBJ']
['τις', 'τις', 'p-s---mn-', 'p-s---cn-', 'SBJ']
['τινα', 'τις', 'p-s---ma-', 'p-s---ca-', 'ATR']
['τινα', 'τις', 'p-s---ma-', 'p-s---ca-', 'ATR']
['τις', 'τις', 'p-s---mn-', 'p-s---cn-', 'SBJ']
['τινα', 'τις', 'p-s---ma-', 'p-s---ca-', 'ATR']
['τις', 'τις', 'p-s---fn-', 'p-s---cn-', 'SBJ']
['τις', 'τις', 'p-s---fn-', 'p-s---cn-', 'SBJ']
['τις', 'τις', 'p-s---mn-', 'p-s---cn-', 'SBJ']
['τινα', 'τις', 'p-s---ma-', 'p-s---ca-', 'ATR']
['τις', 'τις', 'p-s---mn-', 'p-s---cn-', 'SBJ']
['τις', 'τις', 'p-s---mn-', 'p-s---cn-', 'SBJ']
['τις', 'τις', 'p-s---mn-', 'p-s---cn-', 'SBJ']
['τις', 'τις', 'p-s---mn-', 

In [184]:
def print_ou(df_list):
    
    for i,df in enumerate(df_list):
        for index, row in df.iterrows():
            
            postag = row['@postag']
            if len(postag) == 9 and row['@form'] == 'οὗ':
                if postag[0] == 'p' or postag[0] == 'd' :
                    print('frase', i)
                    print([index, row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']]) 

In [185]:
#salvare la lista di directory
lis_dir = os.listdir('output_pedalion_con_relation')
for j,lis in enumerate(dataframes):
    print('Opera',lis_dir[j])
    print_ou(lis)

Opera aeneas.xml
frase 180
[11, 'οὗ', 'ὅς', 'p-s---ng-', 'p-s---ng-', 'ADV']
frase 257
[13, 'οὗ', 'ὅς', 'p-s---mg-', 'p-s---mg-', 'ADV']
frase 276
[14, 'οὗ', 'ὅς', 'p-s---ng-', 'p-s---ng-', 'ADV']
Opera aesop1.xml
frase 337
[6, 'οὗ', 'ὅς', 'p-s---ng-', 'p-s---ng-', 'ADV']
frase 353
[1, 'οὗ', 'ὅς', 'p-s---ng-', 'p-s---ng-', 'ADV']
frase 432
[10, 'οὗ', 'ὅς', 'p-s---ng-', 'p-s---ng-', 'OBJ']
frase 455
[16, 'οὗ', 'ὅς', 'p-s---mg-', 'p-s---mg-', 'OBJ']
frase 533
[17, 'οὗ', 'ὅς', 'p-s---ng-', 'p-s---ng-', 'ADV']
Opera charb1.xml
Opera chion.xml
frase 22
[22, 'οὗ', 'οὗ', 'd--------', 'd--------', 'ADV']
frase 123
[8, 'οὗ', 'ὅς', 'p-s---ng-', 'p-s---ng-', 'ADV']
Opera crit.xml
frase 19
[7, 'οὗ', 'ὅς', 'p-s---ng-', 'p-s---ng-', 'SBJ']
Opera epictetus.xml
frase 249
[22, 'οὗ', 'ὅς', 'p-s---mg-', 'p-s---mg-', 'ADV']
frase 250
[20, 'οὗ', 'ὅς', 'p-s---mg-', 'p-s---mg-', 'ADV']
frase 300
[0, 'οὗ', 'ὅς', 'p-s---mg-', 'p-s---mg-', 'ATR']
frase 301
[0, 'οὗ', 'ὅς', 'p-s---mg-', 'p-s---mg-', 'ATR']
frase 

In [186]:
# QUANTI TOTALI TOLTI E CAMBIATI CON - = PEDALION

# Function to check and display anomalies in the postag
def count_personali_anomalies(df_list):
  greek_pronouns_full_combined = [
    # Nominativo
    "ἐγώ", "νώ", "ἡμεῖς", "σύ", "σφώ", "ὑμεῖς", "σφωε", "σφεῖς",
    # Genitivo
    "ἐμοῦ", "μου", "νῷν", "ἡμών", "σοῦ", "σου", "σφῷν", "ὑμῶν", "οὑ", "σφωιν", "σφῶν",
    # Dativo
    "ἐμοῖ", "μοι", "νῷν", "ἡμῖν", "σοῖ", "σοι", "σφῷν", "ὑμῖν", "οἷ", "οἱ", "σφωιν", "σφίσιν", "σφισιν", "σφιν","σφίσι", "σφισι", "σφι",
    # Accusativo
    "ἐμέ", "με", "νώ", "ἡμᾶς", "σέ", "σε", "σφώ", "ὑμᾶς", "ἕ", "ἑ", "σφωε", "σφᾶς", "σφας",

    # Versioni con accento grave
    "ἐγὼ", "νὼ", "ἡμεῖς", "σὺ", "σφὼ", "ὑμεῖς", "σφωε", "σφεῖς",
    "ἐμοῦ", "μου", "νῷν", "ἡμὼν", "σοῦ", "σου", "σφῷν", "ὑμῶν", "οὑ", "σφωιν", "σφῶν",
    "ἐμοῖ", "μοι", "νῷν", "ἡμῖν", "σοῖ", "σοι", "σφῷν", "ὑμῖν", "οἷ", "οἱ", "σφωιν", "σφὶσιν", "σφισιν", "σφιν","σφὶσι", "σφισι", "σφι",
    "ἐμὲ", "με", "νὼ", "ἡμᾶς", "σὲ", "σε", "σφὼ", "ὑμᾶς", "ἕ", "ἑ", "σφωε", "σφᾶς", "σφας",

    # Versioni senza accento
    "ἐγω", "νω", "ἡμεῖς", "συ", "σφω", "ὑμεῖς", "σφωε", "σφεῖς",
    "ἐμοῦ", "μου", "νῷν", "ἡμων", "σοῦ", "σου", "σφῷν", "ὑμῶν", "οὑ", "σφωιν", "σφῶν",
    "ἐμοῖ", "μοι", "νῷν", "ἡμῖν", "σοῖ", "σοι", "σφῷν", "ὑμῖν", "οἷ", "οἱ", "σφωιν", "σφισιν", "σφισιν", "σφιν","σφισι", "σφισι", "σφι",
    "ἐμε", "με", "νω", "ἡμᾶς", "σε", "σε", "σφω", "ὑμᾶς", "ἕ", "ἑ", "σφωε", "σφᾶς", "σφας"
]
  final_list = []
  pos_6c = ['n', 'f', 'm', '-']
  count = 0
  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if row['@form'] in greek_pronouns_full_combined:
            if len(postag) == 9 and postag[6] in pos_6c and postag[0]=='p':
              if row['@lemma'] != 'ὅς':
                count+=1

  return count

In [187]:
count_personali = sum([count_personali_anomalies(lis) for lis in dataframes])
print(f'count_personali_an:{count_personali}')

count_personali_an:125


In [188]:
#HO CANCELLATO OU VA RICONTROLLATO A MANO PERCHE' UGUALE AL RELATIVO
#Function to check and display anomalies in the postag
def replace_personali_anomalies(df_list):
  greek_pronouns_full_combined = [
    # Nominativo
    "ἐγώ", "νώ", "ἡμεῖς", "σύ", "σφώ", "ὑμεῖς", "σφωε", "σφεῖς",
    # Genitivo
    "ἐμοῦ", "μου", "νῷν", "ἡμών", "σοῦ", "σου", "σφῷν", "ὑμῶν", "οὑ", "σφωιν", "σφῶν",
    # Dativo
    "ἐμοῖ", "μοι", "νῷν", "ἡμῖν", "σοῖ", "σοι", "σφῷν", "ὑμῖν", "οἷ", "οἱ", "σφωιν", "σφίσιν", "σφισιν", "σφιν","σφίσι", "σφισι", "σφι",
    # Accusativo
    "ἐμέ", "με", "νώ", "ἡμᾶς", "σέ", "σε", "σφώ", "ὑμᾶς", "ἕ", "ἑ", "σφωε", "σφᾶς", "σφας",

    # Versioni con accento grave
    "ἐγὼ", "νὼ", "ἡμεῖς", "σὺ", "σφὼ", "ὑμεῖς", "σφωε", "σφεῖς",
    "ἐμοῦ", "μου", "νῷν", "ἡμὼν", "σοῦ", "σου", "σφῷν", "ὑμῶν", "οὑ", "σφωιν", "σφῶν",
    "ἐμοῖ", "μοι", "νῷν", "ἡμῖν", "σοῖ", "σοι", "σφῷν", "ὑμῖν", "οἷ", "οἱ", "σφωιν", "σφὶσιν", "σφισιν", "σφιν","σφὶσι", "σφισι", "σφι",
    "ἐμὲ", "με", "νὼ", "ἡμᾶς", "σὲ", "σε", "σφὼ", "ὑμᾶς", "ἕ", "ἑ", "σφωε", "σφᾶς", "σφας",

    # Versioni senza accento
    "ἐγω", "νω", "ἡμεῖς", "συ", "σφω", "ὑμεῖς", "σφωε", "σφεῖς",
    "ἐμοῦ", "μου", "νῷν", "ἡμων", "σοῦ", "σου", "σφῷν", "ὑμῶν", "οὑ", "σφωιν", "σφῶν",
    "ἐμοῖ", "μοι", "νῷν", "ἡμῖν", "σοῖ", "σοι", "σφῷν", "ὑμῖν", "οἷ", "οἱ", "σφωιν", "σφισιν", "σφισιν", "σφιν","σφισι", "σφισι", "σφι",
    "ἐμε", "με", "νω", "ἡμᾶς", "σε", "σε", "σφω", "ὑμᾶς", "ἕ", "ἑ", "σφωε", "σφᾶς", "σφας"
]
  final_list = []
  pos_6c = ['n', 'f', 'm', '-']
  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if row['@form'] in greek_pronouns_full_combined:
            if len(postag) == 9 and postag[6] in pos_6c and postag[0]=='p':
              if row['@lemma'] != 'ὅς':
              #modify the postag
                row['@postag'] = postag[:6] + 'c' + postag[7:9] 
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']]) 
                #update the dataframe .at è come dire append ma per i dataframe
                df.at[index, '@postag'] = row['@postag']
                modified = True

    #append the dataframe whether modified or not
    final_list.append(df)

  return final_list

#cambia in c solo se prima posizione ha P e solo per femminile e maschile, e neutro

In [189]:
anomaliespersonali_dataframes = [replace_personali_anomalies(lis) for lis in dataframes]

['σφῶν', 'σφεῖς', 'p-p----g-', 'p-p---cg-', 'OBJ']
['σοι', 'σύ', 'p2s----d-', 'p2s---cd-', 'OBJ']
['ἡμᾶς', 'ἐγώ', 'p-p----a-', 'p-p---ca-', 'ADV']
['ἡμᾶς', 'ἐγώ', 'p-p----a-', 'p-p---ca-', 'ADV']
['ἡμᾶς', 'ἐγώ', 'p-p----a-', 'p-p---ca-', 'ADV']
['ἡμεῖς', 'ἐγώ', 'p-p----n-', 'p-p---cn-', 'SBJ']
['ἡμεῖς', 'ἐγώ', 'p-p----n-', 'p-p---cn-', 'SBJ']
['ἡμᾶς', 'ἐγώ', 'p-p----a-', 'p-p---ca-', 'ADV']
['ἡμῖν', 'ἐγώ', 'p-p----d-', 'p-p---cd-', 'OBJ']
['ἡμῖν', 'ἐγώ', 'p-p----d-', 'p-p---cd-', 'OBJ']
['ἡμᾶς', 'ἐγώ', 'p-p----a-', 'p-p---ca-', 'OBJ']
['ἡμᾶς', 'ἐγώ', 'p-p----a-', 'p-p---ca-', 'ADV']
['ἡμᾶς', 'ἐγώ', 'p-p----a-', 'p-p---ca-', 'SBJ']
['ἡμῖν', 'ἐγώ', 'p-p----d-', 'p-p---cd-', 'ATR']
['ἡμῖν', 'ἐγώ', 'p-p----d-', 'p-p---cd-', 'ADV']
['ἡμᾶς', 'ἐγώ', 'p-p----a-', 'p-p---ca-', 'OBJ']
['ἡμῖν', 'ἐγώ', 'p-p----d-', 'p-p---cd-', 'OBJ']
['ἡμᾶς', 'ἐγώ', 'p-p----a-', 'p-p---ca-', 'OBJ']
['ὑμεῖς', 'σύ', 'p2p----n-', 'p2p---cn-', 'SBJ']
['ὑμῶν', 'σύ', 'p2p----g-', 'p2p---cg-', 'OBJ']
['ἡμεῖς', 'ἐγώ', 'p

In [190]:
# QUANTI TOTALI TOLTI E CAMBIATI CON - = PEDALION

# Function to check and display anomalies in the postag
def count_personali2_anomalies(df_list):
    greek_pronouns2 = [    # Nominativo
     "σύ", "σφώ", "ὑμεῖς", 
    # Genitivo
     "σοῦ", "σου", "σφῷν", "ὑμῶν", 
    # Dativo
   "σοῖ", "σοι", "σφῷν", "ὑμῖν",   "σέ", "σε", "σφώ", "ὑμᾶς", 

     "σὺ", "σφὼ", "ὑμεῖς",  "σοῦ", "σου", "σφῷν", "ὑμῶν",  
      "σοῖ", "σοι", "σφῷν", "ὑμῖν", 
    "σὲ", "σε", "σφὼ", "ὑμᾶς", 

  "συ", "σφω", "ὑμεῖς", 
    "σοῦ", "σου", "σφῷν", "ὑμῶν", 
     "σοῖ", "σοι", "σφῷν", "ὑμῖν", "σε", "σε", "σφω", "ὑμᾶς"]
    final_list = []
    count = 0
    for df in df_list:
      modified = False #track if the dataframe has been modified

      for index, row in df.iterrows():
        postag = row['@postag']
        if row['@form'] in greek_pronouns2:
            if len(postag) == 9 and postag[1] == '-' and postag[0] == 'p':
                count+=1

    return count

In [191]:
count_personali2 = sum([count_personali2_anomalies(lis) for lis in dataframes])
print(f'count_pers2:{count_personali2}')

count_pers2:9


In [192]:
def replace_PERSONA2personali_anomalies(df_list):
  greek_pronouns2 = [    # Nominativo
     "σύ", "σφώ", "ὑμεῖς", 
    # Genitivo
     "σοῦ", "σου", "σφῷν", "ὑμῶν", 
    # Dativo
   "σοῖ", "σοι", "σφῷν", "ὑμῖν",   "σέ", "σε", "σφώ", "ὑμᾶς", 

     "σὺ", "σφὼ", "ὑμεῖς",  "σοῦ", "σου", "σφῷν", "ὑμῶν",  
      "σοῖ", "σοι", "σφῷν", "ὑμῖν", 
    "σὲ", "σε", "σφὼ", "ὑμᾶς", 

  "συ", "σφω", "ὑμεῖς", 
    "σοῦ", "σου", "σφῷν", "ὑμῶν", 
     "σοῖ", "σοι", "σφῷν", "ὑμῖν", "σε", "σε", "σφω", "ὑμᾶς"]
  final_list = []
  
  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if row['@form'] in greek_pronouns2:
            if len(postag) == 9 and postag[1] == '-' and postag[0] == 'p':
              #modify the postag
              row['@postag'] = postag[0] + '2' + postag[2:9] 
              print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']]) 
                #update the dataframe .at è come dire append ma per i dataframe
              df.at[index, '@postag'] = row['@postag']
              modified = True

    #append the dataframe whether modified or not
    final_list.append(df)

  return final_list

#cambia in c solo se prima posizione ha P e solo per femminile e maschile, e neutro

In [193]:
anomalies2personali_dataframes = [replace_PERSONA2personali_anomalies(lis) for lis in dataframes]

['σε', 'σύ', 'p-s---ca-', 'p2s---ca-', 'OBJ']
['ὑμᾶς', 'σύ', 'p-p---ca-', 'p2p---ca-', 'SBJ']
['ὑμᾶς', 'σύ', 'p-p---ca-', 'p2p---ca-', 'SBJ']
['ὑμᾶς', 'σύ', 'p-p---ca-', 'p2p---ca-', 'SBJ']
['ὑμᾶς', 'σύ', 'p-p---ca-', 'p2p---ca-', 'OBJ']
['σοι', 'σύ', 'p-s---cd-', 'p2s---cd-', 'OBJ']
['σοι', 'σύ', 'p-s---cd-', 'p2s---cd-', 'OBJ']
['ὑμεῖς', 'σύ', 'p-p---cn-', 'p2p---cn-', 'SBJ']
['σε', 'σύ', 'p-s---ca-', 'p2s---ca-', 'OBJ']


In [194]:
# QUANTI TOTALI TOLTI E CAMBIATI CON - = PEDALION

# Function to check and display anomalies in the postag
def count_personali1_anomalies(df_list):
  greek_pronouns1 = ["ἐγώ", "νώ", "ἡμεῖς", "ἐμοῦ", "μου", "νῷν", "ἡμών", "ἐμοῖ", "μοι", "νῷν", "ἡμῖν", "ἐμέ", "με",
                     "νώ", "ἡμᾶς", "ἐγὼ", "νὼ", "ἡμεῖς", "ἐμοῦ", "μου", "νῷν", "ἡμὼν", "ἐμοῖ", "μοι", "νῷν", "ἡμῖν",
                     
"ἐμὲ", "με", "νὼ", "ἡμᾶς",  "ἐγω", "νω", "ἡμεῖς", 
    "ἐμοῦ", "μου", "νῷν", "ἡμων", 
    "ἐμοῖ", "μοι", "νῷν", "ἡμῖν", 
    "ἐμε", "με", "νω", "ἡμᾶς"]
  final_list = []
  count = 0
  for df in df_list:
      modified = False #track if the dataframe has been modified

      for index, row in df.iterrows():
        postag = row['@postag']
        if row['@form'] in greek_pronouns1:
            if len(postag) == 9 and postag[1] == '-' and postag[0] == 'p':
                count+=1

  return count

In [195]:
count_personali1 = sum([count_personali1_anomalies(lis) for lis in dataframes])
print(f'count_pers1:{count_personali1}')

count_pers1:55


In [196]:
def replace_PERSONA1personali_anomalies(df_list):
  greek_pronouns1 = ["ἐγώ", "νώ", "ἡμεῖς", "ἐμοῦ", "μου", "νῷν", "ἡμών", "ἐμοῖ", "μοι", "νῷν", "ἡμῖν", "ἐμέ", "με",
                     "νώ", "ἡμᾶς", "ἐγὼ", "νὼ", "ἡμεῖς", "ἐμοῦ", "μου", "νῷν", "ἡμὼν", "ἐμοῖ", "μοι", "νῷν", "ἡμῖν",
                     
"ἐμὲ", "με", "νὼ", "ἡμᾶς",  "ἐγω", "νω", "ἡμεῖς", 
    "ἐμοῦ", "μου", "νῷν", "ἡμων", 
    "ἐμοῖ", "μοι", "νῷν", "ἡμῖν", 
    "ἐμε", "με", "νω", "ἡμᾶς"]
  final_list = []
  
  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if row['@form'] in greek_pronouns1:
            if len(postag) == 9 and postag[1] == '-' and postag[0] == 'p':
              #modify the postag
              row['@postag'] = postag[0] + '1' + postag[2:9] 
              print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']]) 
                #update the dataframe .at è come dire append ma per i dataframe
              df.at[index, '@postag'] = row['@postag']
              modified = True

    #append the dataframe whether modified or not
    final_list.append(df)

  return final_list

#cambia in c solo se prima posizione ha P e solo per femminile e maschile, e neutro

In [197]:
anomalies1personali_dataframes = [replace_PERSONA1personali_anomalies(lis) for lis in dataframes]

['ἡμᾶς', 'ἐγώ', 'p-p---ca-', 'p1p---ca-', 'ADV']
['ἡμᾶς', 'ἐγώ', 'p-p---ca-', 'p1p---ca-', 'ADV']
['ἡμᾶς', 'ἐγώ', 'p-p---ca-', 'p1p---ca-', 'ADV']
['ἡμεῖς', 'ἐγώ', 'p-p---cn-', 'p1p---cn-', 'SBJ']
['ἡμεῖς', 'ἐγώ', 'p-p---cn-', 'p1p---cn-', 'SBJ']
['ἡμᾶς', 'ἐγώ', 'p-p---ca-', 'p1p---ca-', 'ADV']
['ἡμῖν', 'ἐγώ', 'p-p---cd-', 'p1p---cd-', 'OBJ']
['ἡμῖν', 'ἐγώ', 'p-p---cd-', 'p1p---cd-', 'OBJ']
['ἡμᾶς', 'ἐγώ', 'p-p---ca-', 'p1p---ca-', 'OBJ']
['ἡμᾶς', 'ἐγώ', 'p-p---ca-', 'p1p---ca-', 'ADV']
['ἡμᾶς', 'ἐγώ', 'p-p---ca-', 'p1p---ca-', 'SBJ']
['ἡμῖν', 'ἐγώ', 'p-p---cd-', 'p1p---cd-', 'ATR']
['ἡμῖν', 'ἐγώ', 'p-p---cd-', 'p1p---cd-', 'ADV']
['ἡμᾶς', 'ἐγώ', 'p-p---ca-', 'p1p---ca-', 'OBJ']
['ἡμῖν', 'ἐγώ', 'p-p---cd-', 'p1p---cd-', 'OBJ']
['ἡμᾶς', 'ἐγώ', 'p-p---ca-', 'p1p---ca-', 'OBJ']
['ἡμεῖς', 'ἐγώ', 'p-p---cn-', 'p1p---cn-', 'SBJ']
['ἡμᾶς', 'ἐγώ', 'p-p---ca-', 'p1p---ca-', 'ADV']
['ἡμεῖς', 'ἐγώ', 'p-p---cn-', 'p1p---cn-', 'SBJ']
['ἡμῖν', 'ἐγώ', 'p-p---cd-', 'p1p---cd-', 'OBJ']
['ἡμεῖς', 'ἐγώ',

In [198]:
# QUANTI TOTALI TOLTI E CAMBIATI CON - = PEDALION

# Function to check and display anomalies in the postag
def count_personali3_anomalies(df_list):
  greek_pronouns3 = [ "σφωε", "σφεῖς",
    # Genitivo
    "οὑ", "σφωιν", "σφῶν",
    # Dativo
     "οἷ", "οἱ", "σφωιν", "σφίσιν", "σφισιν", "σφιν","σφίσι", "σφισι", "σφι",
    # Accusativo
     "ἕ", "ἑ", "σφωε", "σφᾶς", "σφας",

    # Versioni con accento grave
     "σφωε", "σφεῖς",
     "οὑ", "σφωιν", "σφῶν",
     "οἷ", "οἱ", "σφωιν", "σφὶσιν", "σφισιν", "σφιν","σφὶσι", "σφισι", "σφι",
     "ἕ", "ἑ", "σφωε", "σφᾶς", "σφας",

   "σφωε", "σφεῖς",
     "οὑ", "σφωιν", "σφῶν",
     "οἷ", "οἱ", "σφωιν", "σφισιν", "σφισιν", "σφιν","σφισι", "σφισι", "σφι",
    "ἕ", "ἑ", "σφωε", "σφᾶς", "σφας"]
  final_list = []
  count = 0
  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if row['@form'] in greek_pronouns3:
            if len(postag) == 9 and postag[1] == '-' and postag[0] == 'p':
              if row['@lemma'] != 'ὅς':
                    count+=1

  return count

In [199]:
count_personali3 = sum([count_personali3_anomalies(lis) for lis in dataframes])
print(f'count_pers3:{count_personali3}')

count_pers3:157


In [200]:
def replace_PERSONA3personali_anomalies(df_list):
  greek_pronouns3 = [ "σφωε", "σφεῖς",
    # Genitivo
    "οὑ", "σφωιν", "σφῶν",
    # Dativo
     "οἷ", "οἱ", "σφωιν", "σφίσιν", "σφισιν", "σφιν","σφίσι", "σφισι", "σφι",
    # Accusativo
     "ἕ", "ἑ", "σφωε", "σφᾶς", "σφας",

    # Versioni con accento grave
     "σφωε", "σφεῖς",
     "οὑ", "σφωιν", "σφῶν",
     "οἷ", "οἱ", "σφωιν", "σφὶσιν", "σφισιν", "σφιν","σφὶσι", "σφισι", "σφι",
     "ἕ", "ἑ", "σφωε", "σφᾶς", "σφας",

   "σφωε", "σφεῖς",
     "οὑ", "σφωιν", "σφῶν",
     "οἷ", "οἱ", "σφωιν", "σφισιν", "σφισιν", "σφιν","σφισι", "σφισι", "σφι",
    "ἕ", "ἑ", "σφωε", "σφᾶς", "σφας"]
  final_list = []
  
  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if row['@form'] in greek_pronouns3:
            if len(postag) == 9 and postag[1] == '-' and postag[0] == 'p':
              if row['@lemma'] != 'ὅς':
              #modify the postag
                  row['@postag'] = postag[0] + '3' + postag[2:9] 
                  print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']]) 
                #update the dataframe .at è come dire append ma per i dataframe
                  df.at[index, '@postag'] = row['@postag']
                  modified = True

    #append the dataframe whether modified or not
    final_list.append(df)

  return final_list

#cambia in c solo se prima posizione ha P e solo per femminile e maschile, e neutro

In [201]:
anomalies3personali_dataframes = [replace_PERSONA3personali_anomalies(lis) for lis in dataframes]

['σφῶν', 'σφεῖς', 'p-p---cg-', 'p3p---cg-', 'OBJ']
['οἱ', 'ἕ', 'p-s---cd-', 'p3s---cd-', 'OBJ']
['οἱ', 'ἕ', 'p-s---cd-', 'p3s---cd-', 'OBJ']
['οἱ', 'ἕ', 'p-s---cd-', 'p3s---cd-', 'OBJ']
['οἱ', 'ἕ', 'p-s---cd-', 'p3s---cd-', 'ADV']
['οἱ', 'ἕ', 'p-s---cd-', 'p3s---cd-', 'OBJ']
['οἱ', 'ἕ', 'p-s---cd-', 'p3s---cd-', 'ATR']
['οἱ', 'ἕ', 'p-s---cd-', 'p3s---cd-', 'PNOM']
['οἱ', 'ἕ', 'p-s---cd-', 'p3s---cd-', 'ATR']
['οἱ', 'ἕ', 'p-s---cd-', 'p3s---cd-', 'ATR']
['οἱ', 'ἕ', 'p-s---cd-', 'p3s---cd-', 'OBJ']
['σφίσιν', 'σφεῖς', 'p-p---cd-', 'p3p---cd-', 'OBJ']
['σφίσι', 'σφεῖς', 'p-p---cd-', 'p3p---cd-', 'ADV']
['οἱ', 'ἕ', 'p-s---cd-', 'p3s---cd-', 'OBJ']
['σφίσι', 'σφεῖς', 'p-p---cd-', 'p3p---cd-', 'ADV']
['οἱ', 'ἕ', 'p-s---cd-', 'p3s---cd-', 'ADV']
['σφῶν', 'σφεῖς', 'p-p---cg-', 'p3p---cg-', 'ATR']
['σφίσιν', 'σφεῖς', 'p-p---cd-', 'p3p---cd-', 'PNOM']
['σφᾶς', 'σφεῖς', 'p-p---ca-', 'p3p---ca-', 'OBJ']
['σφᾶς', 'σφεῖς', 'p-p---ca-', 'p3p---ca-', 'OBJ']
['σφᾶς', 'σφεῖς', 'p-p---ca-', 'p3p---ca-', 

In [202]:
#DA RICONTROLLARE DA QUI DAL BUE

In [203]:
# QUANTI TOTALI TOLTI E CAMBIATI CON - = PEDALION

# Function to check and display anomalies in the postag
def count_bous_anomalies(df_list):
  bous_list = ['βοῶν', 'βόες', 'βοῦν', 'βόας', 'βοῦς', 'βοός', 'βοΐ', 'βόε', 'βοοῖν', 'βουσί', 'βουσίν', 'βοῦ']
  final_list = []
  pos_6c = ['f', 'm', '-']
  count = 0
  count_all = 0
  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if row['@form'] in bous_list and len(postag) == 9 and postag[0] == 'n':
              count_all +=1
              print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']]) 
              if postag[6] in pos_6c:
                  count+=1

  return count, count_all

In [204]:
count_bousanomalies = [sum(x) for x in zip(*[count_bous_anomalies(lis) for lis in dataframes])]
print(f'count_bousC:{count_bousanomalies[0]}')
print(f'count_all_bous:{count_bousanomalies[1]}')

['βοῶν', 'βοῦς', 'n-p---cg-', 'n-p---cg-', 'OBJ']
['βοῶν', 'βοῦς', 'n-p---cg-', 'n-p---cg-', 'OBJ']
['βόες', 'βοῦς', 'n-p---cn-', 'n-p---cn-', 'SBJ']
['βόες', 'βοῦς', 'n-p---cn-', 'n-p---cn-', 'SBJ']
['βοῦν', 'βοῦς', 'n-s---ca-', 'n-s---ca-', 'OBJ']
['βόας', 'βοῦς', 'n-p---ca-', 'n-p---ca-', 'OBJ']
['βοῦς', 'βοῦς', 'n-s---cn-', 'n-s---cn-', 'SBJ']
['βοῦς', 'βοῦς', 'n-p---ca-', 'n-p---ca-', 'OBJ']
['βοῶν', 'βοῦς', 'n-p---cg-', 'n-p---cg-', 'OBJ']
['βόες', 'βοῦς', 'n-p---mn-', 'n-p---mn-', 'SBJ_CO']
['βόας', 'βοῦς', 'n-p---fa-', 'n-p---fa-', 'OBJ']
['βοῶν', 'βοῦς', 'n-p---cg-', 'n-p---cg-', 'ATR']
['βοῦν', 'βοῦς', 'n-s---ca-', 'n-s---ca-', 'OBJ']
['βοῶν', 'βοῦς', 'n-p---mg-', 'n-p---mg-', 'ADV']
['βοῦν', 'βοῦς', 'n-s---fa-', 'n-s---fa-', 'OBJ']
['βοῦν', 'βοῦς', 'n-s---ca-', 'n-s---ca-', 'OBJ_CO']
['βοῦν', 'βοῦς', 'n-s---ca-', 'n-s---ca-', 'OBJ']
['βοῦν', 'βοῦς', 'n-s---ca-', 'n-s---ca-', 'OBJ']
['βοῦν', 'βοῦς', 'n-s---ca-', 'n-s---ca-', 'OBJ']
['βοῶν', 'βοῦς', 'n-p---cg-', 'n-p---cg-', '

In [205]:
# Function to check and display anomalies in the postag
def replace_bous_anomalies(df_list):
    
  bous_list = ['βοῶν', 'βόες', 'βοῦν', 'βόας', 'βοῦς', 'βοός', 'βοΐ', 'βόε', 'βοοῖν', 'βουσί', 'βουσίν', 'βοῦ']
  pos_6c = ['f', 'm', '-']
  final_list = []
  for df in df_list:
    modified = False #track if the dataframe has been modified

    for index, row in df.iterrows():
        postag = row['@postag']
        if row['@form'] in bous_list and len(postag) == 9 and postag[0] == 'n' and postag[6] in pos_6c:
              #modify the postag
              row['@postag'] = postag[:6] + 'c' + postag[7:9] 
                #update the dataframe .at è come dire append ma per i dataframe
              print(row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']) 
              df.at[index, '@postag'] = row['@postag']
              
              modified = True

    #append the dataframe whether modified or not
    final_list.append(df)

  return final_list


In [206]:
anomaliesbous_dataframes = [replace_bous_anomalies(lis) for lis in dataframes]

βόες βοῦς n-p---mn- n-p---cn- SBJ_CO
βόας βοῦς n-p---fa- n-p---ca- OBJ
βοῶν βοῦς n-p---mg- n-p---cg- ADV
βοῦν βοῦς n-s---fa- n-s---ca- OBJ


In [207]:
'''count_Ganomalies = [sum(x) for x in zip(*[count_G_anomalies(lis) for lis in dataframes])]
print(f'count_G:{count_Ganomalies[0]}')
print(f'count_G_z:{count_Ganomalies[1]}')'''

"count_Ganomalies = [sum(x) for x in zip(*[count_G_anomalies(lis) for lis in dataframes])]\nprint(f'count_G:{count_Ganomalies[0]}')\nprint(f'count_G_z:{count_Ganomalies[1]}')"

In [208]:
# QUANTI ERANO IN ORIGINE I G E QUANTI NE ABBIAMO RIMOSSI
def count_zero_anomalies(df_list):
    count = 0
    for i, df in enumerate(df_list):
        n0 = df.shape[0]
        n1 = df[df['@form']!='[0]'].shape[0]
        count += (n0-n1)
        df_zero=df[df['@form']=='[0]']
        for index, row in df_zero.iterrows():
            if row['@form'] == '[0]':
                print('frase', i)
                print([index, row['@form'], row['@lemma'], row['@postag'], row['@relation']])


    return count

In [209]:
count_zeroanomalies = sum([count_zero_anomalies(lis) for lis in dataframes])
print(f'count_zeroan:{count_zeroanomalies}')

frase 157
[17, '[0]', '""', '""', 'PRED']
frase 264
[21, '[0]', '""', '""', 'ADV']
frase 455
[22, '[0]', '""', '""', 'ADV']
frase 508
[10, '[0]', '""', '""', 'ATR']
frase 0
[4, '[0]', '""', '""', 'PRED']
frase 4
[17, '[0]', '""', '""', 'PRED']
frase 5
[28, '[0]', '""', '""', 'SBJ_CO']
frase 6
[4, '[0]', '""', '""', 'PRED']
frase 7
[17, '[0]', '""', '""', 'PRED']
frase 9
[41, '[0]', '""', '""', 'ADV_CO']
frase 11
[27, '[0]', '""', '""', 'ADV']
frase 13
[4, '[0]', '""', '""', 'PRED']
frase 17
[24, '[0]', '""', '""', 'PRED']
frase 20
[19, '[0]', '""', '""', 'PRED_CO']
frase 27
[13, '[0]', '""', '""', 'PRED']
frase 30
[34, '[0]', '""', '""', 'ADV_CO']
frase 41
[41, '[0]', '""', '""', 'PRED']
frase 44
[7, '[0]', '""', '""', 'PRED']
frase 47
[13, '[0]', '""', '""', 'PRED']
frase 49
[10, '[0]', '""', '""', 'PRED']
frase 50
[4, '[0]', '""', '""', 'PRED']
frase 54
[22, '[0]', '""', '""', 'PRED']
frase 60
[32, '[0]', '""', '""', 'PRED']
frase 61
[51, '[0]', '""', '""', 'PRED_CO']
frase 69
[4, '[

In [210]:
def remove_zero_anomalies(df_list):
    for i, df in enumerate(df_list):

        df_list[i] = df[df['@form'] != '[0]']

    return df_list

In [211]:
zero_dataframes = [remove_zero_anomalies(lis) for lis in dataframes]

In [212]:
# QUANTI ERANO IN ORIGINE I G E QUANTI NE ABBIAMO RIMOSSI
def count_GG_anomalies(df_list):
    count = 0
    for i, df in enumerate(df_list):
        n0 = df.shape[0]
        n1 = df[df['@form']!='G'].shape[0]
        count += (n0-n1)
        df_GG = df[df['@form']=='G']
        for index, row in df_GG.iterrows():
            if row['@form'] == 'G':
                print('frase', i)
                print([index, row['@form'], row['@lemma'], row['@postag'], row['@relation']])

    return count

In [213]:
count_GGanomalies = sum([count_GG_anomalies(lis) for lis in dataframes])
print(f'count_GG:{count_GGanomalies}')

frase 51
[0, 'G', 'G', 'n-s---mn-', 'SBJ']
frase 70
[17, 'G', 'G', '---------', 'GAP']
frase 71
[5, 'G', 'G', '---------', 'GAP']
frase 72
[6, 'G', 'G', '---------', 'GAP']
frase 82
[3, 'G', 'G', '---------', '_']
frase 102
[2, 'G', 'G', 'a-s---mv-', 'ATR']
frase 152
[8, 'G', 'G', 'n-s---fa-', 'OBJ_CO']
frase 156
[3, 'G', 'G', 'n-s---fa-', 'OBJ_CO']
frase 156
[6, 'G', 'G', 'n-s---mg-', 'ATR']
frase 157
[5, 'G', 'G', '---------', 'GAP']
frase 157
[6, 'G', 'G', '---------', 'GAP']
frase 159
[1, 'G', 'G', '---------', 'ATR']
frase 177
[13, 'G', 'G', 'n-s---ma-', 'OBJ']
frase 214
[12, 'G', 'G', 'v2sria---', 'PRED_CO']
frase 227
[14, 'G', 'G', 'v2spma---', 'GAP']
frase 229
[5, 'G', 'G', 'n-p---na-', 'SBJ']
frase 248
[0, 'G', 'G', 'c--------', 'AuxC']
frase 272
[6, 'G', 'G', '---------', 'GAP']
frase 274
[0, 'G', 'G', '---------', 'GAP']
frase 305
[1, 'G', 'G', 'm--------', 'ATR']
frase 305
[5, 'G', 'G', 'n-s---md-', 'ATR']
frase 308
[1, 'G', 'G', 'v--ana---', 'OBJ']
frase 316
[13, 'G', 'G',

In [214]:
def remove_GG_anomalies(df_list):
    for i, df in enumerate(df_list):

        df_list[i] = df[df['@form'] != 'G']

    return df_list

In [215]:
GG_dataframes = [remove_GG_anomalies(lis) for lis in dataframes]

In [216]:
# QUANTI ERANO IN ORIGINE I G E QUANTI NE ABBIAMO RIMOSSI
def count_GL_anomalies(df_list):
    count = 0
    for i, df in enumerate(df_list):
        n0 = df.shape[0]
        n1 = df[df['@form']!='G_L'].shape[0]
        count += (n0-n1)
        df_GL = df[df['@form']=='G_L']
        for index, row in df_GL.iterrows():
            if row['@form'] == 'G_L':
                print('frase', i)
                print([index, row['@form'], row['@lemma'], row['@postag'], row['@relation']])


    return count

In [217]:
count_GLanomalies = sum([count_GL_anomalies(lis) for lis in dataframes])
print(f'count_GL:{count_GLanomalies}')

frase 160
[0, 'G_L', '_', 'z--------', 'GAP']
frase 167
[0, 'G_L', '_', 'z--------', 'GAP']
frase 175
[0, 'G_L', '_', 'z--------', 'GAP']
frase 183
[0, 'G_L', '_', 'z--------', 'GAP']
count_GL:4


In [218]:
def remove_GL_anomalies(df_list):
    for i, df in enumerate(df_list):

        df_list[i] = df[df['@form'] != 'G_L']

    return df_list

In [219]:
GL_dataframes = [remove_GL_anomalies(lis) for lis in dataframes]

In [220]:
# QUANTI ERANO IN ORIGINE I G E QUANTI NE ABBIAMO RIMOSSI
def count_numsott_anomalies(df_list):
    count = 0
    pattern = re.compile(r'^\[(?:[0-9]|1[0-9]|20)\]$')
    
    for i, df in enumerate(df_list):
        # Filter out rows where '@form' matches the pattern
        df_num = df[df['@form'].str.match(pattern)]
        count+=df_num.shape[0]
        for index, row in df_num.iterrows():
                print('frase', i)
                print([index, row['@form'], row['@lemma'], row['@postag'], row['@relation']])

        
    return count

In [221]:
count_numsottanomalies = sum([count_numsott_anomalies(lis) for lis in dataframes])
print(f'count_numsottintesi:{count_numsottanomalies}')

frase 24
[25, '[1]', '""', '""', 'OBJ']
frase 4
[18, '[1]', '""', '""', 'ADV']
frase 20
[20, '[1]', '""', '""', 'PRED']
frase 30
[35, '[1]', '""', '""', 'PRED']
frase 82
[47, '[1]', '""', '""', 'PRED']
frase 160
[30, '[1]', '""', '""', 'ADV']
frase 168
[17, '[1]', '""', '""', 'PRED']
frase 173
[30, '[1]', '""', '""', 'ADV']
frase 179
[32, '[1]', '""', '""', 'ADV']
frase 190
[79, '[1]', '""', '""', 'PRED']
frase 202
[43, '[1]', '""', '""', 'OBJ']
frase 202
[44, '[2]', '""', '""', 'PRED']
frase 204
[36, '[1]', '""', '""', 'PRED_CO']
frase 216
[25, '[1]', '""', '""', 'ADV']
frase 219
[25, '[1]', '""', '""', 'ADV']
frase 239
[16, '[1]', '""', '""', 'ADV']
frase 7
[35, '[1]', '_', '-', 'ExD']
frase 7
[36, '[2]', '_', '-', 'ADV']
frase 24
[27, '[1]', '_', '_', 'ADV']
frase 129
[7, '[1]', '_', '_', 'COORD']
frase 129
[8, '[2]', '_', '_', 'PRED_CO']
frase 236
[16, '[1]', '_', '_', 'SBJ_CO']
frase 246
[17, '[1]', '_', '_', 'ADV']
frase 255
[20, '[1]', '_', '_', 'ADV']
frase 531
[14, '[1]', '_',

In [222]:
import re

def remove_numsott_anomalies(df_list):
    # Regex pattern to match '[number]' where number is from 0 to 20
    pattern = re.compile(r'^\[(?:[0-9]|1[0-9]|20)\]$')
    
    for i, df in enumerate(df_list):
        # Filter out rows where '@form' matches the pattern
        df_list[i] = df[~df['@form'].str.match(pattern)]

    return df_list

In [223]:
NUMERI_dataframes = [remove_numsott_anomalies(lis) for lis in dataframes]

In [224]:
#POSTAG SBAGLIATI TOTALMENTE
# Function to check and display anomalies in the postag
def replace_postag_anomalies(df_list):
    final_list = []
    for df in df_list:
        modified = False
        for index, row in df.iterrows():
            postag = row['@postag']
            if len(postag) == 2 and row['@form']=='αὐτῶν':
                row['@postag'] = 'p-p---mg-'
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            elif len(postag) == 2 and row['@form'] == 'μηδὲν':
                row['@postag'] = 'p-s---na-'
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            elif len(postag) == 2 and row['@form'] == 'ταύτην':
                row['@postag'] = 'p-s---fa-'
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            elif len(postag) == 2 and row['@form'] == 'γε':
                row['@postag'] = 'd--------'
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            elif len(postag) == 2 and row['@form'] == 'μοι':
                row['@postag'] = 'p1s---cd-'
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])   
            elif row['@form'] == 'τὸ' and row['@postag'] == '---------':
                row['@postag'] = 'l-s---na-'
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])                                    
            elif row['@form'] == 'τίνα' and row['@postag'] == '--s---ma-':
                row['@postag'] = 'p-s---ca-'
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])  
            elif row['@form'] == 'ἑπτακόσια'and row['@postag'] == 'm-p---na':
                row['@postag'] = 'm--------'
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']]) 
            elif len(postag) == 9 and row['@form'] == 'τίς'and row['@postag'] == '--s---mn-': #questo richiede un controllo sul vecchio postag
                row['@postag'] = 'p-s---cn-'
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            elif row['@form'] == 'τιμωρεῖται' and row['@postag'] == '---------': #questo richiede un controllo sul vecchio postag
                row['@postag'] = 'v3spie---'
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']]) 
            elif len(postag) == 9 and row['@form'] == 'ἐστὶν' and row['@postag'] == '---------': 
                row['@postag'] = 'v3spia---'
            elif row['@form'] == 'ἀποδέξησθε' and row['@postag'] == 'v2pasm': 
                row['@postag'] = 'v2pase---'                
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']]) 
            elif row['@form'] == 'ἐστὶν' and row['@postag'] == '---------': 
                row['@postag'] = 'v3spia---' 
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']]) 
            elif row['@form'] == 'ἐστιν' and row['@postag'] == '---------': 
                row['@postag'] = 'v3spia---' 
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']]) 
            elif row['@form'] == 'εἰμι' and row['@postag'] == '---------':
                row['@postag'] = 'v1spia---'                
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            elif row['@form'] == 'εἰμί' and row['@postag'] == '---------':
                row['@postag'] = 'v1spia---'                
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            elif row['@form'] == 'εἰκός' and row['@postag'] == '---------': 
                row['@postag'] = 'v-srpann-'                
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']]) 
            elif row['@form'] == 'ὑβρίζειν' and row['@postag'] == '---------':
                row['@postag'] = 'v--pna---'                
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']]) 
            elif row['@form'] == 'λέγει' and row['@postag'] == '---------':
                row['@postag'] = 'v3spia---'                
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])   
            elif len(postag) == 2 and row['@form'] == 'τοιούτων': 
                row['@postag'] = 'p-p---ng-'                
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']]) 
            elif row['@form'] == 'δεκαεπτὰ' and row['@postag']=='m-_---__-': 
                row['@postag'] = 'm--------'                
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])                                                                                                                                                                                                                   
          #update the dataframe .at è come dire append ma per i dataframe
            df.at[index, '@postag'] = row['@postag']
            modified = True
        final_list.append(df)

    return final_list

In [225]:
postag_dataframes = [replace_postag_anomalies(lis) for lis in dataframes]

['αὐτῶν', '""', '""', 'p-p---mg-', 'OBJ']
['μηδὲν', '""', '""', 'p-s---na-', 'SBJ']
['ταύτην', '""', '""', 'p-s---fa-', '!!!!!!ATR']
['γε', '""', '""', 'd--------', 'AuxZ']
['μοι', '""', '""', 'p1s---cd-', 'OBJ']
['τὸ', 'ὁ', '---------', 'l-s---na-', 'ATR']
['τίνα', 'τίς', '--s---ma-', 'p-s---ca-', 'SBJ']
['ἑπτακόσια', 'ἑπτακόσιοι', 'm-p---na', 'm--------', 'ATR_CO']
['τίς', 'τίς', '--s---mn-', 'p-s---cn-', 'SBJ']
['τιμωρεῖται', '_', '---------', 'v3spie---', 'ADV']
['ἀποδέξησθε', 'ἀποδέχομαι', 'v2pasm', 'v2pase---', 'PRED']
['εἰμί', '_', '---------', 'v1spia---', 'PRED_CO']
['ἐστιν', '_', '---------', 'v3spia---', 'PRED']
['ἐστιν', '_', '---------', 'v3spia---', 'PRED']
['εἰκός', '_', '---------', 'v-srpann-', 'PNOM']
['ὑβρίζειν', '_', '---------', 'v--pna---', 'SBJ']
['εἰκός', '_', '---------', 'v-srpann-', 'PNOM']
['ἐστιν', '_', '---------', 'v3spia---', 'PRED']
['ὑβρίζειν', '_', '---------', 'v--pna---', 'SBJ']
['εἰμι', '_', '---------', 'v1spia---', 'ADV']
['λέγει', '_', '--------

In [226]:
def replace_postag2_anomalies_2func(df_list):
    final_list = []
    for df in df_list:
        modified = False
        for index, row in df.iterrows():
            postag = row['@postag']
            if row['@form'] == 'ταῦτα' and row['@postag']=='-': 
                row['@postag'] = 'p-p---na-'                
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']]) 
            elif row['@form'] == 'ἐπιστήσεται' and row['@postag']=='-':
                row['@postag'] = 'v3sfim---'                
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            elif row['@form'] == 'χρῆσθαι' and row['@postag']=='-':
                row['@postag'] = 'v--pne---'                
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            elif row['@form'] == 'λύρᾳ' and row['@postag']=='-':
                row['@postag'] = 'n-s---fd-'                
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            elif row['@form'] == 'προτρέπειν' and row['@postag']=='-':
                row['@postag'] = 'v--pna---'                
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            elif row['@form'] == 'ποιεῖν' and row['@postag']=='-':
                row['@postag'] = 'v--pna---'                
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            elif row['@form'] == 'ἔστω' and row['@postag']=='-':
                row['@postag'] = 'v3spma---'                
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            elif row['@form'] == 'ἀπεκρίνατο' and row['@postag']=='-':
                row['@postag'] = 'v3saim---'                
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            elif row['@form'] == 'τείνειν' and row['@postag']=='-':
                row['@postag'] = 'v--pna---'                
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            elif row['@form'] == 'πρός' and row['@postag']=='-':
                row['@postag'] = 'r--------'                
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            elif row['@form'] == 'ἄχρις' and row['@postag']=='c':
                row['@postag'] = 'd--------'                
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            elif row['@form'] == 'πέπραχα' and row['@postag']=='---------':
                row['@postag'] = 'v1sria---'                
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            elif row['@form'] == 'λέγει' and row['@postag']=='_--------':
                row['@postag'] = 'v3spia---'                
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            elif row['@form'] == 'λέγει' and row['@postag']=='_':
                row['@postag'] = 'v3spia---'                
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            elif row['@form'] == 'Βουλικὰς' and row['@postag']=='n-s---_n-':
                row['@postag'] = 'n-s---mn-'                
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            elif row['@form'] == 'Αὐξώμιδος' and row['@postag']=='n-s---_g-':
                row['@postag'] = 'n-s---fg-'                
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            elif row['@form'] == 'κέντον' and row['@postag']=='a-s---__-':
                row['@postag'] = 'm--------'               
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
            elif row['@form'] == 'ἀπεκρίνατο' and row['@postag']=='-':
                row['@postag'] = 'v3saim---'                
                print([row['@form'], row['@lemma'], postag, row['@postag'], row['@relation']])
                                                                                                                                                         
            df.at[index, '@postag'] = row['@postag']
            modified = True
        final_list.append(df)

    return final_list


In [227]:
postag2_dataframes = [replace_postag2_anomalies_2func(lis) for lis in dataframes]

['ἄχρις', 'ἄχρι', 'c', 'd--------', 'AuxP']
['πέπραχα', '_', '---------', 'v1sria---', 'PRED']
['λέγει', '_', '_', 'v3spia---', 'PRED']
['Βουλικὰς', 'Βουλικάς', 'n-s---_n-', 'n-s---mn-', 'PNOM']
['Αὐξώμιδος', 'Αὐξῶμις', 'n-s---_g-', 'n-s---fg-', 'ATR']
['Αὐξώμιδος', 'Αὐξῶμις', 'n-s---_g-', 'n-s---fg-', 'ATR']
['κέντον', 'κέντον', 'a-s---__-', 'm--------', 'OCOMP']
['ἐπιστήσεται', '_', '-', 'v3sfim---', 'SBJ_CO']
['χρῆσθαι', '_', '-', 'v--pne---', 'OBJ']
['ἐπιστήσεται', '_', '-', 'v3sfim---', 'SBJ_CO']
['χρῆσθαι', '_', '-', 'v--pne---', 'OBJ']
['λύρᾳ', '_', '-', 'n-s---fd-', 'OBJ']
['λύρᾳ', '_', '-', 'n-s---fd-', 'OBJ']
['ἐπιστήσεται', '_', '-', 'v3sfim---', 'SBJ_CO']
['χρῆσθαι', '_', '-', 'v--pne---', 'OBJ']
['λύρᾳ', '_', '-', 'n-s---fd-', 'OBJ_CO']
['προτρέπειν', '_', '-', 'v--pna---', 'APOS_CO']
['ποιεῖν', '_', '-', 'v--pna---', 'SBJ']
['ἔστω', '_', '-', 'v3spma---', 'ADV']
['ἀπεκρίνατο', '_', '-', 'v3saim---', 'PRED_CO']
['ἀπεκρίνατο', '_', '-', 'v3saim---', 'PRED_CO']
['ἀπεκρίνατο'

In [228]:
# Function to check and display anomalies in the postag
def check_postag_new_anomalies1(df):
    valid_characters = {
        0: "nvadlgpcrmiuyk",  # Part of speech
        1: "123-",         # Person
        2: "spd-",         # Number
        3: "pirltfa-",     # Tense
        4: "isomnp-",      # Mood
        5: "apme-",        # Voice
        6: "mfnc-",         # Gender
        7: "ngdav-",       # Case
        8: "cs-"           # Grade
    }

    anomalies = []
    
    for index, row in df.iterrows():
        postag = row['@postag']
        if len(postag) != 9:  # Check if postag length is not 9
            anomalies.append((row['@form'], postag, row['@lemma'], row['@relation'], "Incorrect length", len(postag)))
        else:
            # Check each character position
            
            for i, char in enumerate(postag):
                if char not in valid_characters[i]:
                    anomalies.append((row['@form'], postag, row['@lemma'], row['@relation'], f"Unexpected character '{char}' at position {i+1}"))

    return anomalies

In [229]:
# Loop through the dataframes and check for anomalies
for j, lis in enumerate(dataframes):
    print(lis_dir[j])
    anomalies_info = {}
    output_lines = []  
    for i, df in enumerate(lis):
        anomalies_out = check_postag_new_anomalies1(df)
        if len(anomalies_out) > 0:
            anomalies_info[f"File {i}"] = anomalies_out #c'è un dizionario che prende come chiave il file e come valore le anomalie
            # Print and collect the output only if anomalies exist
            print(f"File {i}")
            print(list(df['@form']))
            print(anomalies_out)
            
            
            # Save the output to the list
            output_lines.append(f"File {i}\n")
            output_lines.append(f"{list(df['@form'])}\n")
            output_lines.append(f"{anomalies_out}\n")

    # Save the collected output lines to a file serve per mettere le anomalie su un file vuoto. w significa che sto aprendo il file in scrittura.
    output_file_path = "C:/Users/lcolo/Desktop/TESI/CODICI DEFINITIVI DIZ UNICO-2/PEDALION/anomalie_pedalion_prova1corr/corr1_anomalies_output_pedalion_" + str(j) + ".txt"  
    with open(output_file_path, 'w', encoding = 'utf-8') as file:
        file.writelines(output_lines) #mi scrive sul file vuoto le righe che ho printato
    
    print(f"Output saved to {output_file_path}")

aeneas.xml
Output saved to C:/Users/lcolo/Desktop/TESI/CODICI DEFINITIVI DIZ UNICO-2/PEDALION/anomalie_pedalion_prova1corr/corr1_anomalies_output_pedalion_0.txt
aesop1.xml
Output saved to C:/Users/lcolo/Desktop/TESI/CODICI DEFINITIVI DIZ UNICO-2/PEDALION/anomalie_pedalion_prova1corr/corr1_anomalies_output_pedalion_1.txt
charb1.xml
File 77
['οὐ', 'γὰρ', 'οἷόν', 'τε', 'ἦν', 'ἐξάγειν', 'ἤδη', 'τὴν', 'κόρην']
[('τε', 'b--------', 'τε', 'MWE', "Unexpected character 'b' at position 1")]
File 349
['ὁ', 'δὲ', '``', 'οὐκ', 'ἐνταῦθά', 'ἐστιν', '``', 'ἀπεκρίνατο', '``', 'διὰ', 'γὰρ', 'τοὺς', 'τελώνας', 'περιέστημεν', 'τὴν', 'πόλιν', 'ἀπὸ', 'ὀγδοήκοντα', 'δὲ', 'σταδίων', 'τὸ', 'πλοῖον', 'ὁρμεῖ', '``', 'καὶ', 'τὸν', 'τόπον', 'ἔφραζεν']
[('καὶ', 'b--------', 'καί', 'COORD_CO', "Unexpected character 'b' at position 1")]
Output saved to C:/Users/lcolo/Desktop/TESI/CODICI DEFINITIVI DIZ UNICO-2/PEDALION/anomalie_pedalion_prova1corr/corr1_anomalies_output_pedalion_2.txt
chion.xml
Output saved to C:/User

In [230]:
#FUNZIONE PER SALVARE SUL COMPUTER LE TABELLE CON POS TAGGING CORRETTO
import os

dir = 'C:/Users/lcolo/Desktop/TESI/CODICI DEFINITIVI DIZ UNICO-2/PEDALION/output_pedalion_no_anomalies'
list_dir = os.listdir("C:/Users/lcolo/Desktop/TESI/CODICI DEFINITIVI DIZ UNICO-2/PEDALION/output_pedalion_con_relation")
# Loop through your dataframes list (list of lists)
for i, lis in enumerate(dataframes):
    # Create the subdirectory if it doesn't exist
    sub_dir = os.path.join(dir, list_dir[i])
    os.makedirs(sub_dir, exist_ok=True)
    
    # Loop through the individual dataframes in the current list
    for j in range(len(lis)):
        # Construct the full file path for the CSV
        file_path = os.path.join(sub_dir, f'{j}.csv')
        
        # Save the dataframe to the CSV file
        lis[j].to_csv(file_path)